In [1]:
import logging
import os.path
import time
from collections import OrderedDict
import sys

import numpy as np
import torch.nn.functional as F
from torch import optim
import torch as th

from braindecode.models.deep4 import Deep4Net
from braindecode.models.util import to_dense_prediction_model
from braindecode.datasets.bcic_iv_2a import BCICompetition4Set2A
from braindecode.experiments.experiment import Experiment
from braindecode.experiments.monitors import LossMonitor, MisclassMonitor, \
    RuntimeMonitor, CroppedTrialMisclassMonitor
from braindecode.experiments.stopcriteria import MaxEpochs, NoDecrease, Or
from braindecode.datautil.iterators import CropsFromTrialsIterator
from braindecode.models.shallow_fbcsp import ShallowFBCSPNet
from braindecode.datautil.splitters import split_into_two_sets
from braindecode.torch_ext.constraints import MaxNormDefaultConstraint
from braindecode.torch_ext.util import set_random_seeds, np_to_var
from braindecode.mne_ext.signalproc import mne_apply
from braindecode.datautil.signalproc import (bandpass_cnt,
                                             exponential_running_standardize)
from braindecode.datautil.trial_segment import create_signal_target_from_raw_mne
from braindecode.datautil.signal_target import SignalAndTarget
from braindecode.datautil.iterators import BalancedBatchSizeIterator

import warnings
warnings.filterwarnings("ignore")

log = logging.getLogger(__name__)
# logging.basicConfig(filename="./outputlog.csv")

In [2]:
data_folder = '/Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/'
subject_id = 1 
low_cut_hz = 4 
ival = [-500, 4000]
max_epochs = 1600
max_increase_epochs = 160
batch_size = 60
high_cut_hz = 38
factor_new = 1e-3
init_block_size = 1000
valid_set_fraction = 0.2
marker_def = OrderedDict([('Left Hand', [1]), ('Right Hand', [2],),
                        ('Foot', [3]), ('Tongue', [4])])   

In [3]:
def load_subject_data(subject_id):
    train_filename = 'A{:02d}T.gdf'.format(subject_id)
    test_filename = 'A{:02d}E.gdf'.format(subject_id)
    train_filepath = os.path.join(data_folder, train_filename)
    test_filepath = os.path.join(data_folder, test_filename)
    train_label_filepath = train_filepath.replace('.gdf', '.mat')
    test_label_filepath = test_filepath.replace('.gdf', '.mat')

    train_loader = BCICompetition4Set2A(
        train_filepath, labels_filename=train_label_filepath)
    test_loader = BCICompetition4Set2A(
        test_filepath, labels_filename=test_label_filepath)
    train_cnt = train_loader.load()
    test_cnt = test_loader.load()
    
    train_cnt = data_preprocessing(train_cnt)
    test_cnt = data_preprocessing(test_cnt)
    
    train_set = create_signal_target_from_raw_mne(train_cnt, marker_def, ival)
    test_set = create_signal_target_from_raw_mne(test_cnt, marker_def, ival)
    
    return SignalAndTarget(np.concatenate((train_set.X, test_set.X), axis=0),
                           np.concatenate((train_set.y, test_set.y), axis=0))

In [4]:
def data_preprocessing(train_cnt):
    train_cnt = train_cnt.drop_channels(['STI 014', 'EOG-left',
                                         'EOG-central', 'EOG-right'])
    assert len(train_cnt.ch_names) == 22
    # lets convert to millvolt for numerical stability of next operations
    train_cnt = mne_apply(lambda a: a * 1e6, train_cnt)
    train_cnt = mne_apply(
        lambda a: bandpass_cnt(a, low_cut_hz, high_cut_hz, train_cnt.info['sfreq'],
                               filt_order=3,
                               axis=1), train_cnt)
    train_cnt = mne_apply(
        lambda a: exponential_running_standardize(a.T, factor_new=factor_new,
                                                  init_block_size=init_block_size,
                                                  eps=1e-4).T,
        train_cnt)
    return train_cnt

In [5]:
def load_train_data(subjects):
    data = load_subject_data(subjects.pop(0))
    x = data.X
    y = data.y
    for s in subjects:
        data = load_subject_data(s)
        x = np.concatenate((x, data.X), axis=0)
        y = np.concatenate((y, data.y), axis=0)
    return SignalAndTarget(x, y)      

In [6]:
def run_exp(train_data, test_data, low_cut_hz, model, cuda):
    batch_size = 60
    train_set, valid_set = split_into_two_sets(
        train_data, first_set_fraction=1-valid_set_fraction)

    set_random_seeds(seed=20181221, cuda=cuda)

    n_classes = 4
    n_chans = int(train_set.X.shape[1])
    input_time_length = train_set.X.shape[2]
    if model == 'shallow':
        model = ShallowFBCSPNet(n_chans, n_classes, input_time_length=input_time_length,
                            final_conv_length='auto').create_network()
    elif model == 'deep':
        model = Deep4Net(n_chans, n_classes, input_time_length=input_time_length,
                            final_conv_length='auto').create_network()
    if cuda:
        model.cuda()
    log.info("Model: \n{:s}".format(str(model)))

    optimizer = optim.Adam(model.parameters())

    iterator = BalancedBatchSizeIterator(batch_size=batch_size)

    stop_criterion = Or([MaxEpochs(max_epochs),
                         NoDecrease('valid_misclass', max_increase_epochs)])

    monitors = [LossMonitor(), MisclassMonitor(), RuntimeMonitor()]

    model_constraint = MaxNormDefaultConstraint()

    exp = Experiment(model, train_set, valid_set, test_data, iterator=iterator,
                     loss_function=F.nll_loss, optimizer=optimizer,
                     model_constraint=model_constraint,
                     monitors=monitors,
                     stop_criterion=stop_criterion,
                     remember_best_column='valid_misclass',
                     run_after_early_stop=True, cuda=cuda)
    exp.run()
    return exp

In [42]:
out = 1
subjects_list = [i for i in range(1, 10)]
subjects_list.remove(out)
train_data = load_train_data(subjects_list)
test_data = load_subject_data(out)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  2708.672 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 662665  =      0.000 ...  2650.660 secs...
2018-12-22 19:41:37,214 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
2018-12-22 19:41:37,470 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  26

In [7]:
def combine_data_set(data_list):
    data = data_list.pop(0)
    x = data.X
    y = data.y
    for data in data_list:
        x = np.concatenate((x, data.X), axis=0)
        y = np.concatenate((y, data.y), axis=0)
    return SignalAndTarget(x, y)  

In [45]:
data = list(map(load_subject_data, [i for i in range(1, 10)]))

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-22 22:24:40,118 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-22 22:24:40,380 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

In [8]:
def leave_one_out_run(out):
    subjects_list = [i for i in range(1, 10)]
    subjects_list.remove(out)
    train_data = load_train_data(subjects_list)
    test_data = load_subject_data(out)

    logging.basicConfig(format='%(asctime)s %(levelname)s : %(message)s',
                            level=logging.DEBUG, stream=sys.stdout)
    cuda = True
    exp = run_exp(train_data, test_data, low_cut_hz, "shallow", cuda)
    log.info("Last 10 epochs")
    log.info("\n" + str(exp.epochs_df.iloc[-10:]))

###  valid_misclass: 0.203905, test_misclass: 0.29688

In [9]:
leave_one_out_run(1)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  2708.672 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 662665  =      0.000 ...  2650.660 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  2642.116 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 648774 

2018-12-23 09:51:25,619 INFO : test_loss                 0.93723
2018-12-23 09:51:25,619 INFO : train_misclass            0.47206
2018-12-23 09:51:25,620 INFO : valid_misclass            0.48373
2018-12-23 09:51:25,620 INFO : test_misclass             0.38021
2018-12-23 09:51:25,621 INFO : runtime                   3.81948
2018-12-23 09:51:25,621 INFO : 
2018-12-23 09:51:25,626 INFO : New best valid_misclass: 0.483731
2018-12-23 09:51:25,626 INFO : 
2018-12-23 09:51:27,776 INFO : Time only for training updates: 2.15s
2018-12-23 09:51:29,431 INFO : Epoch 5
2018-12-23 09:51:29,431 INFO : train_loss                1.15359
2018-12-23 09:51:29,432 INFO : valid_loss                1.07366
2018-12-23 09:51:29,433 INFO : test_loss                 0.89028
2018-12-23 09:51:29,433 INFO : train_misclass            0.50515
2018-12-23 09:51:29,434 INFO : valid_misclass            0.45987
2018-12-23 09:51:29,434 INFO : test_misclass             0.39931
2018-12-23 09:51:29,435 INFO : runtime          

2018-12-23 09:52:15,506 INFO : Epoch 17
2018-12-23 09:52:15,506 INFO : train_loss                0.91053
2018-12-23 09:52:15,507 INFO : valid_loss                0.92572
2018-12-23 09:52:15,508 INFO : test_loss                 0.78000
2018-12-23 09:52:15,508 INFO : train_misclass            0.35784
2018-12-23 09:52:15,509 INFO : valid_misclass            0.37419
2018-12-23 09:52:15,509 INFO : test_misclass             0.34722
2018-12-23 09:52:15,510 INFO : runtime                   3.82328
2018-12-23 09:52:15,510 INFO : 
2018-12-23 09:52:15,514 INFO : New best valid_misclass: 0.374187
2018-12-23 09:52:15,515 INFO : 
2018-12-23 09:52:17,674 INFO : Time only for training updates: 2.16s
2018-12-23 09:52:19,336 INFO : Epoch 18
2018-12-23 09:52:19,337 INFO : train_loss                0.92148
2018-12-23 09:52:19,338 INFO : valid_loss                0.92212
2018-12-23 09:52:19,338 INFO : test_loss                 0.86602
2018-12-23 09:52:19,338 INFO : train_misclass            0.34536
2018-12

2018-12-23 09:53:05,296 INFO : valid_misclass            0.34273
2018-12-23 09:53:05,296 INFO : test_misclass             0.31944
2018-12-23 09:53:05,297 INFO : runtime                   3.83452
2018-12-23 09:53:05,298 INFO : 
2018-12-23 09:53:05,301 INFO : New best valid_misclass: 0.342733
2018-12-23 09:53:05,302 INFO : 
2018-12-23 09:53:07,466 INFO : Time only for training updates: 2.16s
2018-12-23 09:53:09,139 INFO : Epoch 31
2018-12-23 09:53:09,139 INFO : train_loss                0.86660
2018-12-23 09:53:09,140 INFO : valid_loss                0.94768
2018-12-23 09:53:09,140 INFO : test_loss                 0.73489
2018-12-23 09:53:09,141 INFO : train_misclass            0.35052
2018-12-23 09:53:09,141 INFO : valid_misclass            0.36768
2018-12-23 09:53:09,142 INFO : test_misclass             0.30382
2018-12-23 09:53:09,142 INFO : runtime                   3.83799
2018-12-23 09:53:09,143 INFO : 
2018-12-23 09:53:11,309 INFO : Time only for training updates: 2.17s
2018-12-23 

2018-12-23 09:53:55,180 INFO : 
2018-12-23 09:53:57,343 INFO : Time only for training updates: 2.16s
2018-12-23 09:53:59,009 INFO : Epoch 44
2018-12-23 09:53:59,010 INFO : train_loss                0.70170
2018-12-23 09:53:59,010 INFO : valid_loss                0.86442
2018-12-23 09:53:59,010 INFO : test_loss                 0.68491
2018-12-23 09:53:59,011 INFO : train_misclass            0.22084
2018-12-23 09:53:59,012 INFO : valid_misclass            0.34273
2018-12-23 09:53:59,012 INFO : test_misclass             0.27778
2018-12-23 09:53:59,012 INFO : runtime                   3.83715
2018-12-23 09:53:59,013 INFO : 
2018-12-23 09:54:01,178 INFO : Time only for training updates: 2.16s
2018-12-23 09:54:02,842 INFO : Epoch 45
2018-12-23 09:54:02,843 INFO : train_loss                0.69439
2018-12-23 09:54:02,843 INFO : valid_loss                0.80138
2018-12-23 09:54:02,843 INFO : test_loss                 0.70394
2018-12-23 09:54:02,844 INFO : train_misclass            0.21894
201

...

2018-12-23 10:02:44,434 INFO : valid_loss                0.89301
2018-12-23 10:02:44,434 INFO : test_loss                 0.64230
2018-12-23 10:02:44,435 INFO : train_misclass            0.15247
2018-12-23 10:02:44,436 INFO : valid_misclass            0.36443
2018-12-23 10:02:44,436 INFO : test_misclass             0.23958
2018-12-23 10:02:44,437 INFO : runtime                   3.83818
2018-12-23 10:02:44,438 INFO : 
2018-12-23 10:02:46,604 INFO : Time only for training updates: 2.17s
2018-12-23 10:02:48,270 INFO : Epoch 182
2018-12-23 10:02:48,270 INFO : train_loss                0.56182
2018-12-23 10:02:48,271 INFO : valid_loss                0.90199
2018-12-23 10:02:48,271 INFO : test_loss                 0.69129
2018-12-23 10:02:48,271 INFO : train_misclass            0.15979
2018-12-23 10:02:48,272 INFO : valid_misclass            0.35033
2018-12-23 10:02:48,272 INFO : test_misclass             0.28646
2018-12-23 10:02:48,273 INFO : runtime                   3.83836
2018-12-23 10

2018-12-23 10:03:38,171 INFO : Epoch 195
2018-12-23 10:03:38,172 INFO : train_loss                0.64008
2018-12-23 10:03:38,172 INFO : valid_loss                0.85566
2018-12-23 10:03:38,173 INFO : test_loss                 0.72634
2018-12-23 10:03:38,173 INFO : train_misclass            0.21270
2018-12-23 10:03:38,173 INFO : valid_misclass            0.33731
2018-12-23 10:03:38,174 INFO : test_misclass             0.31250
2018-12-23 10:03:38,174 INFO : runtime                   3.83549
2018-12-23 10:03:38,174 INFO : 
2018-12-23 10:03:40,339 INFO : Time only for training updates: 2.16s
2018-12-23 10:03:42,004 INFO : Epoch 196
2018-12-23 10:03:42,004 INFO : train_loss                0.60587
2018-12-23 10:03:42,005 INFO : valid_loss                0.99867
2018-12-23 10:03:42,005 INFO : test_loss                 0.67269
2018-12-23 10:03:42,006 INFO : train_misclass            0.19045
2018-12-23 10:03:42,006 INFO : valid_misclass            0.41866
2018-12-23 10:03:42,007 INFO : test_m

2018-12-23 10:04:28,076 INFO : 
2018-12-23 10:04:30,241 INFO : Time only for training updates: 2.16s
2018-12-23 10:04:31,909 INFO : Epoch 209
2018-12-23 10:04:31,909 INFO : train_loss                0.57558
2018-12-23 10:04:31,910 INFO : valid_loss                0.89841
2018-12-23 10:04:31,911 INFO : test_loss                 0.75983
2018-12-23 10:04:31,911 INFO : train_misclass            0.16007
2018-12-23 10:04:31,912 INFO : valid_misclass            0.35575
2018-12-23 10:04:31,912 INFO : test_misclass             0.29514
2018-12-23 10:04:31,913 INFO : runtime                   3.83341
2018-12-23 10:04:31,913 INFO : 
2018-12-23 10:04:34,079 INFO : Time only for training updates: 2.16s
2018-12-23 10:04:35,744 INFO : Epoch 210
2018-12-23 10:04:35,744 INFO : train_loss                0.56048
2018-12-23 10:04:35,745 INFO : valid_loss                0.89861
2018-12-23 10:04:35,746 INFO : test_loss                 0.63239
2018-12-23 10:04:35,746 INFO : train_misclass            0.14731
2

2018-12-23 10:05:21,780 INFO : test_misclass             0.27431
2018-12-23 10:05:21,781 INFO : runtime                   3.83480
2018-12-23 10:05:21,781 INFO : 
2018-12-23 10:05:23,946 INFO : Time only for training updates: 2.16s
2018-12-23 10:05:25,611 INFO : Epoch 223
2018-12-23 10:05:25,611 INFO : train_loss                0.59564
2018-12-23 10:05:25,612 INFO : valid_loss                0.80973
2018-12-23 10:05:25,613 INFO : test_loss                 0.81403
2018-12-23 10:05:25,613 INFO : train_misclass            0.19208
2018-12-23 10:05:25,614 INFO : valid_misclass            0.32863
2018-12-23 10:05:25,614 INFO : test_misclass             0.35417
2018-12-23 10:05:25,615 INFO : runtime                   3.83684
2018-12-23 10:05:25,615 INFO : 
2018-12-23 10:05:27,781 INFO : Time only for training updates: 2.17s
2018-12-23 10:05:29,449 INFO : Epoch 224
2018-12-23 10:05:29,449 INFO : train_loss                0.59435
2018-12-23 10:05:29,450 INFO : valid_loss                0.87169
2

2018-12-23 10:06:15,504 INFO : train_misclass            0.16739
2018-12-23 10:06:15,505 INFO : valid_misclass            0.34599
2018-12-23 10:06:15,505 INFO : test_misclass             0.27604
2018-12-23 10:06:15,506 INFO : runtime                   3.84053
2018-12-23 10:06:15,506 INFO : 
2018-12-23 10:06:17,673 INFO : Time only for training updates: 2.17s
2018-12-23 10:06:19,336 INFO : Epoch 237
2018-12-23 10:06:19,337 INFO : train_loss                0.56187
2018-12-23 10:06:19,338 INFO : valid_loss                0.79720
2018-12-23 10:06:19,339 INFO : test_loss                 0.64457
2018-12-23 10:06:19,339 INFO : train_misclass            0.15193
2018-12-23 10:06:19,340 INFO : valid_misclass            0.31670
2018-12-23 10:06:19,340 INFO : test_misclass             0.23958
2018-12-23 10:06:19,340 INFO : runtime                   3.83754
2018-12-23 10:06:19,341 INFO : 
2018-12-23 10:06:21,506 INFO : Time only for training updates: 2.16s
2018-12-23 10:06:23,177 INFO : Epoch 238
2

###  valid_misclass: 0.137744, test_misclass: 0.65451

In [10]:
leave_one_out_run(2)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 10:07:06,113 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 10:07:06,377 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  26

2018-12-23 10:08:28,549 INFO : Epoch 1
2018-12-23 10:08:28,550 INFO : train_loss                1.21543
2018-12-23 10:08:28,550 INFO : valid_loss                1.17148
2018-12-23 10:08:28,551 INFO : test_loss                 1.66812
2018-12-23 10:08:28,551 INFO : train_misclass            0.53337
2018-12-23 10:08:28,552 INFO : valid_misclass            0.53688
2018-12-23 10:08:28,553 INFO : test_misclass             0.73438
2018-12-23 10:08:28,553 INFO : runtime                   3.68696
2018-12-23 10:08:28,554 INFO : 
2018-12-23 10:08:28,558 INFO : New best valid_misclass: 0.536876
2018-12-23 10:08:28,558 INFO : 
2018-12-23 10:08:30,697 INFO : Time only for training updates: 2.14s
2018-12-23 10:08:32,252 INFO : Epoch 2
2018-12-23 10:08:32,253 INFO : train_loss                1.14099
2018-12-23 10:08:32,253 INFO : valid_loss                1.12915
2018-12-23 10:08:32,254 INFO : test_loss                 1.69814
2018-12-23 10:08:32,254 INFO : train_misclass            0.49891
2018-12-2

2018-12-23 10:09:12,976 INFO : 
2018-12-23 10:09:15,121 INFO : Time only for training updates: 2.14s
2018-12-23 10:09:16,677 INFO : Epoch 14
2018-12-23 10:09:16,678 INFO : train_loss                0.74923
2018-12-23 10:09:16,679 INFO : valid_loss                0.92728
2018-12-23 10:09:16,679 INFO : test_loss                 1.48078
2018-12-23 10:09:16,679 INFO : train_misclass            0.25800
2018-12-23 10:09:16,680 INFO : valid_misclass            0.37744
2018-12-23 10:09:16,680 INFO : test_misclass             0.69444
2018-12-23 10:09:16,681 INFO : runtime                   3.70985
2018-12-23 10:09:16,681 INFO : 
2018-12-23 10:09:18,824 INFO : Time only for training updates: 2.14s
2018-12-23 10:09:20,381 INFO : Epoch 15
2018-12-23 10:09:20,381 INFO : train_loss                0.80032
2018-12-23 10:09:20,382 INFO : valid_loss                0.86297
2018-12-23 10:09:20,382 INFO : test_loss                 1.73866
2018-12-23 10:09:20,383 INFO : train_misclass            0.31118
201

2018-12-23 10:10:04,887 INFO : valid_misclass            0.34490
2018-12-23 10:10:04,887 INFO : test_misclass             0.64757
2018-12-23 10:10:04,888 INFO : runtime                   3.70584
2018-12-23 10:10:04,889 INFO : 
2018-12-23 10:10:04,891 INFO : New best valid_misclass: 0.344902
2018-12-23 10:10:04,891 INFO : 
2018-12-23 10:10:07,042 INFO : Time only for training updates: 2.15s
2018-12-23 10:10:08,603 INFO : Epoch 28
2018-12-23 10:10:08,603 INFO : train_loss                0.67136
2018-12-23 10:10:08,604 INFO : valid_loss                0.89096
2018-12-23 10:10:08,605 INFO : test_loss                 1.53963
2018-12-23 10:10:08,606 INFO : train_misclass            0.23630
2018-12-23 10:10:08,606 INFO : valid_misclass            0.35141
2018-12-23 10:10:08,606 INFO : test_misclass             0.67708
2018-12-23 10:10:08,607 INFO : runtime                   3.72247
2018-12-23 10:10:08,607 INFO : 
2018-12-23 10:10:10,757 INFO : Time only for training updates: 2.15s
2018-12-23 

2018-12-23 10:10:56,850 INFO : Epoch 41
2018-12-23 10:10:56,851 INFO : train_loss                0.60566
2018-12-23 10:10:56,852 INFO : valid_loss                0.89644
2018-12-23 10:10:56,852 INFO : test_loss                 1.67885
2018-12-23 10:10:56,853 INFO : train_misclass            0.18855
2018-12-23 10:10:56,854 INFO : valid_misclass            0.36443
2018-12-23 10:10:56,854 INFO : test_misclass             0.68056
2018-12-23 10:10:56,855 INFO : runtime                   3.71451
2018-12-23 10:10:56,855 INFO : 
2018-12-23 10:10:59,002 INFO : Time only for training updates: 2.15s
2018-12-23 10:11:00,563 INFO : Epoch 42
2018-12-23 10:11:00,564 INFO : train_loss                0.57371
2018-12-23 10:11:00,564 INFO : valid_loss                0.86654
2018-12-23 10:11:00,565 INFO : test_loss                 1.54727
2018-12-23 10:11:00,565 INFO : train_misclass            0.16224
2018-12-23 10:11:00,566 INFO : valid_misclass            0.34599
2018-12-23 10:11:00,566 INFO : test_mis

...

2018-12-23 10:18:33,270 INFO : test_misclass             0.63542
2018-12-23 10:18:33,270 INFO : runtime                   3.70972
2018-12-23 10:18:33,271 INFO : 
2018-12-23 10:18:35,418 INFO : Time only for training updates: 2.15s
2018-12-23 10:18:36,975 INFO : Epoch 165
2018-12-23 10:18:36,975 INFO : train_loss                0.48155
2018-12-23 10:18:36,976 INFO : valid_loss                0.78742
2018-12-23 10:18:36,976 INFO : test_loss                 1.47545
2018-12-23 10:18:36,977 INFO : train_misclass            0.12154
2018-12-23 10:18:36,978 INFO : valid_misclass            0.31453
2018-12-23 10:18:36,978 INFO : test_misclass             0.63368
2018-12-23 10:18:36,979 INFO : runtime                   3.70920
2018-12-23 10:18:36,979 INFO : 
2018-12-23 10:18:39,129 INFO : Time only for training updates: 2.15s
2018-12-23 10:18:40,686 INFO : Epoch 166
2018-12-23 10:18:40,687 INFO : train_loss                0.47310
2018-12-23 10:18:40,687 INFO : valid_loss                0.80099
2

2018-12-23 10:19:25,252 INFO : train_misclass            0.14379
2018-12-23 10:19:25,252 INFO : valid_misclass            0.33948
2018-12-23 10:19:25,252 INFO : test_misclass             0.65451
2018-12-23 10:19:25,253 INFO : runtime                   3.71673
2018-12-23 10:19:25,253 INFO : 
2018-12-23 10:19:27,404 INFO : Time only for training updates: 2.15s
2018-12-23 10:19:28,962 INFO : Epoch 179
2018-12-23 10:19:28,963 INFO : train_loss                0.45845
2018-12-23 10:19:28,963 INFO : valid_loss                0.79329
2018-12-23 10:19:28,964 INFO : test_loss                 1.59874
2018-12-23 10:19:28,964 INFO : train_misclass            0.11801
2018-12-23 10:19:28,965 INFO : valid_misclass            0.31562
2018-12-23 10:19:28,965 INFO : test_misclass             0.61285
2018-12-23 10:19:28,966 INFO : runtime                   3.71339
2018-12-23 10:19:28,966 INFO : 
2018-12-23 10:19:31,116 INFO : Time only for training updates: 2.15s
2018-12-23 10:19:32,675 INFO : Epoch 180
2

2018-12-23 10:20:17,223 INFO : valid_loss                0.79876
2018-12-23 10:20:17,223 INFO : test_loss                 1.39371
2018-12-23 10:20:17,224 INFO : train_misclass            0.11259
2018-12-23 10:20:17,224 INFO : valid_misclass            0.32755
2018-12-23 10:20:17,225 INFO : test_misclass             0.61111
2018-12-23 10:20:17,225 INFO : runtime                   3.71000
2018-12-23 10:20:17,226 INFO : 
2018-12-23 10:20:19,373 INFO : Time only for training updates: 2.15s
2018-12-23 10:20:20,930 INFO : Epoch 193
2018-12-23 10:20:20,931 INFO : train_loss                0.45047
2018-12-23 10:20:20,931 INFO : valid_loss                0.77305
2018-12-23 10:20:20,932 INFO : test_loss                 1.57232
2018-12-23 10:20:20,932 INFO : train_misclass            0.10689
2018-12-23 10:20:20,933 INFO : valid_misclass            0.31996
2018-12-23 10:20:20,933 INFO : test_misclass             0.62500
2018-12-23 10:20:20,934 INFO : runtime                   3.71320
2018-12-23 10

2018-12-23 10:21:09,180 INFO : Epoch 206
2018-12-23 10:21:09,181 INFO : train_loss                0.44025
2018-12-23 10:21:09,182 INFO : valid_loss                0.86612
2018-12-23 10:21:09,183 INFO : test_loss                 1.42873
2018-12-23 10:21:09,184 INFO : train_misclass            0.10228
2018-12-23 10:21:09,184 INFO : valid_misclass            0.35033
2018-12-23 10:21:09,185 INFO : test_misclass             0.59549
2018-12-23 10:21:09,185 INFO : runtime                   3.71152
2018-12-23 10:21:09,186 INFO : 
2018-12-23 10:21:11,333 INFO : Time only for training updates: 2.15s
2018-12-23 10:21:12,889 INFO : Epoch 207
2018-12-23 10:21:12,890 INFO : train_loss                0.46629
2018-12-23 10:21:12,891 INFO : valid_loss                0.79874
2018-12-23 10:21:12,891 INFO : test_loss                 1.45466
2018-12-23 10:21:12,892 INFO : train_misclass            0.12534
2018-12-23 10:21:12,892 INFO : valid_misclass            0.31020
2018-12-23 10:21:12,893 INFO : test_m

2018-12-23 10:22:00,095 INFO : valid_misclass            0.13774
2018-12-23 10:22:00,096 INFO : test_misclass             0.65451
2018-12-23 10:22:00,096 INFO : runtime                   4.52662
2018-12-23 10:22:00,097 INFO : 
2018-12-23 10:22:00,100 INFO : New best valid_misclass: 0.137744
2018-12-23 10:22:00,100 INFO : 
2018-12-23 10:22:00,101 INFO : Last 10 epochs
2018-12-23 10:22:00,106 INFO : 
     train_loss  valid_loss  test_loss  train_misclass  valid_misclass  \
119    0.556846    0.548576   1.518551        0.181858        0.208243   
120    0.552608    0.541564   1.801741        0.179470        0.198482   
121    0.549154    0.526276   1.811437        0.179253        0.195228   
122    0.544539    0.493217   1.966771        0.174045        0.178959   
123    0.544028    0.496523   1.863543        0.178602        0.174620   
124    0.524871    0.507919   1.761555        0.166667        0.180043   
125    0.523131    0.515597   1.572521        0.157118        0.197397   
126   

###  valid_misclass: 0.180043, test_misclass: 0.24826

In [11]:
leave_one_out_run(3)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 10:22:09,383 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 10:22:09,647 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 10:23:31,408 INFO : Epoch 1
2018-12-23 10:23:31,409 INFO : train_loss                1.28653
2018-12-23 10:23:31,409 INFO : valid_loss                1.26644
2018-12-23 10:23:31,410 INFO : test_loss                 1.23354
2018-12-23 10:23:31,411 INFO : train_misclass            0.61313
2018-12-23 10:23:31,411 INFO : valid_misclass            0.61931
2018-12-23 10:23:31,411 INFO : test_misclass             0.56597
2018-12-23 10:23:31,412 INFO : runtime                   3.68671
2018-12-23 10:23:31,413 INFO : 
2018-12-23 10:23:31,418 INFO : New best valid_misclass: 0.619306
2018-12-23 10:23:31,418 INFO : 
2018-12-23 10:23:33,553 INFO : Time only for training updates: 2.13s
2018-12-23 10:23:35,103 INFO : Epoch 2
2018-12-23 10:23:35,103 INFO : train_loss                1.25545
2018-12-23 10:23:35,104 INFO : valid_loss                1.25759
2018-12-23 10:23:35,104 INFO : test_loss                 1.16395
2018-12-23 10:23:35,105 INFO : train_misclass            0.58030
2018-12-2

2018-12-23 10:24:15,817 INFO : train_misclass            0.36137
2018-12-23 10:24:15,818 INFO : valid_misclass            0.41757
2018-12-23 10:24:15,819 INFO : test_misclass             0.43750
2018-12-23 10:24:15,819 INFO : runtime                   3.70492
2018-12-23 10:24:15,820 INFO : 
2018-12-23 10:24:17,963 INFO : Time only for training updates: 2.14s
2018-12-23 10:24:19,522 INFO : Epoch 14
2018-12-23 10:24:19,523 INFO : train_loss                0.91583
2018-12-23 10:24:19,523 INFO : valid_loss                1.05840
2018-12-23 10:24:19,524 INFO : test_loss                 0.93171
2018-12-23 10:24:19,524 INFO : train_misclass            0.33776
2018-12-23 10:24:19,525 INFO : valid_misclass            0.44685
2018-12-23 10:24:19,525 INFO : test_misclass             0.39236
2018-12-23 10:24:19,526 INFO : runtime                   3.70183
2018-12-23 10:24:19,526 INFO : 
2018-12-23 10:24:21,668 INFO : Time only for training updates: 2.14s
2018-12-23 10:24:23,224 INFO : Epoch 15
201

2018-12-23 10:25:04,008 INFO : runtime                   3.70773
2018-12-23 10:25:04,009 INFO : 
2018-12-23 10:25:06,154 INFO : Time only for training updates: 2.15s
2018-12-23 10:25:07,711 INFO : Epoch 27
2018-12-23 10:25:07,712 INFO : train_loss                0.80891
2018-12-23 10:25:07,713 INFO : valid_loss                0.91527
2018-12-23 10:25:07,713 INFO : test_loss                 0.87416
2018-12-23 10:25:07,714 INFO : train_misclass            0.28703
2018-12-23 10:25:07,714 INFO : valid_misclass            0.38612
2018-12-23 10:25:07,715 INFO : test_misclass             0.36458
2018-12-23 10:25:07,716 INFO : runtime                   3.71224
2018-12-23 10:25:07,716 INFO : 
2018-12-23 10:25:09,862 INFO : Time only for training updates: 2.14s
2018-12-23 10:25:11,419 INFO : Epoch 28
2018-12-23 10:25:11,420 INFO : train_loss                0.80973
2018-12-23 10:25:11,420 INFO : valid_loss                0.95059
2018-12-23 10:25:11,421 INFO : test_loss                 0.90408
201

2018-12-23 10:25:55,920 INFO : valid_loss                0.99673
2018-12-23 10:25:55,920 INFO : test_loss                 0.84216
2018-12-23 10:25:55,921 INFO : train_misclass            0.25583
2018-12-23 10:25:55,921 INFO : valid_misclass            0.42950
2018-12-23 10:25:55,922 INFO : test_misclass             0.34896
2018-12-23 10:25:55,922 INFO : runtime                   3.71314
2018-12-23 10:25:55,922 INFO : 
2018-12-23 10:25:58,070 INFO : Time only for training updates: 2.15s
2018-12-23 10:25:59,627 INFO : Epoch 41
2018-12-23 10:25:59,627 INFO : train_loss                0.75775
2018-12-23 10:25:59,628 INFO : valid_loss                0.91634
2018-12-23 10:25:59,628 INFO : test_loss                 0.83023
2018-12-23 10:25:59,629 INFO : train_misclass            0.25556
2018-12-23 10:25:59,630 INFO : valid_misclass            0.36659
2018-12-23 10:25:59,630 INFO : test_misclass             0.34375
2018-12-23 10:25:59,631 INFO : runtime                   3.70877
2018-12-23 10:

...

2018-12-23 10:37:48,219 INFO : train_misclass            0.16386
2018-12-23 10:37:48,219 INFO : valid_misclass            0.35900
2018-12-23 10:37:48,220 INFO : test_misclass             0.38542
2018-12-23 10:37:48,220 INFO : runtime                   3.71146
2018-12-23 10:37:48,220 INFO : 
2018-12-23 10:37:50,371 INFO : Time only for training updates: 2.15s
2018-12-23 10:37:51,928 INFO : Epoch 233
2018-12-23 10:37:51,928 INFO : train_loss                0.56000
2018-12-23 10:37:51,929 INFO : valid_loss                0.92298
2018-12-23 10:37:51,930 INFO : test_loss                 0.80095
2018-12-23 10:37:51,930 INFO : train_misclass            0.16251
2018-12-23 10:37:51,931 INFO : valid_misclass            0.37419
2018-12-23 10:37:51,931 INFO : test_misclass             0.31771
2018-12-23 10:37:51,932 INFO : runtime                   3.71334
2018-12-23 10:37:51,932 INFO : 
2018-12-23 10:37:54,079 INFO : Time only for training updates: 2.15s
2018-12-23 10:37:55,640 INFO : Epoch 234
2

2018-12-23 10:38:40,157 INFO : valid_loss                0.84447
2018-12-23 10:38:40,158 INFO : test_loss                 0.90263
2018-12-23 10:38:40,159 INFO : train_misclass            0.15247
2018-12-23 10:38:40,160 INFO : valid_misclass            0.33948
2018-12-23 10:38:40,160 INFO : test_misclass             0.38542
2018-12-23 10:38:40,161 INFO : runtime                   3.71339
2018-12-23 10:38:40,161 INFO : 
2018-12-23 10:38:42,311 INFO : Time only for training updates: 2.15s
2018-12-23 10:38:43,869 INFO : Epoch 247
2018-12-23 10:38:43,869 INFO : train_loss                0.57116
2018-12-23 10:38:43,870 INFO : valid_loss                0.90145
2018-12-23 10:38:43,870 INFO : test_loss                 0.96964
2018-12-23 10:38:43,870 INFO : train_misclass            0.17200
2018-12-23 10:38:43,871 INFO : valid_misclass            0.36117
2018-12-23 10:38:43,871 INFO : test_misclass             0.42882
2018-12-23 10:38:43,872 INFO : runtime                   3.71241
2018-12-23 10

2018-12-23 10:39:32,175 INFO : Epoch 260
2018-12-23 10:39:32,176 INFO : train_loss                0.55750
2018-12-23 10:39:32,176 INFO : valid_loss                0.82706
2018-12-23 10:39:32,176 INFO : test_loss                 0.79064
2018-12-23 10:39:32,177 INFO : train_misclass            0.15925
2018-12-23 10:39:32,177 INFO : valid_misclass            0.31996
2018-12-23 10:39:32,177 INFO : test_misclass             0.31076
2018-12-23 10:39:32,178 INFO : runtime                   3.70924
2018-12-23 10:39:32,179 INFO : 
2018-12-23 10:39:34,327 INFO : Time only for training updates: 2.15s
2018-12-23 10:39:35,885 INFO : Epoch 261
2018-12-23 10:39:35,885 INFO : train_loss                0.55918
2018-12-23 10:39:35,886 INFO : valid_loss                0.89239
2018-12-23 10:39:35,886 INFO : test_loss                 0.80682
2018-12-23 10:39:35,887 INFO : train_misclass            0.14379
2018-12-23 10:39:35,888 INFO : valid_misclass            0.34924
2018-12-23 10:39:35,888 INFO : test_m

2018-12-23 10:40:20,472 INFO : 
2018-12-23 10:40:22,621 INFO : Time only for training updates: 2.15s
2018-12-23 10:40:24,178 INFO : Epoch 274
2018-12-23 10:40:24,179 INFO : train_loss                0.56639
2018-12-23 10:40:24,180 INFO : valid_loss                0.88844
2018-12-23 10:40:24,180 INFO : test_loss                 1.00917
2018-12-23 10:40:24,180 INFO : train_misclass            0.15274
2018-12-23 10:40:24,181 INFO : valid_misclass            0.34924
2018-12-23 10:40:24,181 INFO : test_misclass             0.44618
2018-12-23 10:40:24,182 INFO : runtime                   3.71067
2018-12-23 10:40:24,182 INFO : 
2018-12-23 10:40:26,344 INFO : Time only for training updates: 2.16s
2018-12-23 10:40:27,907 INFO : Epoch 275
2018-12-23 10:40:27,907 INFO : train_loss                0.54773
2018-12-23 10:40:27,908 INFO : valid_loss                0.88201
2018-12-23 10:40:27,908 INFO : test_loss                 0.75197
2018-12-23 10:40:27,909 INFO : train_misclass            0.14731
2

2018-12-23 10:41:12,474 INFO : test_misclass             0.35764
2018-12-23 10:41:12,475 INFO : runtime                   3.71302
2018-12-23 10:41:12,475 INFO : 
2018-12-23 10:41:14,625 INFO : Time only for training updates: 2.15s
2018-12-23 10:41:16,183 INFO : Epoch 288
2018-12-23 10:41:16,184 INFO : train_loss                0.54129
2018-12-23 10:41:16,184 INFO : valid_loss                0.80105
2018-12-23 10:41:16,184 INFO : test_loss                 0.79229
2018-12-23 10:41:16,185 INFO : train_misclass            0.14406
2018-12-23 10:41:16,186 INFO : valid_misclass            0.30586
2018-12-23 10:41:16,187 INFO : test_misclass             0.31771
2018-12-23 10:41:16,187 INFO : runtime                   3.73346
2018-12-23 10:41:16,188 INFO : 
2018-12-23 10:41:18,334 INFO : Time only for training updates: 2.15s
2018-12-23 10:41:19,892 INFO : Epoch 289
2018-12-23 10:41:19,892 INFO : train_loss                0.53505
2018-12-23 10:41:19,893 INFO : valid_loss                0.85324
2

###  valid_misclass: 0.167028, test_misclass: 0.50347

In [12]:
leave_one_out_run(4)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 10:42:02,368 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 10:42:02,624 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 10:43:24,438 INFO : Epoch 1
2018-12-23 10:43:24,439 INFO : train_loss                1.24661
2018-12-23 10:43:24,439 INFO : valid_loss                1.22841
2018-12-23 10:43:24,440 INFO : test_loss                 1.32063
2018-12-23 10:43:24,440 INFO : train_misclass            0.56620
2018-12-23 10:43:24,441 INFO : valid_misclass            0.60521
2018-12-23 10:43:24,442 INFO : test_misclass             0.66319
2018-12-23 10:43:24,442 INFO : runtime                   3.68812
2018-12-23 10:43:24,443 INFO : 
2018-12-23 10:43:24,448 INFO : New best valid_misclass: 0.605206
2018-12-23 10:43:24,449 INFO : 
2018-12-23 10:43:26,586 INFO : Time only for training updates: 2.14s
2018-12-23 10:43:28,152 INFO : Epoch 2
2018-12-23 10:43:28,152 INFO : train_loss                1.20468
2018-12-23 10:43:28,153 INFO : valid_loss                1.21845
2018-12-23 10:43:28,153 INFO : test_loss                 1.44412
2018-12-23 10:43:28,154 INFO : train_misclass            0.53500
2018-12-2

2018-12-23 10:44:08,903 INFO : runtime                   3.72008
2018-12-23 10:44:08,904 INFO : 
2018-12-23 10:44:08,907 INFO : New best valid_misclass: 0.347072
2018-12-23 10:44:08,907 INFO : 
2018-12-23 10:44:11,050 INFO : Time only for training updates: 2.14s
2018-12-23 10:44:12,608 INFO : Epoch 14
2018-12-23 10:44:12,609 INFO : train_loss                0.81356
2018-12-23 10:44:12,609 INFO : valid_loss                0.90856
2018-12-23 10:44:12,610 INFO : test_loss                 1.32976
2018-12-23 10:44:12,611 INFO : train_misclass            0.29463
2018-12-23 10:44:12,611 INFO : valid_misclass            0.38069
2018-12-23 10:44:12,611 INFO : test_misclass             0.60243
2018-12-23 10:44:12,612 INFO : runtime                   3.70611
2018-12-23 10:44:12,612 INFO : 
2018-12-23 10:44:14,756 INFO : Time only for training updates: 2.14s
2018-12-23 10:44:16,316 INFO : Epoch 15
2018-12-23 10:44:16,316 INFO : train_loss                0.84209
2018-12-23 10:44:16,317 INFO : valid

2018-12-23 10:45:00,809 INFO : Epoch 27
2018-12-23 10:45:00,809 INFO : train_loss                0.76601
2018-12-23 10:45:00,810 INFO : valid_loss                0.85469
2018-12-23 10:45:00,810 INFO : test_loss                 1.30148
2018-12-23 10:45:00,810 INFO : train_misclass            0.29002
2018-12-23 10:45:00,811 INFO : valid_misclass            0.33731
2018-12-23 10:45:00,812 INFO : test_misclass             0.56424
2018-12-23 10:45:00,812 INFO : runtime                   3.70957
2018-12-23 10:45:00,812 INFO : 
2018-12-23 10:45:00,817 INFO : New best valid_misclass: 0.337310
2018-12-23 10:45:00,818 INFO : 
2018-12-23 10:45:02,965 INFO : Time only for training updates: 2.15s
2018-12-23 10:45:04,519 INFO : Epoch 28
2018-12-23 10:45:04,520 INFO : train_loss                0.73506
2018-12-23 10:45:04,520 INFO : valid_loss                0.84402
2018-12-23 10:45:04,521 INFO : test_loss                 1.26738
2018-12-23 10:45:04,522 INFO : train_misclass            0.25990
2018-12

2018-12-23 10:45:49,074 INFO : valid_loss                0.88339
2018-12-23 10:45:49,075 INFO : test_loss                 1.27104
2018-12-23 10:45:49,076 INFO : train_misclass            0.23901
2018-12-23 10:45:49,076 INFO : valid_misclass            0.36659
2018-12-23 10:45:49,077 INFO : test_misclass             0.56424
2018-12-23 10:45:49,077 INFO : runtime                   3.71371
2018-12-23 10:45:49,077 INFO : 
2018-12-23 10:45:51,224 INFO : Time only for training updates: 2.15s
2018-12-23 10:45:52,780 INFO : Epoch 41
2018-12-23 10:45:52,781 INFO : train_loss                0.69586
2018-12-23 10:45:52,781 INFO : valid_loss                0.83973
2018-12-23 10:45:52,782 INFO : test_loss                 1.26553
2018-12-23 10:45:52,782 INFO : train_misclass            0.24525
2018-12-23 10:45:52,783 INFO : valid_misclass            0.33189
2018-12-23 10:45:52,783 INFO : test_misclass             0.56250
2018-12-23 10:45:52,784 INFO : runtime                   3.71068
2018-12-23 10:

...

2018-12-23 11:16:28,318 INFO : test_misclass             0.49653
2018-12-23 11:16:28,318 INFO : runtime                   3.71406
2018-12-23 11:16:28,319 INFO : 
2018-12-23 11:16:30,488 INFO : Time only for training updates: 2.17s
2018-12-23 11:16:32,046 INFO : Epoch 536
2018-12-23 11:16:32,047 INFO : train_loss                0.47175
2018-12-23 11:16:32,047 INFO : valid_loss                0.77580
2018-12-23 11:16:32,047 INFO : test_loss                 1.12157
2018-12-23 11:16:32,048 INFO : train_misclass            0.12697
2018-12-23 11:16:32,048 INFO : valid_misclass            0.30803
2018-12-23 11:16:32,049 INFO : test_misclass             0.46528
2018-12-23 11:16:32,050 INFO : runtime                   3.73200
2018-12-23 11:16:32,050 INFO : 
2018-12-23 11:16:34,202 INFO : Time only for training updates: 2.15s
2018-12-23 11:16:35,759 INFO : Epoch 537
2018-12-23 11:16:35,759 INFO : train_loss                0.48102
2018-12-23 11:16:35,760 INFO : valid_loss                0.81449
2

2018-12-23 11:17:20,304 INFO : train_misclass            0.14569
2018-12-23 11:17:20,304 INFO : valid_misclass            0.27983
2018-12-23 11:17:20,305 INFO : test_misclass             0.50521
2018-12-23 11:17:20,305 INFO : runtime                   3.71149
2018-12-23 11:17:20,306 INFO : 
2018-12-23 11:17:22,455 INFO : Time only for training updates: 2.15s
2018-12-23 11:17:24,012 INFO : Epoch 550
2018-12-23 11:17:24,013 INFO : train_loss                0.47926
2018-12-23 11:17:24,014 INFO : valid_loss                0.85632
2018-12-23 11:17:24,014 INFO : test_loss                 1.26478
2018-12-23 11:17:24,015 INFO : train_misclass            0.13131
2018-12-23 11:17:24,015 INFO : valid_misclass            0.33731
2018-12-23 11:17:24,015 INFO : test_misclass             0.54340
2018-12-23 11:17:24,016 INFO : runtime                   3.71161
2018-12-23 11:17:24,017 INFO : 
2018-12-23 11:17:26,170 INFO : Time only for training updates: 2.15s
2018-12-23 11:17:27,726 INFO : Epoch 551
2

2018-12-23 11:18:12,292 INFO : valid_loss                0.81545
2018-12-23 11:18:12,292 INFO : test_loss                 1.07809
2018-12-23 11:18:12,293 INFO : train_misclass            0.09875
2018-12-23 11:18:12,293 INFO : valid_misclass            0.31562
2018-12-23 11:18:12,294 INFO : test_misclass             0.47917
2018-12-23 11:18:12,294 INFO : runtime                   3.71639
2018-12-23 11:18:12,294 INFO : 
2018-12-23 11:18:14,446 INFO : Time only for training updates: 2.15s
2018-12-23 11:18:16,003 INFO : Epoch 564
2018-12-23 11:18:16,004 INFO : train_loss                0.45144
2018-12-23 11:18:16,004 INFO : valid_loss                0.82949
2018-12-23 11:18:16,004 INFO : test_loss                 1.14558
2018-12-23 11:18:16,005 INFO : train_misclass            0.09658
2018-12-23 11:18:16,006 INFO : valid_misclass            0.32430
2018-12-23 11:18:16,006 INFO : test_misclass             0.47396
2018-12-23 11:18:16,006 INFO : runtime                   3.71253
2018-12-23 11

2018-12-23 11:19:04,281 INFO : Epoch 577
2018-12-23 11:19:04,282 INFO : train_loss                0.50876
2018-12-23 11:19:04,282 INFO : valid_loss                0.85229
2018-12-23 11:19:04,283 INFO : test_loss                 1.12161
2018-12-23 11:19:04,284 INFO : train_misclass            0.14921
2018-12-23 11:19:04,284 INFO : valid_misclass            0.31345
2018-12-23 11:19:04,284 INFO : test_misclass             0.49479
2018-12-23 11:19:04,285 INFO : runtime                   3.71371
2018-12-23 11:19:04,285 INFO : 
2018-12-23 11:19:06,433 INFO : Time only for training updates: 2.15s
2018-12-23 11:19:07,997 INFO : Epoch 578
2018-12-23 11:19:07,998 INFO : train_loss                0.47193
2018-12-23 11:19:07,998 INFO : valid_loss                0.78379
2018-12-23 11:19:07,999 INFO : test_loss                 1.16949
2018-12-23 11:19:08,000 INFO : train_misclass            0.11150
2018-12-23 11:19:08,000 INFO : valid_misclass            0.31779
2018-12-23 11:19:08,001 INFO : test_m

2018-12-23 11:19:52,539 INFO : 
2018-12-23 11:19:52,539 INFO : Setup for second stop...
2018-12-23 11:19:52,544 INFO : Train loss to reach 0.51634
2018-12-23 11:19:52,544 INFO : Run until second stop...
2018-12-23 11:19:54,403 INFO : Epoch 431
2018-12-23 11:19:54,403 INFO : train_loss                0.56246
2018-12-23 11:19:54,404 INFO : valid_loss                0.74684
2018-12-23 11:19:54,404 INFO : test_loss                 1.07574
2018-12-23 11:19:54,404 INFO : train_misclass            0.17752
2018-12-23 11:19:54,405 INFO : valid_misclass            0.27440
2018-12-23 11:19:54,405 INFO : test_misclass             0.45312
2018-12-23 11:19:54,406 INFO : runtime                   1.62369
2018-12-23 11:19:54,406 INFO : 
2018-12-23 11:19:54,412 INFO : New best valid_misclass: 0.274403
2018-12-23 11:19:54,413 INFO : 
2018-12-23 11:19:57,106 INFO : Time only for training updates: 2.69s
2018-12-23 11:19:58,943 INFO : Epoch 432
2018-12-23 11:19:58,944 INFO : train_loss                0.581

###  valid_misclass: 0.189805, test_misclass: 0.72222

In [13]:
leave_one_out_run(5)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 11:20:12,777 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 11:20:13,037 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 11:21:35,117 INFO : Epoch 1
2018-12-23 11:21:35,118 INFO : train_loss                1.22057
2018-12-23 11:21:35,118 INFO : valid_loss                1.26660
2018-12-23 11:21:35,119 INFO : test_loss                 1.60624
2018-12-23 11:21:35,119 INFO : train_misclass            0.56728
2018-12-23 11:21:35,120 INFO : valid_misclass            0.62364
2018-12-23 11:21:35,121 INFO : test_misclass             0.75868
2018-12-23 11:21:35,121 INFO : runtime                   3.68226
2018-12-23 11:21:35,121 INFO : 
2018-12-23 11:21:35,126 INFO : New best valid_misclass: 0.623644
2018-12-23 11:21:35,127 INFO : 
2018-12-23 11:21:37,267 INFO : Time only for training updates: 2.14s
2018-12-23 11:21:38,817 INFO : Epoch 2
2018-12-23 11:21:38,817 INFO : train_loss                1.14317
2018-12-23 11:21:38,818 INFO : valid_loss                1.26087
2018-12-23 11:21:38,818 INFO : test_loss                 1.71712
2018-12-23 11:21:38,819 INFO : train_misclass            0.50678
2018-12-2

2018-12-23 11:22:19,570 INFO : valid_misclass            0.37202
2018-12-23 11:22:19,570 INFO : test_misclass             0.75174
2018-12-23 11:22:19,571 INFO : runtime                   3.71026
2018-12-23 11:22:19,571 INFO : 
2018-12-23 11:22:21,717 INFO : Time only for training updates: 2.15s
2018-12-23 11:22:23,273 INFO : Epoch 14
2018-12-23 11:22:23,274 INFO : train_loss                0.76092
2018-12-23 11:22:23,275 INFO : valid_loss                0.91938
2018-12-23 11:22:23,275 INFO : test_loss                 2.38237
2018-12-23 11:22:23,276 INFO : train_misclass            0.28839
2018-12-23 11:22:23,276 INFO : valid_misclass            0.38069
2018-12-23 11:22:23,277 INFO : test_misclass             0.71875
2018-12-23 11:22:23,277 INFO : runtime                   3.70614
2018-12-23 11:22:23,278 INFO : 
2018-12-23 11:22:25,421 INFO : Time only for training updates: 2.14s
2018-12-23 11:22:26,977 INFO : Epoch 15
2018-12-23 11:22:26,979 INFO : train_loss                0.77718
201

2018-12-23 11:23:07,780 INFO : 
2018-12-23 11:23:09,928 INFO : Time only for training updates: 2.15s
2018-12-23 11:23:11,485 INFO : Epoch 27
2018-12-23 11:23:11,486 INFO : train_loss                0.68390
2018-12-23 11:23:11,487 INFO : valid_loss                0.83659
2018-12-23 11:23:11,488 INFO : test_loss                 2.66445
2018-12-23 11:23:11,489 INFO : train_misclass            0.23847
2018-12-23 11:23:11,489 INFO : valid_misclass            0.32863
2018-12-23 11:23:11,490 INFO : test_misclass             0.73090
2018-12-23 11:23:11,490 INFO : runtime                   3.70925
2018-12-23 11:23:11,491 INFO : 
2018-12-23 11:23:11,495 INFO : New best valid_misclass: 0.328633
2018-12-23 11:23:11,496 INFO : 
2018-12-23 11:23:13,645 INFO : Time only for training updates: 2.15s
2018-12-23 11:23:15,202 INFO : Epoch 28
2018-12-23 11:23:15,202 INFO : train_loss                0.67220
2018-12-23 11:23:15,203 INFO : valid_loss                0.89030
2018-12-23 11:23:15,203 INFO : test_

2018-12-23 11:23:59,776 INFO : test_loss                 2.13576
2018-12-23 11:23:59,777 INFO : train_misclass            0.20103
2018-12-23 11:23:59,777 INFO : valid_misclass            0.36768
2018-12-23 11:23:59,778 INFO : test_misclass             0.67361
2018-12-23 11:23:59,779 INFO : runtime                   3.72278
2018-12-23 11:23:59,779 INFO : 
2018-12-23 11:24:01,929 INFO : Time only for training updates: 2.15s
2018-12-23 11:24:03,484 INFO : Epoch 41
2018-12-23 11:24:03,485 INFO : train_loss                0.65343
2018-12-23 11:24:03,485 INFO : valid_loss                0.83503
2018-12-23 11:24:03,486 INFO : test_loss                 2.42950
2018-12-23 11:24:03,486 INFO : train_misclass            0.22002
2018-12-23 11:24:03,487 INFO : valid_misclass            0.32104
2018-12-23 11:24:03,487 INFO : test_misclass             0.67188
2018-12-23 11:24:03,488 INFO : runtime                   3.71406
2018-12-23 11:24:03,489 INFO : 
2018-12-23 11:24:05,641 INFO : Time only for tr

...

2018-12-23 11:33:20,238 INFO : Epoch 191
2018-12-23 11:33:20,239 INFO : train_loss                0.47971
2018-12-23 11:33:20,239 INFO : valid_loss                0.80071
2018-12-23 11:33:20,240 INFO : test_loss                 2.32770
2018-12-23 11:33:20,240 INFO : train_misclass            0.12859
2018-12-23 11:33:20,241 INFO : valid_misclass            0.31887
2018-12-23 11:33:20,242 INFO : test_misclass             0.65972
2018-12-23 11:33:20,242 INFO : runtime                   3.70480
2018-12-23 11:33:20,243 INFO : 
2018-12-23 11:33:22,390 INFO : Time only for training updates: 2.15s
2018-12-23 11:33:23,946 INFO : Epoch 192
2018-12-23 11:33:23,947 INFO : train_loss                0.49479
2018-12-23 11:33:23,948 INFO : valid_loss                0.78125
2018-12-23 11:33:23,948 INFO : test_loss                 2.14445
2018-12-23 11:33:23,949 INFO : train_misclass            0.12642
2018-12-23 11:33:23,949 INFO : valid_misclass            0.32430
2018-12-23 11:33:23,950 INFO : test_m

2018-12-23 11:34:08,457 INFO : 
2018-12-23 11:34:10,605 INFO : Time only for training updates: 2.15s
2018-12-23 11:34:12,163 INFO : Epoch 205
2018-12-23 11:34:12,163 INFO : train_loss                0.52297
2018-12-23 11:34:12,164 INFO : valid_loss                0.80254
2018-12-23 11:34:12,164 INFO : test_loss                 2.11538
2018-12-23 11:34:12,165 INFO : train_misclass            0.15193
2018-12-23 11:34:12,166 INFO : valid_misclass            0.32863
2018-12-23 11:34:12,166 INFO : test_misclass             0.73090
2018-12-23 11:34:12,167 INFO : runtime                   3.70764
2018-12-23 11:34:12,167 INFO : 
2018-12-23 11:34:14,313 INFO : Time only for training updates: 2.15s
2018-12-23 11:34:15,870 INFO : Epoch 206
2018-12-23 11:34:15,871 INFO : train_loss                0.47747
2018-12-23 11:34:15,872 INFO : valid_loss                0.88589
2018-12-23 11:34:15,872 INFO : test_loss                 2.19075
2018-12-23 11:34:15,873 INFO : train_misclass            0.13294
2

2018-12-23 11:35:00,382 INFO : test_misclass             0.67014
2018-12-23 11:35:00,382 INFO : runtime                   3.71050
2018-12-23 11:35:00,382 INFO : 
2018-12-23 11:35:02,530 INFO : Time only for training updates: 2.15s
2018-12-23 11:35:04,089 INFO : Epoch 219
2018-12-23 11:35:04,089 INFO : train_loss                0.49004
2018-12-23 11:35:04,090 INFO : valid_loss                0.73404
2018-12-23 11:35:04,091 INFO : test_loss                 2.19394
2018-12-23 11:35:04,091 INFO : train_misclass            0.13185
2018-12-23 11:35:04,092 INFO : valid_misclass            0.28091
2018-12-23 11:35:04,092 INFO : test_misclass             0.67535
2018-12-23 11:35:04,093 INFO : runtime                   3.71248
2018-12-23 11:35:04,093 INFO : 
2018-12-23 11:35:06,239 INFO : Time only for training updates: 2.15s
2018-12-23 11:35:07,798 INFO : Epoch 220
2018-12-23 11:35:07,798 INFO : train_loss                0.51941
2018-12-23 11:35:07,799 INFO : valid_loss                0.79055
2

2018-12-23 11:35:52,316 INFO : train_misclass            0.12453
2018-12-23 11:35:52,317 INFO : valid_misclass            0.32430
2018-12-23 11:35:52,317 INFO : test_misclass             0.64062
2018-12-23 11:35:52,317 INFO : runtime                   3.70999
2018-12-23 11:35:52,318 INFO : 
2018-12-23 11:35:54,466 INFO : Time only for training updates: 2.15s
2018-12-23 11:35:56,024 INFO : Epoch 233
2018-12-23 11:35:56,025 INFO : train_loss                0.53124
2018-12-23 11:35:56,025 INFO : valid_loss                1.00398
2018-12-23 11:35:56,026 INFO : test_loss                 1.89566
2018-12-23 11:35:56,026 INFO : train_misclass            0.17173
2018-12-23 11:35:56,027 INFO : valid_misclass            0.40347
2018-12-23 11:35:56,027 INFO : test_misclass             0.63542
2018-12-23 11:35:56,028 INFO : runtime                   3.71077
2018-12-23 11:35:56,029 INFO : 
2018-12-23 11:35:58,176 INFO : Time only for training updates: 2.15s
2018-12-23 11:35:59,734 INFO : Epoch 234
2

2018-12-23 11:36:44,260 INFO : valid_loss                0.86439
2018-12-23 11:36:44,260 INFO : test_loss                 1.82950
2018-12-23 11:36:44,261 INFO : train_misclass            0.13538
2018-12-23 11:36:44,261 INFO : valid_misclass            0.33514
2018-12-23 11:36:44,262 INFO : test_misclass             0.66319
2018-12-23 11:36:44,263 INFO : runtime                   3.71010
2018-12-23 11:36:44,263 INFO : 
2018-12-23 11:36:46,408 INFO : Time only for training updates: 2.14s
2018-12-23 11:36:47,965 INFO : Epoch 247
2018-12-23 11:36:47,966 INFO : train_loss                0.48796
2018-12-23 11:36:47,966 INFO : valid_loss                0.85277
2018-12-23 11:36:47,967 INFO : test_loss                 2.03642
2018-12-23 11:36:47,968 INFO : train_misclass            0.12181
2018-12-23 11:36:47,968 INFO : valid_misclass            0.34707
2018-12-23 11:36:47,969 INFO : test_misclass             0.64583
2018-12-23 11:36:47,969 INFO : runtime                   3.70620
2018-12-23 11

###  valid_misclass: 0.156182, test_misclass: 0.61806

In [14]:
leave_one_out_run(6)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 11:37:25,984 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 11:37:26,244 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 11:38:48,247 INFO : Epoch 1
2018-12-23 11:38:48,247 INFO : train_loss                1.22680
2018-12-23 11:38:48,248 INFO : valid_loss                1.22047
2018-12-23 11:38:48,248 INFO : test_loss                 1.52304
2018-12-23 11:38:48,249 INFO : train_misclass            0.57216
2018-12-23 11:38:48,249 INFO : valid_misclass            0.57375
2018-12-23 11:38:48,250 INFO : test_misclass             0.72743
2018-12-23 11:38:48,251 INFO : runtime                   3.67404
2018-12-23 11:38:48,251 INFO : 
2018-12-23 11:38:48,256 INFO : New best valid_misclass: 0.573753
2018-12-23 11:38:48,257 INFO : 
2018-12-23 11:38:50,394 INFO : Time only for training updates: 2.14s
2018-12-23 11:38:51,945 INFO : Epoch 2
2018-12-23 11:38:51,946 INFO : train_loss                1.13595
2018-12-23 11:38:51,946 INFO : valid_loss                1.15886
2018-12-23 11:38:51,947 INFO : test_loss                 1.53272
2018-12-23 11:38:51,947 INFO : train_misclass            0.50434
2018-12-2

2018-12-23 11:39:32,987 INFO : 
2018-12-23 11:39:35,129 INFO : Time only for training updates: 2.14s
2018-12-23 11:39:36,682 INFO : Epoch 14
2018-12-23 11:39:36,682 INFO : train_loss                0.82303
2018-12-23 11:39:36,683 INFO : valid_loss                0.89992
2018-12-23 11:39:36,684 INFO : test_loss                 1.77490
2018-12-23 11:39:36,684 INFO : train_misclass            0.31877
2018-12-23 11:39:36,684 INFO : valid_misclass            0.36009
2018-12-23 11:39:36,685 INFO : test_misclass             0.72743
2018-12-23 11:39:36,685 INFO : runtime                   3.69983
2018-12-23 11:39:36,686 INFO : 
2018-12-23 11:39:36,689 INFO : New best valid_misclass: 0.360087
2018-12-23 11:39:36,689 INFO : 
2018-12-23 11:39:38,837 INFO : Time only for training updates: 2.15s
2018-12-23 11:39:40,393 INFO : Epoch 15
2018-12-23 11:39:40,393 INFO : train_loss                0.86149
2018-12-23 11:39:40,394 INFO : valid_loss                0.95797
2018-12-23 11:39:40,395 INFO : test_

2018-12-23 11:40:25,194 INFO : test_loss                 1.90918
2018-12-23 11:40:25,195 INFO : train_misclass            0.31416
2018-12-23 11:40:25,195 INFO : valid_misclass            0.36876
2018-12-23 11:40:25,196 INFO : test_misclass             0.70660
2018-12-23 11:40:25,196 INFO : runtime                   3.78181
2018-12-23 11:40:25,196 INFO : 
2018-12-23 11:40:27,398 INFO : Time only for training updates: 2.20s
2018-12-23 11:40:29,005 INFO : Epoch 28
2018-12-23 11:40:29,005 INFO : train_loss                0.72646
2018-12-23 11:40:29,006 INFO : valid_loss                0.98509
2018-12-23 11:40:29,006 INFO : test_loss                 2.18251
2018-12-23 11:40:29,006 INFO : train_misclass            0.25583
2018-12-23 11:40:29,007 INFO : valid_misclass            0.34924
2018-12-23 11:40:29,007 INFO : test_misclass             0.74653
2018-12-23 11:40:29,008 INFO : runtime                   3.82842
2018-12-23 11:40:29,008 INFO : 
2018-12-23 11:40:31,187 INFO : Time only for tr

2018-12-23 11:41:15,780 INFO : Time only for training updates: 2.14s
2018-12-23 11:41:17,338 INFO : Epoch 41
2018-12-23 11:41:17,338 INFO : train_loss                0.72061
2018-12-23 11:41:17,339 INFO : valid_loss                0.97515
2018-12-23 11:41:17,339 INFO : test_loss                 1.90543
2018-12-23 11:41:17,340 INFO : train_misclass            0.27727
2018-12-23 11:41:17,340 INFO : valid_misclass            0.40781
2018-12-23 11:41:17,341 INFO : test_misclass             0.68924
2018-12-23 11:41:17,341 INFO : runtime                   3.70493
2018-12-23 11:41:17,342 INFO : 
2018-12-23 11:41:19,486 INFO : Time only for training updates: 2.14s
2018-12-23 11:41:21,047 INFO : Epoch 42
2018-12-23 11:41:21,047 INFO : train_loss                0.66886
2018-12-23 11:41:21,048 INFO : valid_loss                0.87542
2018-12-23 11:41:21,048 INFO : test_loss                 1.81847
2018-12-23 11:41:21,049 INFO : train_misclass            0.23250
2018-12-23 11:41:21,049 INFO : vali

...

2018-12-23 11:55:41,124 INFO : test_misclass             0.64410
2018-12-23 11:55:41,124 INFO : runtime                   3.70400
2018-12-23 11:55:41,125 INFO : 
2018-12-23 11:55:43,271 INFO : Time only for training updates: 2.14s
2018-12-23 11:55:44,826 INFO : Epoch 275
2018-12-23 11:55:44,827 INFO : train_loss                0.47675
2018-12-23 11:55:44,827 INFO : valid_loss                0.86256
2018-12-23 11:55:44,827 INFO : test_loss                 1.82559
2018-12-23 11:55:44,829 INFO : train_misclass            0.13646
2018-12-23 11:55:44,829 INFO : valid_misclass            0.34816
2018-12-23 11:55:44,829 INFO : test_misclass             0.66667
2018-12-23 11:55:44,830 INFO : runtime                   3.70628
2018-12-23 11:55:44,830 INFO : 
2018-12-23 11:55:46,975 INFO : Time only for training updates: 2.14s
2018-12-23 11:55:48,542 INFO : Epoch 276
2018-12-23 11:55:48,543 INFO : train_loss                0.50200
2018-12-23 11:55:48,543 INFO : valid_loss                0.83058
2

2018-12-23 11:56:33,005 INFO : train_misclass            0.11747
2018-12-23 11:56:33,006 INFO : valid_misclass            0.34273
2018-12-23 11:56:33,006 INFO : test_misclass             0.65278
2018-12-23 11:56:33,007 INFO : runtime                   3.71018
2018-12-23 11:56:33,007 INFO : 
2018-12-23 11:56:35,150 INFO : Time only for training updates: 2.14s
2018-12-23 11:56:36,707 INFO : Epoch 289
2018-12-23 11:56:36,708 INFO : train_loss                0.48053
2018-12-23 11:56:36,708 INFO : valid_loss                0.94320
2018-12-23 11:56:36,708 INFO : test_loss                 1.91996
2018-12-23 11:56:36,709 INFO : train_misclass            0.11991
2018-12-23 11:56:36,709 INFO : valid_misclass            0.33731
2018-12-23 11:56:36,710 INFO : test_misclass             0.67882
2018-12-23 11:56:36,710 INFO : runtime                   3.70079
2018-12-23 11:56:36,711 INFO : 
2018-12-23 11:56:38,856 INFO : Time only for training updates: 2.14s
2018-12-23 11:56:40,414 INFO : Epoch 290
2

2018-12-23 11:57:24,880 INFO : valid_loss                0.88856
2018-12-23 11:57:24,880 INFO : test_loss                 1.97947
2018-12-23 11:57:24,880 INFO : train_misclass            0.15355
2018-12-23 11:57:24,881 INFO : valid_misclass            0.35900
2018-12-23 11:57:24,881 INFO : test_misclass             0.66146
2018-12-23 11:57:24,882 INFO : runtime                   3.70335
2018-12-23 11:57:24,883 INFO : 
2018-12-23 11:57:27,028 INFO : Time only for training updates: 2.14s
2018-12-23 11:57:28,586 INFO : Epoch 303
2018-12-23 11:57:28,586 INFO : train_loss                0.48447
2018-12-23 11:57:28,587 INFO : valid_loss                0.82666
2018-12-23 11:57:28,587 INFO : test_loss                 1.71712
2018-12-23 11:57:28,588 INFO : train_misclass            0.12371
2018-12-23 11:57:28,588 INFO : valid_misclass            0.33623
2018-12-23 11:57:28,589 INFO : test_misclass             0.65104
2018-12-23 11:57:28,590 INFO : runtime                   3.70648
2018-12-23 11

2018-12-23 11:58:16,763 INFO : Epoch 316
2018-12-23 11:58:16,763 INFO : train_loss                0.54421
2018-12-23 11:58:16,764 INFO : valid_loss                0.94668
2018-12-23 11:58:16,764 INFO : test_loss                 1.86435
2018-12-23 11:58:16,765 INFO : train_misclass            0.16413
2018-12-23 11:58:16,765 INFO : valid_misclass            0.35358
2018-12-23 11:58:16,765 INFO : test_misclass             0.65799
2018-12-23 11:58:16,766 INFO : runtime                   3.70480
2018-12-23 11:58:16,766 INFO : 
2018-12-23 11:58:18,909 INFO : Time only for training updates: 2.14s
2018-12-23 11:58:20,464 INFO : Epoch 317
2018-12-23 11:58:20,465 INFO : train_loss                0.48110
2018-12-23 11:58:20,465 INFO : valid_loss                0.80795
2018-12-23 11:58:20,466 INFO : test_loss                 1.75052
2018-12-23 11:58:20,467 INFO : train_misclass            0.12073
2018-12-23 11:58:20,467 INFO : valid_misclass            0.32538
2018-12-23 11:58:20,467 INFO : test_m

2018-12-23 11:59:04,928 INFO : 
2018-12-23 11:59:07,072 INFO : Time only for training updates: 2.14s
2018-12-23 11:59:08,629 INFO : Epoch 330
2018-12-23 11:59:08,629 INFO : train_loss                0.45246
2018-12-23 11:59:08,630 INFO : valid_loss                0.83799
2018-12-23 11:59:08,630 INFO : test_loss                 1.82171
2018-12-23 11:59:08,630 INFO : train_misclass            0.10065
2018-12-23 11:59:08,631 INFO : valid_misclass            0.32646
2018-12-23 11:59:08,631 INFO : test_misclass             0.63021
2018-12-23 11:59:08,632 INFO : runtime                   3.70439
2018-12-23 11:59:08,632 INFO : 
2018-12-23 11:59:10,776 INFO : Time only for training updates: 2.14s
2018-12-23 11:59:12,327 INFO : Epoch 331
2018-12-23 11:59:12,328 INFO : train_loss                0.51028
2018-12-23 11:59:12,328 INFO : valid_loss                0.89106
2018-12-23 11:59:12,329 INFO : test_loss                 1.73099
2018-12-23 11:59:12,329 INFO : train_misclass            0.15627
2

###  valid_misclass: 0.172451, test_misclass: 0.56944

In [15]:
leave_one_out_run(7)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 11:59:43,682 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 11:59:43,941 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 12:01:05,731 INFO : Epoch 1
2018-12-23 12:01:05,731 INFO : train_loss                1.23705
2018-12-23 12:01:05,732 INFO : valid_loss                1.18890
2018-12-23 12:01:05,733 INFO : test_loss                 1.39652
2018-12-23 12:01:05,733 INFO : train_misclass            0.57678
2018-12-23 12:01:05,734 INFO : valid_misclass            0.54989
2018-12-23 12:01:05,734 INFO : test_misclass             0.69618
2018-12-23 12:01:05,735 INFO : runtime                   3.68028
2018-12-23 12:01:05,735 INFO : 
2018-12-23 12:01:05,739 INFO : New best valid_misclass: 0.549892
2018-12-23 12:01:05,740 INFO : 
2018-12-23 12:01:07,878 INFO : Time only for training updates: 2.14s
2018-12-23 12:01:09,428 INFO : Epoch 2
2018-12-23 12:01:09,429 INFO : train_loss                1.10856
2018-12-23 12:01:09,429 INFO : valid_loss                1.06486
2018-12-23 12:01:09,430 INFO : test_loss                 1.40360
2018-12-23 12:01:09,430 INFO : train_misclass            0.47694
2018-12-2

2018-12-23 12:01:50,130 INFO : runtime                   3.69909
2018-12-23 12:01:50,130 INFO : 
2018-12-23 12:01:50,134 INFO : New best valid_misclass: 0.364425
2018-12-23 12:01:50,134 INFO : 
2018-12-23 12:01:52,277 INFO : Time only for training updates: 2.14s
2018-12-23 12:01:53,830 INFO : Epoch 14
2018-12-23 12:01:53,831 INFO : train_loss                0.86847
2018-12-23 12:01:53,831 INFO : valid_loss                0.93430
2018-12-23 12:01:53,832 INFO : test_loss                 1.33236
2018-12-23 12:01:53,833 INFO : train_misclass            0.33912
2018-12-23 12:01:53,833 INFO : valid_misclass            0.36985
2018-12-23 12:01:53,834 INFO : test_misclass             0.59896
2018-12-23 12:01:53,835 INFO : runtime                   3.70501
2018-12-23 12:01:53,835 INFO : 
2018-12-23 12:01:55,977 INFO : Time only for training updates: 2.14s
2018-12-23 12:01:57,529 INFO : Epoch 15
2018-12-23 12:01:57,530 INFO : train_loss                0.84883
2018-12-23 12:01:57,531 INFO : valid

2018-12-23 12:02:42,004 INFO : Epoch 27
2018-12-23 12:02:42,005 INFO : train_loss                0.84007
2018-12-23 12:02:42,005 INFO : valid_loss                0.84486
2018-12-23 12:02:42,006 INFO : test_loss                 1.27595
2018-12-23 12:02:42,006 INFO : train_misclass            0.32366
2018-12-23 12:02:42,007 INFO : valid_misclass            0.35249
2018-12-23 12:02:42,007 INFO : test_misclass             0.57639
2018-12-23 12:02:42,008 INFO : runtime                   3.70564
2018-12-23 12:02:42,008 INFO : 
2018-12-23 12:02:44,156 INFO : Time only for training updates: 2.15s
2018-12-23 12:02:45,715 INFO : Epoch 28
2018-12-23 12:02:45,715 INFO : train_loss                0.79625
2018-12-23 12:02:45,716 INFO : valid_loss                0.86380
2018-12-23 12:02:45,716 INFO : test_loss                 1.18303
2018-12-23 12:02:45,717 INFO : train_misclass            0.29571
2018-12-23 12:02:45,717 INFO : valid_misclass            0.35249
2018-12-23 12:02:45,718 INFO : test_mis

2018-12-23 12:03:30,214 INFO : test_misclass             0.61458
2018-12-23 12:03:30,214 INFO : runtime                   3.70563
2018-12-23 12:03:30,215 INFO : 
2018-12-23 12:03:32,362 INFO : Time only for training updates: 2.15s
2018-12-23 12:03:33,918 INFO : Epoch 41
2018-12-23 12:03:33,918 INFO : train_loss                0.76527
2018-12-23 12:03:33,919 INFO : valid_loss                0.91140
2018-12-23 12:03:33,919 INFO : test_loss                 1.29494
2018-12-23 12:03:33,920 INFO : train_misclass            0.27564
2018-12-23 12:03:33,920 INFO : valid_misclass            0.37852
2018-12-23 12:03:33,921 INFO : test_misclass             0.59201
2018-12-23 12:03:33,921 INFO : runtime                   3.71211
2018-12-23 12:03:33,922 INFO : 
2018-12-23 12:03:36,066 INFO : Time only for training updates: 2.14s
2018-12-23 12:03:37,620 INFO : Epoch 42
2018-12-23 12:03:37,620 INFO : train_loss                0.70496
2018-12-23 12:03:37,621 INFO : valid_loss                0.81499
201

...

2018-12-23 12:24:43,881 INFO : test_misclass             0.54340
2018-12-23 12:24:43,881 INFO : runtime                   3.70712
2018-12-23 12:24:43,882 INFO : 
2018-12-23 12:24:46,030 INFO : Time only for training updates: 2.15s
2018-12-23 12:24:47,589 INFO : Epoch 384
2018-12-23 12:24:47,590 INFO : train_loss                0.49281
2018-12-23 12:24:47,591 INFO : valid_loss                0.80288
2018-12-23 12:24:47,591 INFO : test_loss                 1.16961
2018-12-23 12:24:47,591 INFO : train_misclass            0.11964
2018-12-23 12:24:47,592 INFO : valid_misclass            0.32972
2018-12-23 12:24:47,592 INFO : test_misclass             0.51736
2018-12-23 12:24:47,593 INFO : runtime                   3.71776
2018-12-23 12:24:47,593 INFO : 
2018-12-23 12:24:49,740 INFO : Time only for training updates: 2.15s
2018-12-23 12:24:51,299 INFO : Epoch 385
2018-12-23 12:24:51,299 INFO : train_loss                0.48523
2018-12-23 12:24:51,300 INFO : valid_loss                0.83275
2

2018-12-23 12:25:35,827 INFO : train_misclass            0.14623
2018-12-23 12:25:35,827 INFO : valid_misclass            0.34490
2018-12-23 12:25:35,828 INFO : test_misclass             0.54688
2018-12-23 12:25:35,828 INFO : runtime                   3.70685
2018-12-23 12:25:35,828 INFO : 
2018-12-23 12:25:37,977 INFO : Time only for training updates: 2.15s
2018-12-23 12:25:39,532 INFO : Epoch 398
2018-12-23 12:25:39,533 INFO : train_loss                0.51680
2018-12-23 12:25:39,533 INFO : valid_loss                0.79549
2018-12-23 12:25:39,534 INFO : test_loss                 1.15506
2018-12-23 12:25:39,534 INFO : train_misclass            0.12561
2018-12-23 12:25:39,535 INFO : valid_misclass            0.31236
2018-12-23 12:25:39,536 INFO : test_misclass             0.52083
2018-12-23 12:25:39,536 INFO : runtime                   3.71590
2018-12-23 12:25:39,537 INFO : 
2018-12-23 12:25:41,684 INFO : Time only for training updates: 2.15s
2018-12-23 12:25:43,241 INFO : Epoch 399
2

2018-12-23 12:26:27,776 INFO : valid_loss                0.83452
2018-12-23 12:26:27,776 INFO : test_loss                 1.19372
2018-12-23 12:26:27,778 INFO : train_misclass            0.11639
2018-12-23 12:26:27,778 INFO : valid_misclass            0.33514
2018-12-23 12:26:27,778 INFO : test_misclass             0.50000
2018-12-23 12:26:27,779 INFO : runtime                   3.70785
2018-12-23 12:26:27,779 INFO : 
2018-12-23 12:26:29,925 INFO : Time only for training updates: 2.14s
2018-12-23 12:26:31,482 INFO : Epoch 412
2018-12-23 12:26:31,483 INFO : train_loss                0.59325
2018-12-23 12:26:31,483 INFO : valid_loss                0.80401
2018-12-23 12:26:31,484 INFO : test_loss                 1.27079
2018-12-23 12:26:31,485 INFO : train_misclass            0.19506
2018-12-23 12:26:31,485 INFO : valid_misclass            0.33080
2018-12-23 12:26:31,485 INFO : test_misclass             0.52604
2018-12-23 12:26:31,486 INFO : runtime                   3.70721
2018-12-23 12

2018-12-23 12:27:19,684 INFO : Epoch 425
2018-12-23 12:27:19,684 INFO : train_loss                0.51026
2018-12-23 12:27:19,685 INFO : valid_loss                0.83751
2018-12-23 12:27:19,685 INFO : test_loss                 1.15524
2018-12-23 12:27:19,686 INFO : train_misclass            0.13077
2018-12-23 12:27:19,686 INFO : valid_misclass            0.34707
2018-12-23 12:27:19,687 INFO : test_misclass             0.50868
2018-12-23 12:27:19,688 INFO : runtime                   3.70940
2018-12-23 12:27:19,688 INFO : 
2018-12-23 12:27:21,833 INFO : Time only for training updates: 2.14s
2018-12-23 12:27:23,390 INFO : Epoch 426
2018-12-23 12:27:23,391 INFO : train_loss                0.59674
2018-12-23 12:27:23,391 INFO : valid_loss                0.78382
2018-12-23 12:27:23,392 INFO : test_loss                 1.29298
2018-12-23 12:27:23,392 INFO : train_misclass            0.19995
2018-12-23 12:27:23,393 INFO : valid_misclass            0.31887
2018-12-23 12:27:23,394 INFO : test_m

2018-12-23 12:28:07,913 INFO : 
2018-12-23 12:28:10,062 INFO : Time only for training updates: 2.15s
2018-12-23 12:28:11,618 INFO : Epoch 439
2018-12-23 12:28:11,618 INFO : train_loss                0.51910
2018-12-23 12:28:11,619 INFO : valid_loss                0.85148
2018-12-23 12:28:11,619 INFO : test_loss                 1.29357
2018-12-23 12:28:11,620 INFO : train_misclass            0.14352
2018-12-23 12:28:11,620 INFO : valid_misclass            0.33839
2018-12-23 12:28:11,621 INFO : test_misclass             0.54861
2018-12-23 12:28:11,622 INFO : runtime                   3.70915
2018-12-23 12:28:11,623 INFO : 
2018-12-23 12:28:13,772 INFO : Time only for training updates: 2.15s
2018-12-23 12:28:15,329 INFO : Epoch 440
2018-12-23 12:28:15,329 INFO : train_loss                0.52572
2018-12-23 12:28:15,330 INFO : valid_loss                0.82790
2018-12-23 12:28:15,330 INFO : test_loss                 1.21908
2018-12-23 12:28:15,331 INFO : train_misclass            0.14569
2

###  valid_misclass: 0.164859, test_misclass: 0.27604

In [16]:
leave_one_out_run(8)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 12:28:51,257 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 12:28:51,517 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 12:30:13,673 INFO : Epoch 1
2018-12-23 12:30:13,673 INFO : train_loss                1.24619
2018-12-23 12:30:13,674 INFO : valid_loss                1.26935
2018-12-23 12:30:13,674 INFO : test_loss                 1.30399
2018-12-23 12:30:13,674 INFO : train_misclass            0.58519
2018-12-23 12:30:13,675 INFO : valid_misclass            0.62473
2018-12-23 12:30:13,676 INFO : test_misclass             0.62500
2018-12-23 12:30:13,676 INFO : runtime                   3.68696
2018-12-23 12:30:13,677 INFO : 
2018-12-23 12:30:13,683 INFO : New best valid_misclass: 0.624729
2018-12-23 12:30:13,683 INFO : 
2018-12-23 12:30:15,825 INFO : Time only for training updates: 2.14s
2018-12-23 12:30:17,376 INFO : Epoch 2
2018-12-23 12:30:17,377 INFO : train_loss                1.14913
2018-12-23 12:30:17,378 INFO : valid_loss                1.30442
2018-12-23 12:30:17,378 INFO : test_loss                 1.09972
2018-12-23 12:30:17,379 INFO : train_misclass            0.51818
2018-12-2

2018-12-23 12:30:58,126 INFO : valid_misclass            0.45011
2018-12-23 12:30:58,127 INFO : test_misclass             0.39583
2018-12-23 12:30:58,127 INFO : runtime                   3.70771
2018-12-23 12:30:58,128 INFO : 
2018-12-23 12:30:58,131 INFO : New best valid_misclass: 0.450108
2018-12-23 12:30:58,132 INFO : 
2018-12-23 12:31:00,275 INFO : Time only for training updates: 2.14s
2018-12-23 12:31:01,832 INFO : Epoch 14
2018-12-23 12:31:01,832 INFO : train_loss                0.86733
2018-12-23 12:31:01,833 INFO : valid_loss                1.05053
2018-12-23 12:31:01,834 INFO : test_loss                 0.94858
2018-12-23 12:31:01,834 INFO : train_misclass            0.31823
2018-12-23 12:31:01,835 INFO : valid_misclass            0.46312
2018-12-23 12:31:01,836 INFO : test_misclass             0.37153
2018-12-23 12:31:01,836 INFO : runtime                   3.70699
2018-12-23 12:31:01,836 INFO : 
2018-12-23 12:31:03,980 INFO : Time only for training updates: 2.14s
2018-12-23 

2018-12-23 12:31:46,355 INFO : valid_misclass            0.45011
2018-12-23 12:31:46,355 INFO : test_misclass             0.36458
2018-12-23 12:31:46,356 INFO : runtime                   3.71128
2018-12-23 12:31:46,356 INFO : 
2018-12-23 12:31:48,505 INFO : Time only for training updates: 2.15s
2018-12-23 12:31:50,060 INFO : Epoch 27
2018-12-23 12:31:50,061 INFO : train_loss                0.85504
2018-12-23 12:31:50,061 INFO : valid_loss                1.02550
2018-12-23 12:31:50,062 INFO : test_loss                 0.95136
2018-12-23 12:31:50,063 INFO : train_misclass            0.31905
2018-12-23 12:31:50,064 INFO : valid_misclass            0.44035
2018-12-23 12:31:50,065 INFO : test_misclass             0.38889
2018-12-23 12:31:50,066 INFO : runtime                   3.71227
2018-12-23 12:31:50,067 INFO : 
2018-12-23 12:31:52,215 INFO : Time only for training updates: 2.15s
2018-12-23 12:31:53,773 INFO : Epoch 28
2018-12-23 12:31:53,774 INFO : train_loss                0.77470
201

2018-12-23 12:32:34,595 INFO : test_misclass             0.39062
2018-12-23 12:32:34,596 INFO : runtime                   3.70716
2018-12-23 12:32:34,597 INFO : 
2018-12-23 12:32:36,741 INFO : Time only for training updates: 2.14s
2018-12-23 12:32:38,296 INFO : Epoch 40
2018-12-23 12:32:38,297 INFO : train_loss                0.72709
2018-12-23 12:32:38,297 INFO : valid_loss                1.04701
2018-12-23 12:32:38,298 INFO : test_loss                 0.95753
2018-12-23 12:32:38,298 INFO : train_misclass            0.23549
2018-12-23 12:32:38,298 INFO : valid_misclass            0.47505
2018-12-23 12:32:38,299 INFO : test_misclass             0.42014
2018-12-23 12:32:38,299 INFO : runtime                   3.70938
2018-12-23 12:32:38,300 INFO : 
2018-12-23 12:32:40,448 INFO : Time only for training updates: 2.15s
2018-12-23 12:32:42,005 INFO : Epoch 41
2018-12-23 12:32:42,005 INFO : train_loss                0.80314
2018-12-23 12:32:42,006 INFO : valid_loss                1.11584
201

...

2018-12-23 12:53:47,393 INFO : Epoch 382
2018-12-23 12:53:47,393 INFO : train_loss                0.50830
2018-12-23 12:53:47,394 INFO : valid_loss                0.90260
2018-12-23 12:53:47,394 INFO : test_loss                 0.96847
2018-12-23 12:53:47,395 INFO : train_misclass            0.12914
2018-12-23 12:53:47,395 INFO : valid_misclass            0.37202
2018-12-23 12:53:47,396 INFO : test_misclass             0.43576
2018-12-23 12:53:47,396 INFO : runtime                   3.70819
2018-12-23 12:53:47,397 INFO : 
2018-12-23 12:53:49,546 INFO : Time only for training updates: 2.15s
2018-12-23 12:53:51,104 INFO : Epoch 383
2018-12-23 12:53:51,105 INFO : train_loss                0.52046
2018-12-23 12:53:51,105 INFO : valid_loss                0.93174
2018-12-23 12:53:51,106 INFO : test_loss                 0.80875
2018-12-23 12:53:51,106 INFO : train_misclass            0.13022
2018-12-23 12:53:51,107 INFO : valid_misclass            0.39046
2018-12-23 12:53:51,107 INFO : test_m

2018-12-23 12:54:35,650 INFO : 
2018-12-23 12:54:37,796 INFO : Time only for training updates: 2.15s
2018-12-23 12:54:39,351 INFO : Epoch 396
2018-12-23 12:54:39,352 INFO : train_loss                0.51959
2018-12-23 12:54:39,353 INFO : valid_loss                0.85655
2018-12-23 12:54:39,354 INFO : test_loss                 0.83618
2018-12-23 12:54:39,355 INFO : train_misclass            0.12995
2018-12-23 12:54:39,355 INFO : valid_misclass            0.34490
2018-12-23 12:54:39,355 INFO : test_misclass             0.35069
2018-12-23 12:54:39,356 INFO : runtime                   3.70654
2018-12-23 12:54:39,356 INFO : 
2018-12-23 12:54:41,504 INFO : Time only for training updates: 2.15s
2018-12-23 12:54:43,060 INFO : Epoch 397
2018-12-23 12:54:43,061 INFO : train_loss                0.56009
2018-12-23 12:54:43,062 INFO : valid_loss                0.95374
2018-12-23 12:54:43,063 INFO : test_loss                 1.01410
2018-12-23 12:54:43,063 INFO : train_misclass            0.16359
2

2018-12-23 12:55:28,210 INFO : test_misclass             0.42188
2018-12-23 12:55:28,210 INFO : runtime                   3.71138
2018-12-23 12:55:28,211 INFO : 
2018-12-23 12:55:30,359 INFO : Time only for training updates: 2.15s
2018-12-23 12:55:31,927 INFO : Epoch 410
2018-12-23 12:55:31,927 INFO : train_loss                0.56461
2018-12-23 12:55:31,928 INFO : valid_loss                0.94422
2018-12-23 12:55:31,928 INFO : test_loss                 1.03420
2018-12-23 12:55:31,929 INFO : train_misclass            0.16359
2018-12-23 12:55:31,929 INFO : valid_misclass            0.39262
2018-12-23 12:55:31,929 INFO : test_misclass             0.46528
2018-12-23 12:55:31,930 INFO : runtime                   3.71224
2018-12-23 12:55:31,931 INFO : 
2018-12-23 12:55:34,082 INFO : Time only for training updates: 2.15s
2018-12-23 12:55:35,639 INFO : Epoch 411
2018-12-23 12:55:35,640 INFO : train_loss                0.49922
2018-12-23 12:55:35,641 INFO : valid_loss                0.93329
2

2018-12-23 12:56:20,190 INFO : train_misclass            0.13945
2018-12-23 12:56:20,190 INFO : valid_misclass            0.37310
2018-12-23 12:56:20,191 INFO : test_misclass             0.42882
2018-12-23 12:56:20,191 INFO : runtime                   3.70891
2018-12-23 12:56:20,192 INFO : 
2018-12-23 12:56:22,341 INFO : Time only for training updates: 2.15s
2018-12-23 12:56:23,898 INFO : Epoch 424
2018-12-23 12:56:23,898 INFO : train_loss                0.53135
2018-12-23 12:56:23,899 INFO : valid_loss                0.87780
2018-12-23 12:56:23,899 INFO : test_loss                 0.94573
2018-12-23 12:56:23,900 INFO : train_misclass            0.14813
2018-12-23 12:56:23,900 INFO : valid_misclass            0.34924
2018-12-23 12:56:23,901 INFO : test_misclass             0.41319
2018-12-23 12:56:23,902 INFO : runtime                   3.71322
2018-12-23 12:56:23,903 INFO : 
2018-12-23 12:56:26,052 INFO : Time only for training updates: 2.15s
2018-12-23 12:56:27,610 INFO : Epoch 425
2

2018-12-23 12:57:10,718 INFO : train_misclass            0.18511
2018-12-23 12:57:10,718 INFO : valid_misclass            0.16486
2018-12-23 12:57:10,719 INFO : test_misclass             0.27604
2018-12-23 12:57:10,719 INFO : runtime                   4.53357
2018-12-23 12:57:10,720 INFO : 
2018-12-23 12:57:10,723 INFO : New best valid_misclass: 0.164859
2018-12-23 12:57:10,723 INFO : 
2018-12-23 12:57:10,724 INFO : Last 10 epochs
2018-12-23 12:57:10,729 INFO : 
     train_loss  valid_loss  test_loss  train_misclass  valid_misclass  \
267    0.530127    0.922273   0.954251        0.136462        0.367679   
268    0.539715    0.950836   0.850137        0.161150        0.380694   
269    0.522520    0.956233   0.998966        0.126424        0.381779   
270    0.555614    0.826245   0.794746        0.183397        0.328633   
271    0.609764    0.826245   0.794746        0.212457        0.328633   
272    0.608024    0.630521   0.866088        0.184028        0.215835   
273    0.645353

###  valid_misclass: 0.182213, test_misclass: 0.33854

In [17]:
leave_one_out_run(9)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 12:57:20,045 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 12:57:20,308 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 12:58:42,574 INFO : Epoch 1
2018-12-23 12:58:42,575 INFO : train_loss                1.24620
2018-12-23 12:58:42,575 INFO : valid_loss                1.33938
2018-12-23 12:58:42,576 INFO : test_loss                 1.19190
2018-12-23 12:58:42,576 INFO : train_misclass            0.58519
2018-12-23 12:58:42,577 INFO : valid_misclass            0.65618
2018-12-23 12:58:42,577 INFO : test_misclass             0.57465
2018-12-23 12:58:42,578 INFO : runtime                   3.68541
2018-12-23 12:58:42,578 INFO : 
2018-12-23 12:58:42,584 INFO : New best valid_misclass: 0.656182
2018-12-23 12:58:42,584 INFO : 
2018-12-23 12:58:44,723 INFO : Time only for training updates: 2.14s
2018-12-23 12:58:46,276 INFO : Epoch 2
2018-12-23 12:58:46,277 INFO : train_loss                1.14913
2018-12-23 12:58:46,277 INFO : valid_loss                1.21170
2018-12-23 12:58:46,278 INFO : test_loss                 1.24811
2018-12-23 12:58:46,278 INFO : train_misclass            0.51818
2018-12-2

2018-12-23 12:59:27,029 INFO : valid_misclass            0.43926
2018-12-23 12:59:27,029 INFO : test_misclass             0.40972
2018-12-23 12:59:27,030 INFO : runtime                   3.70846
2018-12-23 12:59:27,030 INFO : 
2018-12-23 12:59:29,177 INFO : Time only for training updates: 2.15s
2018-12-23 12:59:30,742 INFO : Epoch 14
2018-12-23 12:59:30,743 INFO : train_loss                0.86733
2018-12-23 12:59:30,743 INFO : valid_loss                1.03338
2018-12-23 12:59:30,743 INFO : test_loss                 0.97613
2018-12-23 12:59:30,744 INFO : train_misclass            0.31796
2018-12-23 12:59:30,745 INFO : valid_misclass            0.42842
2018-12-23 12:59:30,745 INFO : test_misclass             0.42708
2018-12-23 12:59:30,746 INFO : runtime                   3.70762
2018-12-23 12:59:30,747 INFO : 
2018-12-23 12:59:32,895 INFO : Time only for training updates: 2.15s
2018-12-23 12:59:34,451 INFO : Epoch 15
2018-12-23 12:59:34,451 INFO : train_loss                0.87058
201

2018-12-23 13:00:15,280 INFO : 
2018-12-23 13:00:15,283 INFO : New best valid_misclass: 0.405640
2018-12-23 13:00:15,284 INFO : 
2018-12-23 13:00:17,433 INFO : Time only for training updates: 2.15s
2018-12-23 13:00:18,990 INFO : Epoch 27
2018-12-23 13:00:18,991 INFO : train_loss                0.85534
2018-12-23 13:00:18,991 INFO : valid_loss                1.00794
2018-12-23 13:00:18,992 INFO : test_loss                 0.97992
2018-12-23 13:00:18,992 INFO : train_misclass            0.31877
2018-12-23 13:00:18,992 INFO : valid_misclass            0.42842
2018-12-23 13:00:18,993 INFO : test_misclass             0.40799
2018-12-23 13:00:18,993 INFO : runtime                   3.71939
2018-12-23 13:00:18,994 INFO : 
2018-12-23 13:00:21,142 INFO : Time only for training updates: 2.15s
2018-12-23 13:00:22,701 INFO : Epoch 28
2018-12-23 13:00:22,701 INFO : train_loss                0.77457
2018-12-23 13:00:22,702 INFO : valid_loss                0.99508
2018-12-23 13:00:22,702 INFO : test_

2018-12-23 13:01:07,265 INFO : Epoch 40
2018-12-23 13:01:07,265 INFO : train_loss                0.72708
2018-12-23 13:01:07,267 INFO : valid_loss                0.99990
2018-12-23 13:01:07,267 INFO : test_loss                 1.03281
2018-12-23 13:01:07,268 INFO : train_misclass            0.23549
2018-12-23 13:01:07,268 INFO : valid_misclass            0.45119
2018-12-23 13:01:07,269 INFO : test_misclass             0.45660
2018-12-23 13:01:07,269 INFO : runtime                   3.70834
2018-12-23 13:01:07,269 INFO : 
2018-12-23 13:01:09,417 INFO : Time only for training updates: 2.15s
2018-12-23 13:01:10,977 INFO : Epoch 41
2018-12-23 13:01:10,977 INFO : train_loss                0.80340
2018-12-23 13:01:10,978 INFO : valid_loss                0.99938
2018-12-23 13:01:10,979 INFO : test_loss                 1.12205
2018-12-23 13:01:10,980 INFO : train_misclass            0.31525
2018-12-23 13:01:10,980 INFO : valid_misclass            0.40781
2018-12-23 13:01:10,980 INFO : test_mis

...

2018-12-23 13:35:09,225 INFO : test_misclass             0.38542
2018-12-23 13:35:09,225 INFO : runtime                   3.71895
2018-12-23 13:35:09,226 INFO : 
2018-12-23 13:35:11,381 INFO : Time only for training updates: 2.15s
2018-12-23 13:35:12,944 INFO : Epoch 590
2018-12-23 13:35:12,944 INFO : train_loss                0.51518
2018-12-23 13:35:12,945 INFO : valid_loss                0.84763
2018-12-23 13:35:12,945 INFO : test_loss                 0.94445
2018-12-23 13:35:12,945 INFO : train_misclass            0.11774
2018-12-23 13:35:12,946 INFO : valid_misclass            0.34490
2018-12-23 13:35:12,947 INFO : test_misclass             0.40451
2018-12-23 13:35:12,947 INFO : runtime                   3.72160
2018-12-23 13:35:12,947 INFO : 
2018-12-23 13:35:15,103 INFO : Time only for training updates: 2.15s
2018-12-23 13:35:16,663 INFO : Epoch 591
2018-12-23 13:35:16,663 INFO : train_loss                0.50094
2018-12-23 13:35:16,664 INFO : valid_loss                0.92724
2

2018-12-23 13:36:01,315 INFO : train_misclass            0.12561
2018-12-23 13:36:01,316 INFO : valid_misclass            0.36009
2018-12-23 13:36:01,316 INFO : test_misclass             0.43229
2018-12-23 13:36:01,316 INFO : runtime                   3.72809
2018-12-23 13:36:01,317 INFO : 
2018-12-23 13:36:03,472 INFO : Time only for training updates: 2.15s
2018-12-23 13:36:05,046 INFO : Epoch 604
2018-12-23 13:36:05,046 INFO : train_loss                0.51894
2018-12-23 13:36:05,047 INFO : valid_loss                0.92404
2018-12-23 13:36:05,047 INFO : test_loss                 0.97913
2018-12-23 13:36:05,047 INFO : train_misclass            0.13375
2018-12-23 13:36:05,048 INFO : valid_misclass            0.37419
2018-12-23 13:36:05,048 INFO : test_misclass             0.38889
2018-12-23 13:36:05,049 INFO : runtime                   3.72458
2018-12-23 13:36:05,050 INFO : 
2018-12-23 13:36:07,210 INFO : Time only for training updates: 2.16s
2018-12-23 13:36:08,772 INFO : Epoch 605
2

2018-12-23 13:36:53,443 INFO : valid_loss                0.87712
2018-12-23 13:36:53,443 INFO : test_loss                 0.94719
2018-12-23 13:36:53,444 INFO : train_misclass            0.09387
2018-12-23 13:36:53,444 INFO : valid_misclass            0.35141
2018-12-23 13:36:53,445 INFO : test_misclass             0.39757
2018-12-23 13:36:53,445 INFO : runtime                   3.71994
2018-12-23 13:36:53,446 INFO : 
2018-12-23 13:36:55,600 INFO : Time only for training updates: 2.15s
2018-12-23 13:36:57,162 INFO : Epoch 618
2018-12-23 13:36:57,163 INFO : train_loss                0.49911
2018-12-23 13:36:57,163 INFO : valid_loss                0.87607
2018-12-23 13:36:57,164 INFO : test_loss                 0.94100
2018-12-23 13:36:57,165 INFO : train_misclass            0.12290
2018-12-23 13:36:57,165 INFO : valid_misclass            0.35249
2018-12-23 13:36:57,166 INFO : test_misclass             0.37326
2018-12-23 13:36:57,166 INFO : runtime                   3.72743
2018-12-23 13

2018-12-23 13:37:45,555 INFO : Epoch 631
2018-12-23 13:37:45,556 INFO : train_loss                0.50206
2018-12-23 13:37:45,556 INFO : valid_loss                0.88424
2018-12-23 13:37:45,557 INFO : test_loss                 0.92650
2018-12-23 13:37:45,557 INFO : train_misclass            0.11394
2018-12-23 13:37:45,558 INFO : valid_misclass            0.35466
2018-12-23 13:37:45,558 INFO : test_misclass             0.38021
2018-12-23 13:37:45,559 INFO : runtime                   3.72055
2018-12-23 13:37:45,559 INFO : 
2018-12-23 13:37:47,713 INFO : Time only for training updates: 2.15s
2018-12-23 13:37:49,274 INFO : Epoch 632
2018-12-23 13:37:49,275 INFO : train_loss                0.61167
2018-12-23 13:37:49,275 INFO : valid_loss                0.91066
2018-12-23 13:37:49,276 INFO : test_loss                 1.08557
2018-12-23 13:37:49,277 INFO : train_misclass            0.21405
2018-12-23 13:37:49,277 INFO : valid_misclass            0.37419
2018-12-23 13:37:49,278 INFO : test_m

2018-12-23 13:38:33,957 INFO : 
2018-12-23 13:38:36,111 INFO : Time only for training updates: 2.15s
2018-12-23 13:38:37,673 INFO : Epoch 645
2018-12-23 13:38:37,674 INFO : train_loss                0.55567
2018-12-23 13:38:37,675 INFO : valid_loss                0.94605
2018-12-23 13:38:37,675 INFO : test_loss                 0.99807
2018-12-23 13:38:37,675 INFO : train_misclass            0.17037
2018-12-23 13:38:37,676 INFO : valid_misclass            0.39262
2018-12-23 13:38:37,677 INFO : test_misclass             0.39757
2018-12-23 13:38:37,677 INFO : runtime                   3.72586
2018-12-23 13:38:37,678 INFO : 
2018-12-23 13:38:39,831 INFO : Time only for training updates: 2.15s
2018-12-23 13:38:41,394 INFO : Epoch 646
2018-12-23 13:38:41,395 INFO : train_loss                0.53704
2018-12-23 13:38:41,395 INFO : valid_loss                0.80763
2018-12-23 13:38:41,396 INFO : test_loss                 0.93160
2018-12-23 13:38:41,396 INFO : train_misclass            0.16196
2

In [9]:
def run_crop_exp(train_data, test_data, low_cut_hz, model, cuda):
    ival = [-500, 4000]
    input_time_length = 1000
    max_epochs = 800
    max_increase_epochs = 80
    batch_size = 60
    high_cut_hz = 38
    factor_new = 1e-3
    init_block_size = 1000
    valid_set_fraction = 0.2
    train_set, valid_set = split_into_two_sets(
        train_data, first_set_fraction=1-valid_set_fraction)

    set_random_seeds(seed=20190706, cuda=cuda)

    n_classes = 4
    n_chans = int(train_set.X.shape[1])
    if model == 'shallow':
        model = ShallowFBCSPNet(n_chans, n_classes, input_time_length=input_time_length,
                            final_conv_length=30).create_network()
    elif model == 'deep':
        model = Deep4Net(n_chans, n_classes, input_time_length=input_time_length,
                            final_conv_length=2).create_network()


    to_dense_prediction_model(model)
    if cuda:
        model.cuda()

    log.info("Model: \n{:s}".format(str(model)))
    dummy_input = np_to_var(train_set.X[:1, :, :, None])
    if cuda:
        dummy_input = dummy_input.cuda()
    out = model(dummy_input)

    n_preds_per_input = out.cpu().data.numpy().shape[2]

    optimizer = optim.Adam(model.parameters())

    iterator = CropsFromTrialsIterator(batch_size=batch_size,
                                       input_time_length=input_time_length,
                                       n_preds_per_input=n_preds_per_input)

    stop_criterion = Or([MaxEpochs(max_epochs),
                         NoDecrease('valid_misclass', max_increase_epochs)])

    monitors = [LossMonitor(), MisclassMonitor(col_suffix='sample_misclass'),
                CroppedTrialMisclassMonitor(
                    input_time_length=input_time_length), RuntimeMonitor()]

    model_constraint = MaxNormDefaultConstraint()

    loss_function = lambda preds, targets: F.nll_loss(
        th.mean(preds, dim=2, keepdim=False), targets)

    exp = Experiment(model, train_set, valid_set, test_data, iterator=iterator,
                     loss_function=loss_function, optimizer=optimizer,
                     model_constraint=model_constraint,
                     monitors=monitors,
                     stop_criterion=stop_criterion,
                     remember_best_column='valid_misclass',
                     run_after_early_stop=True, cuda=cuda)
    exp.run()
    return exp

In [10]:
def leave_one_out_crop_run(out):
    subjects_list = [i for i in range(1, 10)]
    subjects_list.remove(out)
    train_data = load_train_data(subjects_list)
    test_data = load_subject_data(out)

    logging.basicConfig(format='%(asctime)s %(levelname)s : %(message)s',
                            level=logging.DEBUG, stream=sys.stdout)
    cuda = True
    exp = run_crop_exp(train_data, test_data, low_cut_hz, "shallow", cuda)
    log.info("Last 10 epochs")
    log.info("\n" + str(exp.epochs_df.iloc[-10:]))

###  valid_misclass: 0.27007, test_misclass: 0.35764

In [26]:
leave_one_out_crop_run(1)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  2708.672 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 662665  =      0.000 ...  2650.660 secs...
2018-12-23 15:12:59,002 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
2018-12-23 15:12:59,251 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  26

2018-12-23 15:14:20,608 INFO : runtime                   0.00000
2018-12-23 15:14:20,608 INFO : 
2018-12-23 15:14:20,611 INFO : New best valid_misclass: 0.749458
2018-12-23 15:14:20,611 INFO : 
2018-12-23 15:14:25,962 INFO : Time only for training updates: 4.66s
2018-12-23 15:14:29,394 INFO : Epoch 1
2018-12-23 15:14:29,394 INFO : train_loss                1.28606
2018-12-23 15:14:29,395 INFO : valid_loss                1.17079
2018-12-23 15:14:29,396 INFO : test_loss                 1.12823
2018-12-23 15:14:29,396 INFO : train_sample_misclass     0.61400
2018-12-23 15:14:29,397 INFO : valid_sample_misclass     0.52659
2018-12-23 15:14:29,397 INFO : test_sample_misclass      0.54432
2018-12-23 15:14:29,397 INFO : train_misclass            0.60445
2018-12-23 15:14:29,398 INFO : valid_misclass            0.52169
2018-12-23 15:14:29,398 INFO : test_misclass             0.53993
2018-12-23 15:14:29,399 INFO : runtime                   8.82330
2018-12-23 15:14:29,399 INFO : 
2018-12-23 15:14

2018-12-23 15:15:48,563 INFO : valid_misclass            0.44035
2018-12-23 15:15:48,563 INFO : test_misclass             0.39931
2018-12-23 15:15:48,564 INFO : runtime                   8.78640
2018-12-23 15:15:48,564 INFO : 
2018-12-23 15:15:53,939 INFO : Time only for training updates: 4.68s
2018-12-23 15:15:57,375 INFO : Epoch 11
2018-12-23 15:15:57,376 INFO : train_loss                1.09802
2018-12-23 15:15:57,377 INFO : valid_loss                1.04847
2018-12-23 15:15:57,378 INFO : test_loss                 0.94524
2018-12-23 15:15:57,379 INFO : train_sample_misclass     0.48167
2018-12-23 15:15:57,379 INFO : valid_sample_misclass     0.43942
2018-12-23 15:15:57,379 INFO : test_sample_misclass      0.43422
2018-12-23 15:15:57,380 INFO : train_misclass            0.44167
2018-12-23 15:15:57,380 INFO : valid_misclass            0.38395
2018-12-23 15:15:57,381 INFO : test_misclass             0.41146
2018-12-23 15:15:57,381 INFO : runtime                   8.78771
2018-12-23 15:

2018-12-23 15:17:25,794 INFO : Epoch 21
2018-12-23 15:17:25,794 INFO : train_loss                1.03042
2018-12-23 15:17:25,795 INFO : valid_loss                1.05487
2018-12-23 15:17:25,795 INFO : test_loss                 0.88686
2018-12-23 15:17:25,796 INFO : train_sample_misclass     0.43473
2018-12-23 15:17:25,796 INFO : valid_sample_misclass     0.42129
2018-12-23 15:17:25,797 INFO : test_sample_misclass      0.39313
2018-12-23 15:17:25,798 INFO : train_misclass            0.38551
2018-12-23 15:17:25,798 INFO : valid_misclass            0.36768
2018-12-23 15:17:25,798 INFO : test_misclass             0.35243
2018-12-23 15:17:25,799 INFO : runtime                   8.87338
2018-12-23 15:17:25,799 INFO : 
2018-12-23 15:17:31,204 INFO : Time only for training updates: 4.71s
2018-12-23 15:17:34,635 INFO : Epoch 22
2018-12-23 15:17:34,636 INFO : train_loss                1.00551
2018-12-23 15:17:34,636 INFO : valid_loss                1.11815
2018-12-23 15:17:34,636 INFO : test_los

2018-12-23 15:18:54,261 INFO : valid_sample_misclass     0.47285
2018-12-23 15:18:54,261 INFO : test_sample_misclass      0.42830
2018-12-23 15:18:54,261 INFO : train_misclass            0.35540
2018-12-23 15:18:54,262 INFO : valid_misclass            0.44469
2018-12-23 15:18:54,262 INFO : test_misclass             0.38715
2018-12-23 15:18:54,263 INFO : runtime                   8.83637
2018-12-23 15:18:54,264 INFO : 
2018-12-23 15:18:59,669 INFO : Time only for training updates: 4.71s
2018-12-23 15:19:03,152 INFO : Epoch 32
2018-12-23 15:19:03,152 INFO : train_loss                1.14680
2018-12-23 15:19:03,153 INFO : valid_loss                1.28936
2018-12-23 15:19:03,153 INFO : test_loss                 1.01855
2018-12-23 15:19:03,154 INFO : train_sample_misclass     0.47994
2018-12-23 15:19:03,154 INFO : valid_sample_misclass     0.50085
2018-12-23 15:19:03,155 INFO : test_sample_misclass      0.46876
2018-12-23 15:19:03,155 INFO : train_misclass            0.46012
2018-12-23 15:

...

2018-12-23 15:34:16,937 INFO : valid_loss                1.16135
2018-12-23 15:34:16,937 INFO : test_loss                 1.06343
2018-12-23 15:34:16,938 INFO : train_sample_misclass     0.32325
2018-12-23 15:34:16,938 INFO : valid_sample_misclass     0.46128
2018-12-23 15:34:16,939 INFO : test_sample_misclass      0.44946
2018-12-23 15:34:16,939 INFO : train_misclass            0.26587
2018-12-23 15:34:16,940 INFO : valid_misclass            0.42082
2018-12-23 15:34:16,940 INFO : test_misclass             0.40451
2018-12-23 15:34:16,941 INFO : runtime                   8.85813
2018-12-23 15:34:16,942 INFO : 
2018-12-23 15:34:22,349 INFO : Time only for training updates: 4.71s
2018-12-23 15:34:25,786 INFO : Epoch 136
2018-12-23 15:34:25,787 INFO : train_loss                0.88147
2018-12-23 15:34:25,787 INFO : valid_loss                1.22600
2018-12-23 15:34:25,788 INFO : test_loss                 0.85898
2018-12-23 15:34:25,788 INFO : train_sample_misclass     0.36350
2018-12-23 15

2018-12-23 15:35:45,462 INFO : train_misclass            0.21894
2018-12-23 15:35:45,462 INFO : valid_misclass            0.44360
2018-12-23 15:35:45,463 INFO : test_misclass             0.37847
2018-12-23 15:35:45,463 INFO : runtime                   8.88035
2018-12-23 15:35:45,464 INFO : 
2018-12-23 15:35:50,873 INFO : Time only for training updates: 4.71s
2018-12-23 15:35:54,302 INFO : Epoch 146
2018-12-23 15:35:54,303 INFO : train_loss                0.89261
2018-12-23 15:35:54,304 INFO : valid_loss                1.15749
2018-12-23 15:35:54,304 INFO : test_loss                 0.88998
2018-12-23 15:35:54,304 INFO : train_sample_misclass     0.35369
2018-12-23 15:35:54,305 INFO : valid_sample_misclass     0.41527
2018-12-23 15:35:54,305 INFO : test_sample_misclass      0.38903
2018-12-23 15:35:54,306 INFO : train_misclass            0.31063
2018-12-23 15:35:54,306 INFO : valid_misclass            0.37744
2018-12-23 15:35:54,307 INFO : test_misclass             0.33681
2018-12-23 15

2018-12-23 15:37:19,386 INFO : Time only for training updates: 4.71s
2018-12-23 15:37:22,808 INFO : Epoch 156
2018-12-23 15:37:22,809 INFO : train_loss                0.83252
2018-12-23 15:37:22,809 INFO : valid_loss                1.14149
2018-12-23 15:37:22,810 INFO : test_loss                 0.99780
2018-12-23 15:37:22,811 INFO : train_sample_misclass     0.31986
2018-12-23 15:37:22,812 INFO : valid_sample_misclass     0.45262
2018-12-23 15:37:22,813 INFO : test_sample_misclass      0.45181
2018-12-23 15:37:22,813 INFO : train_misclass            0.26560
2018-12-23 15:37:22,814 INFO : valid_misclass            0.43059
2018-12-23 15:37:22,814 INFO : test_misclass             0.43924
2018-12-23 15:37:22,815 INFO : runtime                   8.84317
2018-12-23 15:37:22,815 INFO : 
2018-12-23 15:37:28,220 INFO : Time only for training updates: 4.71s
2018-12-23 15:37:31,686 INFO : Epoch 157
2018-12-23 15:37:31,686 INFO : train_loss                0.85975
2018-12-23 15:37:31,687 INFO : va

2018-12-23 15:38:51,362 INFO : train_sample_misclass     0.33985
2018-12-23 15:38:51,362 INFO : valid_sample_misclass     0.48993
2018-12-23 15:38:51,362 INFO : test_sample_misclass      0.41813
2018-12-23 15:38:51,363 INFO : train_misclass            0.29219
2018-12-23 15:38:51,363 INFO : valid_misclass            0.48482
2018-12-23 15:38:51,363 INFO : test_misclass             0.39757
2018-12-23 15:38:51,364 INFO : runtime                   8.83652
2018-12-23 15:38:51,364 INFO : 
2018-12-23 15:38:56,772 INFO : Time only for training updates: 4.71s
2018-12-23 15:39:00,206 INFO : Epoch 167
2018-12-23 15:39:00,206 INFO : train_loss                0.94084
2018-12-23 15:39:00,207 INFO : valid_loss                1.12050
2018-12-23 15:39:00,207 INFO : test_loss                 0.93332
2018-12-23 15:39:00,208 INFO : train_sample_misclass     0.36918
2018-12-23 15:39:00,208 INFO : valid_sample_misclass     0.41558
2018-12-23 15:39:00,209 INFO : test_sample_misclass      0.39197
2018-12-23 15

2018-12-23 15:40:19,863 INFO : test_misclass             0.41667
2018-12-23 15:40:19,863 INFO : runtime                   8.84587
2018-12-23 15:40:19,863 INFO : 
2018-12-23 15:40:19,864 INFO : Setup for second stop...
2018-12-23 15:40:19,867 INFO : Train loss to reach 0.97642
2018-12-23 15:40:19,868 INFO : Run until second stop...
2018-12-23 15:40:24,010 INFO : Epoch 97
2018-12-23 15:40:24,011 INFO : train_loss                0.98370
2018-12-23 15:40:24,012 INFO : valid_loss                1.01280
2018-12-23 15:40:24,012 INFO : test_loss                 1.07371
2018-12-23 15:40:24,013 INFO : train_sample_misclass     0.40594
2018-12-23 15:40:24,013 INFO : valid_sample_misclass     0.39011
2018-12-23 15:40:24,014 INFO : test_sample_misclass      0.44166
2018-12-23 15:40:24,014 INFO : train_misclass            0.37240
2018-12-23 15:40:24,014 INFO : valid_misclass            0.32755
2018-12-23 15:40:24,015 INFO : test_misclass             0.42361
2018-12-23 15:40:24,015 INFO : runtime    

###  valid_misclass: 0.248373, test_misclass: 0.76215

In [27]:
leave_one_out_crop_run(2)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 15:41:45,460 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 15:41:45,727 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  26

2018-12-23 15:43:08,803 INFO : runtime                   0.00000
2018-12-23 15:43:08,804 INFO : 
2018-12-23 15:43:08,806 INFO : New best valid_misclass: 0.749458
2018-12-23 15:43:08,806 INFO : 
2018-12-23 15:43:14,198 INFO : Time only for training updates: 4.70s
2018-12-23 15:43:17,617 INFO : Epoch 1
2018-12-23 15:43:17,617 INFO : train_loss                1.17815
2018-12-23 15:43:17,618 INFO : valid_loss                1.18911
2018-12-23 15:43:17,618 INFO : test_loss                 1.61774
2018-12-23 15:43:17,619 INFO : train_sample_misclass     0.52837
2018-12-23 15:43:17,619 INFO : valid_sample_misclass     0.51329
2018-12-23 15:43:17,620 INFO : test_sample_misclass      0.71929
2018-12-23 15:43:17,621 INFO : train_misclass            0.50488
2018-12-23 15:43:17,621 INFO : valid_misclass            0.50217
2018-12-23 15:43:17,622 INFO : test_misclass             0.71181
2018-12-23 15:43:17,622 INFO : runtime                   8.86277
2018-12-23 15:43:17,624 INFO : 
2018-12-23 15:43

2018-12-23 15:44:37,281 INFO : test_misclass             0.76736
2018-12-23 15:44:37,282 INFO : runtime                   8.86505
2018-12-23 15:44:37,282 INFO : 
2018-12-23 15:44:42,701 INFO : Time only for training updates: 4.72s
2018-12-23 15:44:46,165 INFO : Epoch 11
2018-12-23 15:44:46,165 INFO : train_loss                0.90985
2018-12-23 15:44:46,166 INFO : valid_loss                1.03957
2018-12-23 15:44:46,166 INFO : test_loss                 1.90488
2018-12-23 15:44:46,166 INFO : train_sample_misclass     0.37327
2018-12-23 15:44:46,167 INFO : valid_sample_misclass     0.41502
2018-12-23 15:44:46,168 INFO : test_sample_misclass      0.72374
2018-12-23 15:44:46,168 INFO : train_misclass            0.32284
2018-12-23 15:44:46,169 INFO : valid_misclass            0.36659
2018-12-23 15:44:46,170 INFO : test_misclass             0.71007
2018-12-23 15:44:46,170 INFO : runtime                   8.86061
2018-12-23 15:44:46,171 INFO : 
2018-12-23 15:44:51,589 INFO : Time only for tr

2018-12-23 15:46:14,881 INFO : valid_loss                1.05861
2018-12-23 15:46:14,881 INFO : test_loss                 2.02705
2018-12-23 15:46:14,882 INFO : train_sample_misclass     0.36387
2018-12-23 15:46:14,882 INFO : valid_sample_misclass     0.39999
2018-12-23 15:46:14,883 INFO : test_sample_misclass      0.71214
2018-12-23 15:46:14,883 INFO : train_misclass            0.30928
2018-12-23 15:46:14,884 INFO : valid_misclass            0.35683
2018-12-23 15:46:14,884 INFO : test_misclass             0.68924
2018-12-23 15:46:14,884 INFO : runtime                   8.94028
2018-12-23 15:46:14,885 INFO : 
2018-12-23 15:46:14,889 INFO : New best valid_misclass: 0.356833
2018-12-23 15:46:14,890 INFO : 
2018-12-23 15:46:20,323 INFO : Time only for training updates: 4.72s
2018-12-23 15:46:23,749 INFO : Epoch 22
2018-12-23 15:46:23,750 INFO : train_loss                0.83793
2018-12-23 15:46:23,750 INFO : valid_loss                1.10835
2018-12-23 15:46:23,751 INFO : test_loss       

2018-12-23 15:47:43,547 INFO : train_sample_misclass     0.32540
2018-12-23 15:47:43,547 INFO : valid_sample_misclass     0.44703
2018-12-23 15:47:43,548 INFO : test_sample_misclass      0.72756
2018-12-23 15:47:43,548 INFO : train_misclass            0.26994
2018-12-23 15:47:43,549 INFO : valid_misclass            0.42408
2018-12-23 15:47:43,549 INFO : test_misclass             0.72743
2018-12-23 15:47:43,550 INFO : runtime                   8.88637
2018-12-23 15:47:43,551 INFO : 
2018-12-23 15:47:48,974 INFO : Time only for training updates: 4.72s
2018-12-23 15:47:52,410 INFO : Epoch 32
2018-12-23 15:47:52,411 INFO : train_loss                0.82365
2018-12-23 15:47:52,411 INFO : valid_loss                1.16954
2018-12-23 15:47:52,412 INFO : test_loss                 1.92977
2018-12-23 15:47:52,413 INFO : train_sample_misclass     0.33088
2018-12-23 15:47:52,413 INFO : valid_sample_misclass     0.45260
2018-12-23 15:47:52,413 INFO : test_sample_misclass      0.69996
2018-12-23 15:

...

2018-12-23 15:52:18,296 INFO : train_misclass            0.21378
2018-12-23 15:52:18,296 INFO : valid_misclass            0.37744
2018-12-23 15:52:18,297 INFO : test_misclass             0.72049
2018-12-23 15:52:18,297 INFO : runtime                   8.85578
2018-12-23 15:52:18,297 INFO : 
2018-12-23 15:52:23,720 INFO : Time only for training updates: 4.72s
2018-12-23 15:52:27,182 INFO : Epoch 63
2018-12-23 15:52:27,182 INFO : train_loss                0.79409
2018-12-23 15:52:27,183 INFO : valid_loss                1.05874
2018-12-23 15:52:27,183 INFO : test_loss                 2.25958
2018-12-23 15:52:27,184 INFO : train_sample_misclass     0.31513
2018-12-23 15:52:27,184 INFO : valid_sample_misclass     0.41368
2018-12-23 15:52:27,184 INFO : test_sample_misclass      0.71184
2018-12-23 15:52:27,185 INFO : train_misclass            0.26072
2018-12-23 15:52:27,185 INFO : valid_misclass            0.37527
2018-12-23 15:52:27,186 INFO : test_misclass             0.70312
2018-12-23 15:

2018-12-23 15:53:52,352 INFO : Time only for training updates: 4.72s
2018-12-23 15:53:55,797 INFO : Epoch 73
2018-12-23 15:53:55,798 INFO : train_loss                0.81491
2018-12-23 15:53:55,798 INFO : valid_loss                1.22866
2018-12-23 15:53:55,799 INFO : test_loss                 2.87627
2018-12-23 15:53:55,799 INFO : train_sample_misclass     0.32745
2018-12-23 15:53:55,800 INFO : valid_sample_misclass     0.46618
2018-12-23 15:53:55,801 INFO : test_sample_misclass      0.73738
2018-12-23 15:53:55,802 INFO : train_misclass            0.28378
2018-12-23 15:53:55,802 INFO : valid_misclass            0.45445
2018-12-23 15:53:55,803 INFO : test_misclass             0.73264
2018-12-23 15:53:55,803 INFO : runtime                   8.85501
2018-12-23 15:53:55,804 INFO : 
2018-12-23 15:54:01,218 INFO : Time only for training updates: 4.72s
2018-12-23 15:54:04,666 INFO : Epoch 74
2018-12-23 15:54:04,667 INFO : train_loss                0.85024
2018-12-23 15:54:04,668 INFO : vali

2018-12-23 15:55:24,431 INFO : train_sample_misclass     0.26146
2018-12-23 15:55:24,432 INFO : valid_sample_misclass     0.43752
2018-12-23 15:55:24,432 INFO : test_sample_misclass      0.72356
2018-12-23 15:55:24,433 INFO : train_misclass            0.19940
2018-12-23 15:55:24,433 INFO : valid_misclass            0.41106
2018-12-23 15:55:24,434 INFO : test_misclass             0.71701
2018-12-23 15:55:24,434 INFO : runtime                   8.89390
2018-12-23 15:55:24,434 INFO : 
2018-12-23 15:55:29,854 INFO : Time only for training updates: 4.72s
2018-12-23 15:55:33,288 INFO : Epoch 84
2018-12-23 15:55:33,289 INFO : train_loss                0.72883
2018-12-23 15:55:33,289 INFO : valid_loss                1.13894
2018-12-23 15:55:33,290 INFO : test_loss                 1.94818
2018-12-23 15:55:33,290 INFO : train_sample_misclass     0.27912
2018-12-23 15:55:33,290 INFO : valid_sample_misclass     0.42179
2018-12-23 15:55:33,292 INFO : test_sample_misclass      0.71675
2018-12-23 15:

2018-12-23 15:56:53,035 INFO : test_misclass             0.71701
2018-12-23 15:56:53,035 INFO : runtime                   8.85596
2018-12-23 15:56:53,035 INFO : 
2018-12-23 15:56:58,451 INFO : Time only for training updates: 4.72s
2018-12-23 15:57:01,876 INFO : Epoch 94
2018-12-23 15:57:01,876 INFO : train_loss                0.73980
2018-12-23 15:57:01,877 INFO : valid_loss                1.12029
2018-12-23 15:57:01,878 INFO : test_loss                 2.12334
2018-12-23 15:57:01,878 INFO : train_sample_misclass     0.28627
2018-12-23 15:57:01,879 INFO : valid_sample_misclass     0.42669
2018-12-23 15:57:01,879 INFO : test_sample_misclass      0.72456
2018-12-23 15:57:01,880 INFO : train_misclass            0.22355
2018-12-23 15:57:01,880 INFO : valid_misclass            0.39805
2018-12-23 15:57:01,881 INFO : test_misclass             0.71181
2018-12-23 15:57:01,881 INFO : runtime                   8.84831
2018-12-23 15:57:01,882 INFO : 
2018-12-23 15:57:07,301 INFO : Time only for tr

2018-12-23 15:58:30,876 INFO : valid_loss                1.07817
2018-12-23 15:58:30,876 INFO : test_loss                 2.02806
2018-12-23 15:58:30,877 INFO : train_sample_misclass     0.29929
2018-12-23 15:58:30,878 INFO : valid_sample_misclass     0.40486
2018-12-23 15:58:30,878 INFO : test_sample_misclass      0.74780
2018-12-23 15:58:30,879 INFO : train_misclass            0.25231
2018-12-23 15:58:30,880 INFO : valid_misclass            0.34599
2018-12-23 15:58:30,880 INFO : test_misclass             0.75000
2018-12-23 15:58:30,881 INFO : runtime                   8.83282
2018-12-23 15:58:30,881 INFO : 
2018-12-23 15:58:36,306 INFO : Time only for training updates: 4.72s
2018-12-23 15:58:39,746 INFO : Epoch 105
2018-12-23 15:58:39,747 INFO : train_loss                0.73513
2018-12-23 15:58:39,747 INFO : valid_loss                1.19453
2018-12-23 15:58:39,748 INFO : test_loss                 1.76895
2018-12-23 15:58:39,748 INFO : train_sample_misclass     0.26595
2018-12-23 15

###  valid_misclass: 0.342733, test_misclass: 0.55729

In [28]:
leave_one_out_crop_run(3)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 15:59:14,921 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 15:59:15,182 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 16:00:36,456 INFO : runtime                   0.00000
2018-12-23 16:00:36,456 INFO : 
2018-12-23 16:00:36,458 INFO : New best valid_misclass: 0.749458
2018-12-23 16:00:36,459 INFO : 
2018-12-23 16:00:41,845 INFO : Time only for training updates: 4.69s
2018-12-23 16:00:45,262 INFO : Epoch 1
2018-12-23 16:00:45,263 INFO : train_loss                1.29725
2018-12-23 16:00:45,263 INFO : valid_loss                1.20348
2018-12-23 16:00:45,264 INFO : test_loss                 1.18418
2018-12-23 16:00:45,264 INFO : train_sample_misclass     0.60964
2018-12-23 16:00:45,265 INFO : valid_sample_misclass     0.54186
2018-12-23 16:00:45,265 INFO : test_sample_misclass      0.54051
2018-12-23 16:00:45,266 INFO : train_misclass            0.59333
2018-12-23 16:00:45,266 INFO : valid_misclass            0.53037
2018-12-23 16:00:45,266 INFO : test_misclass             0.52604
2018-12-23 16:00:45,267 INFO : runtime                   8.89464
2018-12-23 16:00:45,267 INFO : 
2018-12-23 16:00

2018-12-23 16:02:04,903 INFO : test_misclass             0.34028
2018-12-23 16:02:04,903 INFO : runtime                   8.85757
2018-12-23 16:02:04,903 INFO : 
2018-12-23 16:02:10,333 INFO : Time only for training updates: 4.73s
2018-12-23 16:02:13,769 INFO : Epoch 11
2018-12-23 16:02:13,770 INFO : train_loss                1.09745
2018-12-23 16:02:13,770 INFO : valid_loss                1.03332
2018-12-23 16:02:13,771 INFO : test_loss                 1.01566
2018-12-23 16:02:13,771 INFO : train_sample_misclass     0.47926
2018-12-23 16:02:13,772 INFO : valid_sample_misclass     0.42053
2018-12-23 16:02:13,772 INFO : test_sample_misclass      0.43183
2018-12-23 16:02:13,773 INFO : train_misclass            0.43977
2018-12-23 16:02:13,773 INFO : valid_misclass            0.35466
2018-12-23 16:02:13,774 INFO : test_misclass             0.39931
2018-12-23 16:02:13,774 INFO : runtime                   8.89042
2018-12-23 16:02:13,774 INFO : 
2018-12-23 16:02:13,779 INFO : New best valid_m

2018-12-23 16:03:42,577 INFO : Epoch 21
2018-12-23 16:03:42,577 INFO : train_loss                0.99526
2018-12-23 16:03:42,578 INFO : valid_loss                1.03675
2018-12-23 16:03:42,578 INFO : test_loss                 0.96034
2018-12-23 16:03:42,578 INFO : train_sample_misclass     0.42083
2018-12-23 16:03:42,579 INFO : valid_sample_misclass     0.40111
2018-12-23 16:03:42,579 INFO : test_sample_misclass      0.40399
2018-12-23 16:03:42,579 INFO : train_misclass            0.36923
2018-12-23 16:03:42,580 INFO : valid_misclass            0.34273
2018-12-23 16:03:42,580 INFO : test_misclass             0.34549
2018-12-23 16:03:42,580 INFO : runtime                   8.89100
2018-12-23 16:03:42,581 INFO : 
2018-12-23 16:03:42,584 INFO : New best valid_misclass: 0.342733
2018-12-23 16:03:42,585 INFO : 
2018-12-23 16:03:48,058 INFO : Time only for training updates: 4.76s
2018-12-23 16:03:51,545 INFO : Epoch 22
2018-12-23 16:03:51,545 INFO : train_loss                0.97120
2018-12

2018-12-23 16:05:12,208 INFO : train_sample_misclass     0.38937
2018-12-23 16:05:12,209 INFO : valid_sample_misclass     0.48117
2018-12-23 16:05:12,210 INFO : test_sample_misclass      0.42625
2018-12-23 16:05:12,210 INFO : train_misclass            0.33749
2018-12-23 16:05:12,210 INFO : valid_misclass            0.45879
2018-12-23 16:05:12,211 INFO : test_misclass             0.38542
2018-12-23 16:05:12,211 INFO : runtime                   8.85288
2018-12-23 16:05:12,211 INFO : 
2018-12-23 16:05:17,621 INFO : Time only for training updates: 4.71s
2018-12-23 16:05:21,082 INFO : Epoch 32
2018-12-23 16:05:21,083 INFO : train_loss                0.90645
2018-12-23 16:05:21,083 INFO : valid_loss                1.08695
2018-12-23 16:05:21,084 INFO : test_loss                 0.93831
2018-12-23 16:05:21,084 INFO : train_sample_misclass     0.35545
2018-12-23 16:05:21,086 INFO : valid_sample_misclass     0.44043
2018-12-23 16:05:21,086 INFO : test_sample_misclass      0.37694
2018-12-23 16:

...

2018-12-23 16:09:46,822 INFO : train_misclass            0.28405
2018-12-23 16:09:46,823 INFO : valid_misclass            0.41649
2018-12-23 16:09:46,823 INFO : test_misclass             0.39931
2018-12-23 16:09:46,824 INFO : runtime                   8.85575
2018-12-23 16:09:46,825 INFO : 
2018-12-23 16:09:52,239 INFO : Time only for training updates: 4.72s
2018-12-23 16:09:55,673 INFO : Epoch 63
2018-12-23 16:09:55,674 INFO : train_loss                0.88640
2018-12-23 16:09:55,675 INFO : valid_loss                1.06883
2018-12-23 16:09:55,675 INFO : test_loss                 1.14228
2018-12-23 16:09:55,676 INFO : train_sample_misclass     0.34407
2018-12-23 16:09:55,676 INFO : valid_sample_misclass     0.43341
2018-12-23 16:09:55,676 INFO : test_sample_misclass      0.51261
2018-12-23 16:09:55,677 INFO : train_misclass            0.27645
2018-12-23 16:09:55,677 INFO : valid_misclass            0.39371
2018-12-23 16:09:55,678 INFO : test_misclass             0.49653
2018-12-23 16:

2018-12-23 16:11:20,813 INFO : Time only for training updates: 4.72s
2018-12-23 16:11:24,247 INFO : Epoch 73
2018-12-23 16:11:24,247 INFO : train_loss                0.84881
2018-12-23 16:11:24,248 INFO : valid_loss                1.19466
2018-12-23 16:11:24,248 INFO : test_loss                 1.00663
2018-12-23 16:11:24,248 INFO : train_sample_misclass     0.32403
2018-12-23 16:11:24,249 INFO : valid_sample_misclass     0.47133
2018-12-23 16:11:24,251 INFO : test_sample_misclass      0.42807
2018-12-23 16:11:24,251 INFO : train_misclass            0.25936
2018-12-23 16:11:24,251 INFO : valid_misclass            0.44035
2018-12-23 16:11:24,252 INFO : test_misclass             0.39757
2018-12-23 16:11:24,252 INFO : runtime                   8.85402
2018-12-23 16:11:24,253 INFO : 
2018-12-23 16:11:29,659 INFO : Time only for training updates: 4.71s
2018-12-23 16:11:33,098 INFO : Epoch 74
2018-12-23 16:11:33,099 INFO : train_loss                0.89475
2018-12-23 16:11:33,099 INFO : vali

2018-12-23 16:12:52,805 INFO : train_sample_misclass     0.31120
2018-12-23 16:12:52,806 INFO : valid_sample_misclass     0.43420
2018-12-23 16:12:52,806 INFO : test_sample_misclass      0.39665
2018-12-23 16:12:52,807 INFO : train_misclass            0.24797
2018-12-23 16:12:52,807 INFO : valid_misclass            0.39696
2018-12-23 16:12:52,807 INFO : test_misclass             0.35243
2018-12-23 16:12:52,808 INFO : runtime                   8.86621
2018-12-23 16:12:52,808 INFO : 
2018-12-23 16:12:58,220 INFO : Time only for training updates: 4.71s
2018-12-23 16:13:01,692 INFO : Epoch 84
2018-12-23 16:13:01,693 INFO : train_loss                0.94103
2018-12-23 16:13:01,693 INFO : valid_loss                1.19872
2018-12-23 16:13:01,694 INFO : test_loss                 1.17902
2018-12-23 16:13:01,694 INFO : train_sample_misclass     0.39217
2018-12-23 16:13:01,695 INFO : valid_sample_misclass     0.45925
2018-12-23 16:13:01,695 INFO : test_sample_misclass      0.50788
2018-12-23 16:

2018-12-23 16:14:21,462 INFO : test_misclass             0.49132
2018-12-23 16:14:21,462 INFO : runtime                   8.85370
2018-12-23 16:14:21,463 INFO : 
2018-12-23 16:14:26,865 INFO : Time only for training updates: 4.71s
2018-12-23 16:14:30,292 INFO : Epoch 94
2018-12-23 16:14:30,293 INFO : train_loss                0.84945
2018-12-23 16:14:30,294 INFO : valid_loss                1.09085
2018-12-23 16:14:30,294 INFO : test_loss                 1.00016
2018-12-23 16:14:30,295 INFO : train_sample_misclass     0.34038
2018-12-23 16:14:30,295 INFO : valid_sample_misclass     0.43476
2018-12-23 16:14:30,296 INFO : test_sample_misclass      0.43920
2018-12-23 16:14:30,297 INFO : train_misclass            0.29300
2018-12-23 16:14:30,299 INFO : valid_misclass            0.39805
2018-12-23 16:14:30,299 INFO : test_misclass             0.40625
2018-12-23 16:14:30,300 INFO : runtime                   8.83948
2018-12-23 16:14:30,301 INFO : 
2018-12-23 16:14:35,809 INFO : Time only for tr

2018-12-23 16:15:47,705 INFO : 
2018-12-23 16:15:47,710 INFO : New best valid_misclass: 0.342733
2018-12-23 16:15:47,710 INFO : 
2018-12-23 16:15:47,711 INFO : Last 10 epochs
2018-12-23 16:15:47,717 INFO : 
    train_loss  valid_loss  test_loss  train_sample_misclass  \
14    1.032623    1.084765   1.030635               0.436551   
15    1.034566    1.132661   1.037783               0.432634   
16    0.995432    1.106596   0.990004               0.415570   
17    1.008420    1.122124   1.055279               0.420570   
18    1.248013    1.248353   1.478561               0.492866   
19    1.038582    1.096585   1.170336               0.425598   
20    1.001110    1.082610   0.937241               0.425308   
21    0.995259    1.036755   0.960337               0.420833   
22    1.003562    1.036755   0.960337               0.416887   
23    1.048842    0.960109   1.113127               0.458276   

    valid_sample_misclass  test_sample_misclass  train_misclass  \
14               0.44

###  valid_misclass: 0.259219, test_misclass: 0.61806

In [29]:
leave_one_out_crop_run(4)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-23 16:15:57,131 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-23 16:15:57,394 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-23 16:17:18,579 INFO : runtime                   0.00000
2018-12-23 16:17:18,579 INFO : 
2018-12-23 16:17:18,580 INFO : New best valid_misclass: 0.749458
2018-12-23 16:17:18,581 INFO : 
2018-12-23 16:17:23,959 INFO : Time only for training updates: 4.68s
2018-12-23 16:17:27,374 INFO : Epoch 1
2018-12-23 16:17:27,375 INFO : train_loss                1.26043
2018-12-23 16:17:27,375 INFO : valid_loss                1.25717
2018-12-23 16:17:27,376 INFO : test_loss                 1.38690
2018-12-23 16:17:27,376 INFO : train_sample_misclass     0.60052
2018-12-23 16:17:27,377 INFO : valid_sample_misclass     0.57629
2018-12-23 16:17:27,378 INFO : test_sample_misclass      0.67744
2018-12-23 16:17:27,378 INFO : train_misclass            0.60038
2018-12-23 16:17:27,379 INFO : valid_misclass            0.61388
2018-12-23 16:17:27,380 INFO : test_misclass             0.66840
2018-12-23 16:17:27,380 INFO : runtime                   8.86843
2018-12-23 16:17:27,381 INFO : 
2018-12-23 16:17

2018-12-23 16:18:46,825 INFO : valid_misclass            0.35249
2018-12-23 16:18:46,825 INFO : test_misclass             0.62500
2018-12-23 16:18:46,826 INFO : runtime                   8.85174
2018-12-23 16:18:46,826 INFO : 
2018-12-23 16:18:52,231 INFO : Time only for training updates: 4.71s
2018-12-23 16:18:55,652 INFO : Epoch 11
2018-12-23 16:18:55,653 INFO : train_loss                1.00675
2018-12-23 16:18:55,653 INFO : valid_loss                1.05048
2018-12-23 16:18:55,653 INFO : test_loss                 1.45126
2018-12-23 16:18:55,654 INFO : train_sample_misclass     0.41694
2018-12-23 16:18:55,654 INFO : valid_sample_misclass     0.41829
2018-12-23 16:18:55,655 INFO : test_sample_misclass      0.66994
2018-12-23 16:18:55,656 INFO : train_misclass            0.38063
2018-12-23 16:18:55,657 INFO : valid_misclass            0.37961
2018-12-23 16:18:55,657 INFO : test_misclass             0.63889
2018-12-23 16:18:55,658 INFO : runtime                   8.83498
2018-12-23 16:

2018-12-23 16:20:15,256 INFO : 
2018-12-23 16:20:15,260 INFO : New best valid_misclass: 0.345987
2018-12-23 16:20:15,260 INFO : 
2018-12-23 16:20:20,657 INFO : Time only for training updates: 4.70s
2018-12-23 16:20:24,073 INFO : Epoch 21
2018-12-23 16:20:24,073 INFO : train_loss                0.93190
2018-12-23 16:20:24,074 INFO : valid_loss                1.02441
2018-12-23 16:20:24,075 INFO : test_loss                 1.49696
2018-12-23 16:20:24,075 INFO : train_sample_misclass     0.38465
2018-12-23 16:20:24,076 INFO : valid_sample_misclass     0.40390
2018-12-23 16:20:24,076 INFO : test_sample_misclass      0.64803
2018-12-23 16:20:24,077 INFO : train_misclass            0.32881
2018-12-23 16:20:24,078 INFO : valid_misclass            0.35249
2018-12-23 16:20:24,078 INFO : test_misclass             0.64062
2018-12-23 16:20:24,078 INFO : runtime                   8.81947
2018-12-23 16:20:24,079 INFO : 
2018-12-23 16:20:29,480 INFO : Time only for training updates: 4.70s
2018-12-23 

2018-12-23 16:21:43,544 INFO : 
2018-12-23 16:21:48,945 INFO : Time only for training updates: 4.71s
2018-12-23 16:21:52,365 INFO : Epoch 31
2018-12-23 16:21:52,366 INFO : train_loss                0.88023
2018-12-23 16:21:52,366 INFO : valid_loss                1.10847
2018-12-23 16:21:52,367 INFO : test_loss                 1.56474
2018-12-23 16:21:52,367 INFO : train_sample_misclass     0.35316
2018-12-23 16:21:52,368 INFO : valid_sample_misclass     0.44040
2018-12-23 16:21:52,368 INFO : test_sample_misclass      0.66862
2018-12-23 16:21:52,369 INFO : train_misclass            0.30005
2018-12-23 16:21:52,369 INFO : valid_misclass            0.39588
2018-12-23 16:21:52,370 INFO : test_misclass             0.67708
2018-12-23 16:21:52,371 INFO : runtime                   8.82687
2018-12-23 16:21:52,371 INFO : 
2018-12-23 16:21:57,781 INFO : Time only for training updates: 4.72s
2018-12-23 16:22:01,199 INFO : Epoch 32
2018-12-23 16:22:01,200 INFO : train_loss                0.85526
201

...

2018-12-23 16:27:54,889 INFO : train_misclass            0.35730
2018-12-23 16:27:54,890 INFO : valid_misclass            0.48807
2018-12-23 16:27:54,890 INFO : test_misclass             0.65972
2018-12-23 16:27:54,891 INFO : runtime                   8.86751
2018-12-23 16:27:54,891 INFO : 
2018-12-23 16:28:00,304 INFO : Time only for training updates: 4.71s
2018-12-23 16:28:03,722 INFO : Epoch 73
2018-12-23 16:28:03,723 INFO : train_loss                0.82672
2018-12-23 16:28:03,723 INFO : valid_loss                1.10874
2018-12-23 16:28:03,724 INFO : test_loss                 1.57129
2018-12-23 16:28:03,724 INFO : train_sample_misclass     0.31987
2018-12-23 16:28:03,725 INFO : valid_sample_misclass     0.44687
2018-12-23 16:28:03,725 INFO : test_sample_misclass      0.66642
2018-12-23 16:28:03,726 INFO : train_misclass            0.26614
2018-12-23 16:28:03,727 INFO : valid_misclass            0.41215
2018-12-23 16:28:03,727 INFO : test_misclass             0.68056
2018-12-23 16:

2018-12-23 16:29:28,734 INFO : Time only for training updates: 4.71s
2018-12-23 16:29:32,153 INFO : Epoch 83
2018-12-23 16:29:32,153 INFO : train_loss                0.81144
2018-12-23 16:29:32,154 INFO : valid_loss                1.02914
2018-12-23 16:29:32,154 INFO : test_loss                 1.57732
2018-12-23 16:29:32,154 INFO : train_sample_misclass     0.31827
2018-12-23 16:29:32,155 INFO : valid_sample_misclass     0.40867
2018-12-23 16:29:32,156 INFO : test_sample_misclass      0.66509
2018-12-23 16:29:32,156 INFO : train_misclass            0.26886
2018-12-23 16:29:32,157 INFO : valid_misclass            0.35900
2018-12-23 16:29:32,157 INFO : test_misclass             0.66493
2018-12-23 16:29:32,158 INFO : runtime                   8.83869
2018-12-23 16:29:32,158 INFO : 
2018-12-23 16:29:37,563 INFO : Time only for training updates: 4.71s
2018-12-23 16:29:40,979 INFO : Epoch 84
2018-12-23 16:29:40,980 INFO : train_loss                0.90462
2018-12-23 16:29:40,980 INFO : vali

2018-12-23 16:31:00,571 INFO : train_sample_misclass     0.31202
2018-12-23 16:31:00,572 INFO : valid_sample_misclass     0.42124
2018-12-23 16:31:00,572 INFO : test_sample_misclass      0.67733
2018-12-23 16:31:00,573 INFO : train_misclass            0.25583
2018-12-23 16:31:00,574 INFO : valid_misclass            0.36117
2018-12-23 16:31:00,574 INFO : test_misclass             0.69097
2018-12-23 16:31:00,575 INFO : runtime                   8.83499
2018-12-23 16:31:00,575 INFO : 
2018-12-23 16:31:05,980 INFO : Time only for training updates: 4.71s
2018-12-23 16:31:09,399 INFO : Epoch 94
2018-12-23 16:31:09,399 INFO : train_loss                0.81956
2018-12-23 16:31:09,400 INFO : valid_loss                1.19459
2018-12-23 16:31:09,400 INFO : test_loss                 1.53314
2018-12-23 16:31:09,400 INFO : train_sample_misclass     0.32183
2018-12-23 16:31:09,401 INFO : valid_sample_misclass     0.46348
2018-12-23 16:31:09,401 INFO : test_sample_misclass      0.65335
2018-12-23 16:

2018-12-23 16:32:28,979 INFO : test_misclass             0.71181
2018-12-23 16:32:28,980 INFO : runtime                   8.83652
2018-12-23 16:32:28,980 INFO : 
2018-12-23 16:32:34,384 INFO : Time only for training updates: 4.71s
2018-12-23 16:32:37,841 INFO : Epoch 104
2018-12-23 16:32:37,842 INFO : train_loss                0.82142
2018-12-23 16:32:37,842 INFO : valid_loss                1.08467
2018-12-23 16:32:37,843 INFO : test_loss                 1.58495
2018-12-23 16:32:37,844 INFO : train_sample_misclass     0.31490
2018-12-23 16:32:37,844 INFO : valid_sample_misclass     0.43228
2018-12-23 16:32:37,845 INFO : test_sample_misclass      0.67537
2018-12-23 16:32:37,845 INFO : train_misclass            0.26343
2018-12-23 16:32:37,846 INFO : valid_misclass            0.37744
2018-12-23 16:32:37,846 INFO : test_misclass             0.68403
2018-12-23 16:32:37,846 INFO : runtime                   8.82752
2018-12-23 16:32:37,847 INFO : 
2018-12-23 16:32:43,252 INFO : Time only for t

2018-12-23 16:33:56,694 INFO : 
2018-12-23 16:33:56,697 INFO : New best valid_misclass: 0.259219
2018-12-23 16:33:56,697 INFO : 
2018-12-23 16:33:56,698 INFO : Last 10 epochs
2018-12-23 16:33:56,703 INFO : 
    train_loss  valid_loss  test_loss  train_sample_misclass  \
24    1.091612    0.989074   1.383522               0.454806   
25    0.925324    0.987286   1.391692               0.374460   
26    0.936481    1.120991   1.588933               0.386672   
27    0.921218    1.110733   1.536250               0.368836   
28    0.886930    1.069293   1.436028               0.346744   
29    0.909218    1.076363   1.493343               0.361742   
30    0.884272    1.008340   1.505118               0.352120   
31    0.909096    1.008340   1.505118               0.358087   
32    0.990711    0.954381   1.603118               0.422584   
33    0.943831    0.819932   1.486821               0.390280   

    valid_sample_misclass  test_sample_misclass  train_misclass  \
24               0.38

###  valid_misclass: 0.258134, test_misclass: 0.74826

In [12]:
leave_one_out_crop_run(5)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  2708.672 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 662665 

2018-12-24 12:33:51,236 INFO : valid_loss                1.13307
2018-12-24 12:33:51,237 INFO : test_loss                 2.19368
2018-12-24 12:33:51,237 INFO : train_sample_misclass     0.49802
2018-12-24 12:33:51,237 INFO : valid_sample_misclass     0.46055
2018-12-24 12:33:51,238 INFO : test_sample_misclass      0.71663
2018-12-24 12:33:51,238 INFO : train_misclass            0.46609
2018-12-24 12:33:51,239 INFO : valid_misclass            0.41540
2018-12-24 12:33:51,239 INFO : test_misclass             0.71875
2018-12-24 12:33:51,240 INFO : runtime                   8.85930
2018-12-24 12:33:51,240 INFO : 
2018-12-24 12:33:51,244 INFO : New best valid_misclass: 0.415401
2018-12-24 12:33:51,245 INFO : 
2018-12-24 12:33:56,635 INFO : Time only for training updates: 4.70s
2018-12-24 12:34:00,062 INFO : Epoch 4
2018-12-24 12:34:00,063 INFO : train_loss                1.14331
2018-12-24 12:34:00,063 INFO : valid_loss                1.05847
2018-12-24 12:34:00,064 INFO : test_loss        

2018-12-24 12:35:20,154 INFO : train_loss                0.93849
2018-12-24 12:35:20,155 INFO : valid_loss                1.03131
2018-12-24 12:35:20,155 INFO : test_loss                 1.79190
2018-12-24 12:35:20,156 INFO : train_sample_misclass     0.38424
2018-12-24 12:35:20,156 INFO : valid_sample_misclass     0.40653
2018-12-24 12:35:20,156 INFO : test_sample_misclass      0.71457
2018-12-24 12:35:20,157 INFO : train_misclass            0.31796
2018-12-24 12:35:20,158 INFO : valid_misclass            0.34599
2018-12-24 12:35:20,158 INFO : test_misclass             0.71701
2018-12-24 12:35:20,158 INFO : runtime                   8.97971
2018-12-24 12:35:20,159 INFO : 
2018-12-24 12:35:20,162 INFO : New best valid_misclass: 0.345987
2018-12-24 12:35:20,162 INFO : 
2018-12-24 12:35:25,595 INFO : Time only for training updates: 4.73s
2018-12-24 12:35:29,096 INFO : Epoch 14
2018-12-24 12:35:29,097 INFO : train_loss                0.94096
2018-12-24 12:35:29,098 INFO : valid_loss      

2018-12-24 12:36:49,340 INFO : train_sample_misclass     0.34307
2018-12-24 12:36:49,341 INFO : valid_sample_misclass     0.40436
2018-12-24 12:36:49,342 INFO : test_sample_misclass      0.73268
2018-12-24 12:36:49,342 INFO : train_misclass            0.28215
2018-12-24 12:36:49,342 INFO : valid_misclass            0.35249
2018-12-24 12:36:49,343 INFO : test_misclass             0.73611
2018-12-24 12:36:49,343 INFO : runtime                   8.87306
2018-12-24 12:36:49,344 INFO : 
2018-12-24 12:36:54,758 INFO : Time only for training updates: 4.71s
2018-12-24 12:36:58,186 INFO : Epoch 24
2018-12-24 12:36:58,186 INFO : train_loss                0.93020
2018-12-24 12:36:58,187 INFO : valid_loss                1.02747
2018-12-24 12:36:58,188 INFO : test_loss                 2.90220
2018-12-24 12:36:58,189 INFO : train_sample_misclass     0.39295
2018-12-24 12:36:58,189 INFO : valid_sample_misclass     0.40038
2018-12-24 12:36:58,189 INFO : test_sample_misclass      0.74906
2018-12-24 12:

2018-12-24 12:38:17,927 INFO : test_misclass             0.70833
2018-12-24 12:38:17,927 INFO : runtime                   8.85929
2018-12-24 12:38:17,927 INFO : 
2018-12-24 12:38:23,368 INFO : Time only for training updates: 4.74s
2018-12-24 12:38:26,801 INFO : Epoch 34
2018-12-24 12:38:26,802 INFO : train_loss                0.86457
2018-12-24 12:38:26,802 INFO : valid_loss                1.11027
2018-12-24 12:38:26,803 INFO : test_loss                 2.21923
2018-12-24 12:38:26,803 INFO : train_sample_misclass     0.34245
2018-12-24 12:38:26,803 INFO : valid_sample_misclass     0.41918
2018-12-24 12:38:26,804 INFO : test_sample_misclass      0.73137
2018-12-24 12:38:26,804 INFO : train_misclass            0.28812
2018-12-24 12:38:26,805 INFO : valid_misclass            0.38720
2018-12-24 12:38:26,806 INFO : test_misclass             0.73264
2018-12-24 12:38:26,807 INFO : runtime                   8.88726
2018-12-24 12:38:26,807 INFO : 
2018-12-24 12:38:32,220 INFO : Time only for tr

...

2018-12-24 12:41:23,958 INFO : train_misclass            0.24037
2018-12-24 12:41:23,958 INFO : valid_misclass            0.41215
2018-12-24 12:41:23,959 INFO : test_misclass             0.73264
2018-12-24 12:41:23,959 INFO : runtime                   8.84663
2018-12-24 12:41:23,959 INFO : 
2018-12-24 12:41:29,374 INFO : Time only for training updates: 4.72s
2018-12-24 12:41:32,806 INFO : Epoch 55
2018-12-24 12:41:32,807 INFO : train_loss                0.86219
2018-12-24 12:41:32,807 INFO : valid_loss                1.29134
2018-12-24 12:41:32,808 INFO : test_loss                 1.88969
2018-12-24 12:41:32,808 INFO : train_sample_misclass     0.34491
2018-12-24 12:41:32,809 INFO : valid_sample_misclass     0.47738
2018-12-24 12:41:32,809 INFO : test_sample_misclass      0.72756
2018-12-24 12:41:32,810 INFO : train_misclass            0.29870
2018-12-24 12:41:32,810 INFO : valid_misclass            0.47722
2018-12-24 12:41:32,811 INFO : test_misclass             0.72917
2018-12-24 12:

2018-12-24 12:42:58,151 INFO : Time only for training updates: 4.81s
2018-12-24 12:43:01,745 INFO : Epoch 65
2018-12-24 12:43:01,745 INFO : train_loss                0.84485
2018-12-24 12:43:01,746 INFO : valid_loss                1.20326
2018-12-24 12:43:01,747 INFO : test_loss                 2.12842
2018-12-24 12:43:01,747 INFO : train_sample_misclass     0.35986
2018-12-24 12:43:01,747 INFO : valid_sample_misclass     0.48132
2018-12-24 12:43:01,748 INFO : test_sample_misclass      0.73076
2018-12-24 12:43:01,748 INFO : train_misclass            0.32474
2018-12-24 12:43:01,748 INFO : valid_misclass            0.48048
2018-12-24 12:43:01,749 INFO : test_misclass             0.73438
2018-12-24 12:43:01,749 INFO : runtime                   9.00784
2018-12-24 12:43:01,750 INFO : 
2018-12-24 12:43:07,203 INFO : Time only for training updates: 4.74s
2018-12-24 12:43:10,632 INFO : Epoch 66
2018-12-24 12:43:10,633 INFO : train_loss                0.93486
2018-12-24 12:43:10,633 INFO : vali

2018-12-24 12:44:30,338 INFO : train_sample_misclass     0.30496
2018-12-24 12:44:30,338 INFO : valid_sample_misclass     0.44823
2018-12-24 12:44:30,339 INFO : test_sample_misclass      0.74001
2018-12-24 12:44:30,340 INFO : train_misclass            0.25068
2018-12-24 12:44:30,340 INFO : valid_misclass            0.43275
2018-12-24 12:44:30,340 INFO : test_misclass             0.74132
2018-12-24 12:44:30,341 INFO : runtime                   8.85057
2018-12-24 12:44:30,341 INFO : 
2018-12-24 12:44:35,755 INFO : Time only for training updates: 4.72s
2018-12-24 12:44:39,186 INFO : Epoch 76
2018-12-24 12:44:39,187 INFO : train_loss                0.83884
2018-12-24 12:44:39,187 INFO : valid_loss                1.13949
2018-12-24 12:44:39,187 INFO : test_loss                 2.80902
2018-12-24 12:44:39,188 INFO : train_sample_misclass     0.34543
2018-12-24 12:44:39,189 INFO : valid_sample_misclass     0.43034
2018-12-24 12:44:39,189 INFO : test_sample_misclass      0.74216
2018-12-24 12:

2018-12-24 12:45:58,947 INFO : test_misclass             0.75000
2018-12-24 12:45:58,948 INFO : runtime                   8.86505
2018-12-24 12:45:58,948 INFO : 
2018-12-24 12:46:04,371 INFO : Time only for training updates: 4.73s
2018-12-24 12:46:07,797 INFO : Epoch 86
2018-12-24 12:46:07,798 INFO : train_loss                0.78895
2018-12-24 12:46:07,798 INFO : valid_loss                1.29595
2018-12-24 12:46:07,799 INFO : test_loss                 3.12784
2018-12-24 12:46:07,800 INFO : train_sample_misclass     0.30154
2018-12-24 12:46:07,800 INFO : valid_sample_misclass     0.48224
2018-12-24 12:46:07,800 INFO : test_sample_misclass      0.73753
2018-12-24 12:46:07,801 INFO : train_misclass            0.24281
2018-12-24 12:46:07,801 INFO : valid_misclass            0.47180
2018-12-24 12:46:07,802 INFO : test_misclass             0.73611
2018-12-24 12:46:07,803 INFO : runtime                   8.85690
2018-12-24 12:46:07,803 INFO : 
2018-12-24 12:46:13,225 INFO : Time only for tr

2018-12-24 12:47:24,918 INFO : 
2018-12-24 12:47:31,715 INFO : Time only for training updates: 5.92s
2018-12-24 12:47:35,771 INFO : Epoch 16
2018-12-24 12:47:35,772 INFO : train_loss                0.95012
2018-12-24 12:47:35,772 INFO : valid_loss                0.81441
2018-12-24 12:47:35,773 INFO : test_loss                 2.60321
2018-12-24 12:47:35,774 INFO : train_sample_misclass     0.38647
2018-12-24 12:47:35,774 INFO : valid_sample_misclass     0.30871
2018-12-24 12:47:35,775 INFO : test_sample_misclass      0.74616
2018-12-24 12:47:35,775 INFO : train_misclass            0.34701
2018-12-24 12:47:35,775 INFO : valid_misclass            0.25813
2018-12-24 12:47:35,776 INFO : test_misclass             0.74826
2018-12-24 12:47:35,776 INFO : runtime                   10.87522
2018-12-24 12:47:35,776 INFO : 
2018-12-24 12:47:35,783 INFO : New best valid_misclass: 0.258134
2018-12-24 12:47:35,784 INFO : 
2018-12-24 12:47:35,784 INFO : Last 10 epochs
2018-12-24 12:47:35,789 INFO : 
 

###  valid_misclass: 0.292842, test_misclass: 0.71875

In [13]:
leave_one_out_crop_run(6)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-24 12:47:45,314 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-24 12:47:45,569 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-24 12:49:06,698 INFO : runtime                   0.00000
2018-12-24 12:49:06,698 INFO : 
2018-12-24 12:49:06,700 INFO : New best valid_misclass: 0.749458
2018-12-24 12:49:06,701 INFO : 
2018-12-24 12:49:12,104 INFO : Time only for training updates: 4.70s
2018-12-24 12:49:15,526 INFO : Epoch 1
2018-12-24 12:49:15,526 INFO : train_loss                1.25533
2018-12-24 12:49:15,527 INFO : valid_loss                1.24596
2018-12-24 12:49:15,528 INFO : test_loss                 1.62152
2018-12-24 12:49:15,528 INFO : train_sample_misclass     0.57031
2018-12-24 12:49:15,528 INFO : valid_sample_misclass     0.48348
2018-12-24 12:49:15,530 INFO : test_sample_misclass      0.74217
2018-12-24 12:49:15,530 INFO : train_misclass            0.55562
2018-12-24 12:49:15,530 INFO : valid_misclass            0.46638
2018-12-24 12:49:15,531 INFO : test_misclass             0.74479
2018-12-24 12:49:15,531 INFO : runtime                   8.88847
2018-12-24 12:49:15,532 INFO : 
2018-12-24 12:49

2018-12-24 12:50:35,235 INFO : test_misclass             0.71875
2018-12-24 12:50:35,236 INFO : runtime                   8.85839
2018-12-24 12:50:35,237 INFO : 
2018-12-24 12:50:40,648 INFO : Time only for training updates: 4.72s
2018-12-24 12:50:44,079 INFO : Epoch 11
2018-12-24 12:50:44,080 INFO : train_loss                0.99587
2018-12-24 12:50:44,081 INFO : valid_loss                1.20346
2018-12-24 12:50:44,082 INFO : test_loss                 2.31949
2018-12-24 12:50:44,082 INFO : train_sample_misclass     0.42114
2018-12-24 12:50:44,083 INFO : valid_sample_misclass     0.42205
2018-12-24 12:50:44,083 INFO : test_sample_misclass      0.73016
2018-12-24 12:50:44,084 INFO : train_misclass            0.37954
2018-12-24 12:50:44,084 INFO : valid_misclass            0.39154
2018-12-24 12:50:44,084 INFO : test_misclass             0.73438
2018-12-24 12:50:44,085 INFO : runtime                   8.84711
2018-12-24 12:50:44,085 INFO : 
2018-12-24 12:50:44,090 INFO : New best valid_m

2018-12-24 12:52:03,937 INFO : valid_misclass            0.42733
2018-12-24 12:52:03,937 INFO : test_misclass             0.70660
2018-12-24 12:52:03,937 INFO : runtime                   8.89550
2018-12-24 12:52:03,938 INFO : 
2018-12-24 12:52:09,368 INFO : Time only for training updates: 4.73s
2018-12-24 12:52:12,803 INFO : Epoch 21
2018-12-24 12:52:12,804 INFO : train_loss                0.90188
2018-12-24 12:52:12,804 INFO : valid_loss                1.29426
2018-12-24 12:52:12,805 INFO : test_loss                 2.36478
2018-12-24 12:52:12,806 INFO : train_sample_misclass     0.36764
2018-12-24 12:52:12,806 INFO : valid_sample_misclass     0.47963
2018-12-24 12:52:12,807 INFO : test_sample_misclass      0.71383
2018-12-24 12:52:12,807 INFO : train_misclass            0.30792
2018-12-24 12:52:12,807 INFO : valid_misclass            0.47939
2018-12-24 12:52:12,808 INFO : test_misclass             0.73264
2018-12-24 12:52:12,808 INFO : runtime                   8.87365
2018-12-24 12:

2018-12-24 12:53:41,592 INFO : Epoch 31
2018-12-24 12:53:41,592 INFO : train_loss                0.91967
2018-12-24 12:53:41,593 INFO : valid_loss                1.38099
2018-12-24 12:53:41,594 INFO : test_loss                 2.46309
2018-12-24 12:53:41,594 INFO : train_sample_misclass     0.37654
2018-12-24 12:53:41,595 INFO : valid_sample_misclass     0.50141
2018-12-24 12:53:41,595 INFO : test_sample_misclass      0.69854
2018-12-24 12:53:41,596 INFO : train_misclass            0.33180
2018-12-24 12:53:41,596 INFO : valid_misclass            0.49566
2018-12-24 12:53:41,596 INFO : test_misclass             0.71007
2018-12-24 12:53:41,597 INFO : runtime                   8.91366
2018-12-24 12:53:41,597 INFO : 
2018-12-24 12:53:47,036 INFO : Time only for training updates: 4.74s
2018-12-24 12:53:50,481 INFO : Epoch 32
2018-12-24 12:53:50,481 INFO : train_loss                0.89081
2018-12-24 12:53:50,482 INFO : valid_loss                1.09296
2018-12-24 12:53:50,483 INFO : test_los

...

2018-12-24 12:59:45,660 INFO : train_misclass            0.32881
2018-12-24 12:59:45,660 INFO : valid_misclass            0.53037
2018-12-24 12:59:45,661 INFO : test_misclass             0.71354
2018-12-24 12:59:45,661 INFO : runtime                   8.88073
2018-12-24 12:59:45,662 INFO : 
2018-12-24 12:59:51,108 INFO : Time only for training updates: 4.75s
2018-12-24 12:59:54,543 INFO : Epoch 73
2018-12-24 12:59:54,543 INFO : train_loss                0.83124
2018-12-24 12:59:54,544 INFO : valid_loss                1.31035
2018-12-24 12:59:54,544 INFO : test_loss                 2.05304
2018-12-24 12:59:54,545 INFO : train_sample_misclass     0.32571
2018-12-24 12:59:54,545 INFO : valid_sample_misclass     0.47837
2018-12-24 12:59:54,546 INFO : test_sample_misclass      0.67905
2018-12-24 12:59:54,546 INFO : train_misclass            0.27645
2018-12-24 12:59:54,547 INFO : valid_misclass            0.46963
2018-12-24 12:59:54,547 INFO : test_misclass             0.69444
2018-12-24 12:

2018-12-24 13:01:19,922 INFO : Time only for training updates: 4.73s
2018-12-24 13:01:23,360 INFO : Epoch 83
2018-12-24 13:01:23,360 INFO : train_loss                0.77918
2018-12-24 13:01:23,361 INFO : valid_loss                1.10551
2018-12-24 13:01:23,361 INFO : test_loss                 2.01805
2018-12-24 13:01:23,362 INFO : train_sample_misclass     0.29886
2018-12-24 13:01:23,362 INFO : valid_sample_misclass     0.41957
2018-12-24 13:01:23,363 INFO : test_sample_misclass      0.66316
2018-12-24 13:01:23,363 INFO : train_misclass            0.23793
2018-12-24 13:01:23,364 INFO : valid_misclass            0.40130
2018-12-24 13:01:23,364 INFO : test_misclass             0.66840
2018-12-24 13:01:23,365 INFO : runtime                   8.87513
2018-12-24 13:01:23,366 INFO : 
2018-12-24 13:01:28,796 INFO : Time only for training updates: 4.73s
2018-12-24 13:01:32,230 INFO : Epoch 84
2018-12-24 13:01:32,231 INFO : train_loss                0.92523
2018-12-24 13:01:32,231 INFO : vali

2018-12-24 13:02:52,180 INFO : train_sample_misclass     0.28601
2018-12-24 13:02:52,181 INFO : valid_sample_misclass     0.43620
2018-12-24 13:02:52,182 INFO : test_sample_misclass      0.67250
2018-12-24 13:02:52,183 INFO : train_misclass            0.22436
2018-12-24 13:02:52,183 INFO : valid_misclass            0.41974
2018-12-24 13:02:52,183 INFO : test_misclass             0.67535
2018-12-24 13:02:52,184 INFO : runtime                   8.88714
2018-12-24 13:02:52,184 INFO : 
2018-12-24 13:02:57,617 INFO : Time only for training updates: 4.73s
2018-12-24 13:03:01,059 INFO : Epoch 94
2018-12-24 13:03:01,059 INFO : train_loss                0.75822
2018-12-24 13:03:01,060 INFO : valid_loss                1.35300
2018-12-24 13:03:01,060 INFO : test_loss                 2.16717
2018-12-24 13:03:01,061 INFO : train_sample_misclass     0.28212
2018-12-24 13:03:01,062 INFO : valid_sample_misclass     0.49808
2018-12-24 13:03:01,062 INFO : test_sample_misclass      0.70880
2018-12-24 13:

2018-12-24 13:04:21,004 INFO : test_misclass             0.70833
2018-12-24 13:04:21,004 INFO : runtime                   8.87227
2018-12-24 13:04:21,005 INFO : 
2018-12-24 13:04:26,438 INFO : Time only for training updates: 4.73s
2018-12-24 13:04:29,879 INFO : Epoch 104
2018-12-24 13:04:29,879 INFO : train_loss                0.82293
2018-12-24 13:04:29,880 INFO : valid_loss                1.20036
2018-12-24 13:04:29,880 INFO : test_loss                 1.77116
2018-12-24 13:04:29,881 INFO : train_sample_misclass     0.32044
2018-12-24 13:04:29,882 INFO : valid_sample_misclass     0.45942
2018-12-24 13:04:29,882 INFO : test_sample_misclass      0.65179
2018-12-24 13:04:29,883 INFO : train_misclass            0.27075
2018-12-24 13:04:29,883 INFO : valid_misclass            0.44360
2018-12-24 13:04:29,884 INFO : test_misclass             0.66146
2018-12-24 13:04:29,884 INFO : runtime                   8.88063
2018-12-24 13:04:29,885 INFO : 
2018-12-24 13:04:35,318 INFO : Time only for t

2018-12-24 13:05:45,077 INFO : 
2018-12-24 13:05:51,870 INFO : Time only for training updates: 5.93s
2018-12-24 13:05:55,930 INFO : Epoch 34
2018-12-24 13:05:55,930 INFO : train_loss                0.92477
2018-12-24 13:05:55,931 INFO : valid_loss                0.87760
2018-12-24 13:05:55,931 INFO : test_loss                 1.81804
2018-12-24 13:05:55,932 INFO : train_sample_misclass     0.38136
2018-12-24 13:05:55,933 INFO : valid_sample_misclass     0.34222
2018-12-24 13:05:55,933 INFO : test_sample_misclass      0.68935
2018-12-24 13:05:55,934 INFO : train_misclass            0.33290
2018-12-24 13:05:55,934 INFO : valid_misclass            0.29284
2018-12-24 13:05:55,934 INFO : test_misclass             0.71875
2018-12-24 13:05:55,935 INFO : runtime                   10.89834
2018-12-24 13:05:55,935 INFO : 
2018-12-24 13:05:55,940 INFO : New best valid_misclass: 0.292842
2018-12-24 13:05:55,941 INFO : 
2018-12-24 13:05:55,942 INFO : Last 10 epochs
2018-12-24 13:05:55,946 INFO : 
 

###  valid_misclass: 0.206074, test_misclass: 0.72222

In [14]:
leave_one_out_crop_run(7)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-24 13:06:05,383 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-24 13:06:05,647 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-24 13:07:26,965 INFO : runtime                   0.00000
2018-12-24 13:07:26,966 INFO : 
2018-12-24 13:07:26,968 INFO : New best valid_misclass: 0.749458
2018-12-24 13:07:26,968 INFO : 
2018-12-24 13:07:32,369 INFO : Time only for training updates: 4.70s
2018-12-24 13:07:35,793 INFO : Epoch 1
2018-12-24 13:07:35,793 INFO : train_loss                1.26431
2018-12-24 13:07:35,794 INFO : valid_loss                1.14719
2018-12-24 13:07:35,794 INFO : test_loss                 1.39237
2018-12-24 13:07:35,794 INFO : train_sample_misclass     0.59035
2018-12-24 13:07:35,795 INFO : valid_sample_misclass     0.49784
2018-12-24 13:07:35,795 INFO : test_sample_misclass      0.67510
2018-12-24 13:07:35,796 INFO : train_misclass            0.57705
2018-12-24 13:07:35,796 INFO : valid_misclass            0.46529
2018-12-24 13:07:35,797 INFO : test_misclass             0.66840
2018-12-24 13:07:35,797 INFO : runtime                   8.88615
2018-12-24 13:07:35,797 INFO : 
2018-12-24 13:07

2018-12-24 13:08:55,472 INFO : test_misclass             0.67882
2018-12-24 13:08:55,473 INFO : runtime                   8.87619
2018-12-24 13:08:55,473 INFO : 
2018-12-24 13:09:00,887 INFO : Time only for training updates: 4.72s
2018-12-24 13:09:04,325 INFO : Epoch 11
2018-12-24 13:09:04,325 INFO : train_loss                1.07139
2018-12-24 13:09:04,326 INFO : valid_loss                1.09321
2018-12-24 13:09:04,327 INFO : test_loss                 1.30005
2018-12-24 13:09:04,327 INFO : train_sample_misclass     0.48135
2018-12-24 13:09:04,328 INFO : valid_sample_misclass     0.45735
2018-12-24 13:09:04,328 INFO : test_sample_misclass      0.61319
2018-12-24 13:09:04,328 INFO : train_misclass            0.44981
2018-12-24 13:09:04,329 INFO : valid_misclass            0.41215
2018-12-24 13:09:04,329 INFO : test_misclass             0.59722
2018-12-24 13:09:04,330 INFO : runtime                   8.85796
2018-12-24 13:09:04,331 INFO : 
2018-12-24 13:09:09,743 INFO : Time only for tr

2018-12-24 13:10:33,044 INFO : Epoch 21
2018-12-24 13:10:33,045 INFO : train_loss                1.00299
2018-12-24 13:10:33,046 INFO : valid_loss                1.18790
2018-12-24 13:10:33,046 INFO : test_loss                 1.52706
2018-12-24 13:10:33,047 INFO : train_sample_misclass     0.42188
2018-12-24 13:10:33,048 INFO : valid_sample_misclass     0.48764
2018-12-24 13:10:33,048 INFO : test_sample_misclass      0.70872
2018-12-24 13:10:33,048 INFO : train_misclass            0.38470
2018-12-24 13:10:33,049 INFO : valid_misclass            0.48807
2018-12-24 13:10:33,049 INFO : test_misclass             0.70312
2018-12-24 13:10:33,050 INFO : runtime                   8.89485
2018-12-24 13:10:33,050 INFO : 
2018-12-24 13:10:38,474 INFO : Time only for training updates: 4.73s
2018-12-24 13:10:41,908 INFO : Epoch 22
2018-12-24 13:10:41,909 INFO : train_loss                0.96224
2018-12-24 13:10:41,910 INFO : valid_loss                1.08519
2018-12-24 13:10:41,910 INFO : test_los

2018-12-24 13:12:01,805 INFO : train_sample_misclass     0.40207
2018-12-24 13:12:01,806 INFO : valid_sample_misclass     0.50198
2018-12-24 13:12:01,806 INFO : test_sample_misclass      0.67920
2018-12-24 13:12:01,807 INFO : train_misclass            0.35431
2018-12-24 13:12:01,807 INFO : valid_misclass            0.48915
2018-12-24 13:12:01,808 INFO : test_misclass             0.68576
2018-12-24 13:12:01,808 INFO : runtime                   8.87210
2018-12-24 13:12:01,808 INFO : 
2018-12-24 13:12:07,238 INFO : Time only for training updates: 4.73s
2018-12-24 13:12:10,675 INFO : Epoch 32
2018-12-24 13:12:10,675 INFO : train_loss                0.92308
2018-12-24 13:12:10,676 INFO : valid_loss                1.10113
2018-12-24 13:12:10,676 INFO : test_loss                 1.44141
2018-12-24 13:12:10,676 INFO : train_sample_misclass     0.37238
2018-12-24 13:12:10,677 INFO : valid_sample_misclass     0.43758
2018-12-24 13:12:10,678 INFO : test_sample_misclass      0.67165
2018-12-24 13:

...

2018-12-24 13:32:00,539 INFO : train_sample_misclass     0.34797
2018-12-24 13:32:00,540 INFO : valid_sample_misclass     0.39830
2018-12-24 13:32:00,540 INFO : test_sample_misclass      0.65926
2018-12-24 13:32:00,540 INFO : train_misclass            0.30982
2018-12-24 13:32:00,541 INFO : valid_misclass            0.35141
2018-12-24 13:32:00,541 INFO : test_misclass             0.66319
2018-12-24 13:32:00,542 INFO : runtime                   8.88913
2018-12-24 13:32:00,542 INFO : 
2018-12-24 13:32:05,977 INFO : Time only for training updates: 4.73s
2018-12-24 13:32:09,411 INFO : Epoch 167
2018-12-24 13:32:09,412 INFO : train_loss                0.79678
2018-12-24 13:32:09,412 INFO : valid_loss                1.13312
2018-12-24 13:32:09,413 INFO : test_loss                 1.38785
2018-12-24 13:32:09,413 INFO : train_sample_misclass     0.29821
2018-12-24 13:32:09,414 INFO : valid_sample_misclass     0.44007
2018-12-24 13:32:09,414 INFO : test_sample_misclass      0.62927
2018-12-24 13

2018-12-24 13:33:30,410 INFO : test_misclass             0.58160
2018-12-24 13:33:30,410 INFO : runtime                   9.00681
2018-12-24 13:33:30,411 INFO : 
2018-12-24 13:33:35,924 INFO : Time only for training updates: 4.81s
2018-12-24 13:33:39,406 INFO : Epoch 177
2018-12-24 13:33:39,407 INFO : train_loss                0.84855
2018-12-24 13:33:39,407 INFO : valid_loss                1.02792
2018-12-24 13:33:39,408 INFO : test_loss                 1.43302
2018-12-24 13:33:39,408 INFO : train_sample_misclass     0.33687
2018-12-24 13:33:39,408 INFO : valid_sample_misclass     0.39564
2018-12-24 13:33:39,409 INFO : test_sample_misclass      0.63292
2018-12-24 13:33:39,409 INFO : train_misclass            0.29707
2018-12-24 13:33:39,410 INFO : valid_misclass            0.35792
2018-12-24 13:33:39,411 INFO : test_misclass             0.62326
2018-12-24 13:33:39,411 INFO : runtime                   9.00929
2018-12-24 13:33:39,411 INFO : 
2018-12-24 13:33:44,885 INFO : Time only for t

2018-12-24 13:35:08,107 INFO : valid_loss                1.19144
2018-12-24 13:35:08,108 INFO : test_loss                 1.51047
2018-12-24 13:35:08,108 INFO : train_sample_misclass     0.33068
2018-12-24 13:35:08,109 INFO : valid_sample_misclass     0.46015
2018-12-24 13:35:08,110 INFO : test_sample_misclass      0.65499
2018-12-24 13:35:08,110 INFO : train_misclass            0.28757
2018-12-24 13:35:08,111 INFO : valid_misclass            0.46529
2018-12-24 13:35:08,111 INFO : test_misclass             0.65972
2018-12-24 13:35:08,112 INFO : runtime                   8.85913
2018-12-24 13:35:08,113 INFO : 
2018-12-24 13:35:13,534 INFO : Time only for training updates: 4.73s
2018-12-24 13:35:16,958 INFO : Epoch 188
2018-12-24 13:35:16,959 INFO : train_loss                0.90101
2018-12-24 13:35:16,960 INFO : valid_loss                1.16960
2018-12-24 13:35:16,960 INFO : test_loss                 1.32004
2018-12-24 13:35:16,961 INFO : train_sample_misclass     0.38649
2018-12-24 13

2018-12-24 13:36:36,798 INFO : train_misclass            0.29164
2018-12-24 13:36:36,798 INFO : valid_misclass            0.42950
2018-12-24 13:36:36,799 INFO : test_misclass             0.66146
2018-12-24 13:36:36,799 INFO : runtime                   8.88207
2018-12-24 13:36:36,800 INFO : 
2018-12-24 13:36:42,219 INFO : Time only for training updates: 4.73s
2018-12-24 13:36:45,648 INFO : Epoch 198
2018-12-24 13:36:45,649 INFO : train_loss                0.78251
2018-12-24 13:36:45,649 INFO : valid_loss                1.17434
2018-12-24 13:36:45,650 INFO : test_loss                 1.41891
2018-12-24 13:36:45,650 INFO : train_sample_misclass     0.28994
2018-12-24 13:36:45,650 INFO : valid_sample_misclass     0.44890
2018-12-24 13:36:45,651 INFO : test_sample_misclass      0.62777
2018-12-24 13:36:45,652 INFO : train_misclass            0.22355
2018-12-24 13:36:45,652 INFO : valid_misclass            0.41866
2018-12-24 13:36:45,653 INFO : test_misclass             0.60938
2018-12-24 13

2018-12-24 13:38:05,684 INFO : train_misclass            0.31185
2018-12-24 13:38:05,685 INFO : valid_misclass            0.25705
2018-12-24 13:38:05,686 INFO : test_misclass             0.68576
2018-12-24 13:38:05,686 INFO : runtime                   10.97440
2018-12-24 13:38:05,686 INFO : 
2018-12-24 13:38:05,690 INFO : New best valid_misclass: 0.257050
2018-12-24 13:38:05,691 INFO : 
2018-12-24 13:38:12,482 INFO : Time only for training updates: 5.92s
2018-12-24 13:38:16,527 INFO : Epoch 128
2018-12-24 13:38:16,528 INFO : train_loss                0.84134
2018-12-24 13:38:16,528 INFO : valid_loss                0.81741
2018-12-24 13:38:16,529 INFO : test_loss                 1.42816
2018-12-24 13:38:16,530 INFO : train_sample_misclass     0.33048
2018-12-24 13:38:16,530 INFO : valid_sample_misclass     0.33626
2018-12-24 13:38:16,531 INFO : test_sample_misclass      0.63841
2018-12-24 13:38:16,531 INFO : train_misclass            0.27756
2018-12-24 13:38:16,532 INFO : valid_misclass

###  valid_misclass: 0.341649, test_misclass: 0.55556

In [15]:
leave_one_out_crop_run(8)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-24 13:38:36,808 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-24 13:38:37,073 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-24 13:39:59,090 INFO : runtime                   0.00000
2018-12-24 13:39:59,091 INFO : 
2018-12-24 13:39:59,092 INFO : New best valid_misclass: 0.749458
2018-12-24 13:39:59,092 INFO : 
2018-12-24 13:40:04,488 INFO : Time only for training updates: 4.70s
2018-12-24 13:40:07,911 INFO : Epoch 1
2018-12-24 13:40:07,912 INFO : train_loss                1.29313
2018-12-24 13:40:07,912 INFO : valid_loss                1.27036
2018-12-24 13:40:07,913 INFO : test_loss                 1.19160
2018-12-24 13:40:07,914 INFO : train_sample_misclass     0.61083
2018-12-24 13:40:07,914 INFO : valid_sample_misclass     0.59251
2018-12-24 13:40:07,915 INFO : test_sample_misclass      0.53467
2018-12-24 13:40:07,915 INFO : train_misclass            0.59767
2018-12-24 13:40:07,916 INFO : valid_misclass            0.57809
2018-12-24 13:40:07,916 INFO : test_misclass             0.49653
2018-12-24 13:40:07,916 INFO : runtime                   8.87547
2018-12-24 13:40:07,917 INFO : 
2018-12-24 13:40

2018-12-24 13:41:27,468 INFO : valid_sample_misclass     0.51220
2018-12-24 13:41:27,469 INFO : test_sample_misclass      0.41374
2018-12-24 13:41:27,470 INFO : train_misclass            0.49050
2018-12-24 13:41:27,470 INFO : valid_misclass            0.48482
2018-12-24 13:41:27,471 INFO : test_misclass             0.36285
2018-12-24 13:41:27,471 INFO : runtime                   8.83899
2018-12-24 13:41:27,471 INFO : 
2018-12-24 13:41:27,475 INFO : New best valid_misclass: 0.484816
2018-12-24 13:41:27,475 INFO : 
2018-12-24 13:41:32,890 INFO : Time only for training updates: 4.72s
2018-12-24 13:41:36,309 INFO : Epoch 11
2018-12-24 13:41:36,309 INFO : train_loss                1.07830
2018-12-24 13:41:36,310 INFO : valid_loss                1.17223
2018-12-24 13:41:36,310 INFO : test_loss                 1.02323
2018-12-24 13:41:36,311 INFO : train_sample_misclass     0.46786
2018-12-24 13:41:36,311 INFO : valid_sample_misclass     0.49100
2018-12-24 13:41:36,312 INFO : test_sample_misc

2018-12-24 13:42:57,606 INFO : train_sample_misclass     0.47280
2018-12-24 13:42:57,606 INFO : valid_sample_misclass     0.51640
2018-12-24 13:42:57,607 INFO : test_sample_misclass      0.46770
2018-12-24 13:42:57,607 INFO : train_misclass            0.45090
2018-12-24 13:42:57,608 INFO : valid_misclass            0.48156
2018-12-24 13:42:57,609 INFO : test_misclass             0.43403
2018-12-24 13:42:57,609 INFO : runtime                   9.06782
2018-12-24 13:42:57,609 INFO : 
2018-12-24 13:43:03,199 INFO : Time only for training updates: 4.87s
2018-12-24 13:43:06,742 INFO : Epoch 21
2018-12-24 13:43:06,743 INFO : train_loss                1.03602
2018-12-24 13:43:06,743 INFO : valid_loss                1.26705
2018-12-24 13:43:06,744 INFO : test_loss                 1.40561
2018-12-24 13:43:06,744 INFO : train_sample_misclass     0.44086
2018-12-24 13:43:06,745 INFO : valid_sample_misclass     0.53555
2018-12-24 13:43:06,745 INFO : test_sample_misclass      0.60818
2018-12-24 13:

2018-12-24 13:44:28,119 INFO : train_misclass            0.30928
2018-12-24 13:44:28,120 INFO : valid_misclass            0.40672
2018-12-24 13:44:28,120 INFO : test_misclass             0.34201
2018-12-24 13:44:28,120 INFO : runtime                   9.09444
2018-12-24 13:44:28,121 INFO : 
2018-12-24 13:44:33,561 INFO : Time only for training updates: 4.73s
2018-12-24 13:44:37,000 INFO : Epoch 31
2018-12-24 13:44:37,001 INFO : train_loss                0.94085
2018-12-24 13:44:37,001 INFO : valid_loss                1.16601
2018-12-24 13:44:37,001 INFO : test_loss                 1.10101
2018-12-24 13:44:37,003 INFO : train_sample_misclass     0.38553
2018-12-24 13:44:37,003 INFO : valid_sample_misclass     0.49291
2018-12-24 13:44:37,003 INFO : test_sample_misclass      0.48233
2018-12-24 13:44:37,004 INFO : train_misclass            0.33234
2018-12-24 13:44:37,004 INFO : valid_misclass            0.44577
2018-12-24 13:44:37,005 INFO : test_misclass             0.46181
2018-12-24 13:

...

2018-12-24 13:49:03,970 INFO : test_misclass             0.37500
2018-12-24 13:49:03,971 INFO : runtime                   8.95919
2018-12-24 13:49:03,971 INFO : 
2018-12-24 13:49:09,406 INFO : Time only for training updates: 4.74s
2018-12-24 13:49:12,936 INFO : Epoch 62
2018-12-24 13:49:12,936 INFO : train_loss                0.91925
2018-12-24 13:49:12,936 INFO : valid_loss                1.18889
2018-12-24 13:49:12,937 INFO : test_loss                 1.08502
2018-12-24 13:49:12,937 INFO : train_sample_misclass     0.37396
2018-12-24 13:49:12,938 INFO : valid_sample_misclass     0.48701
2018-12-24 13:49:12,938 INFO : test_sample_misclass      0.42764
2018-12-24 13:49:12,938 INFO : train_misclass            0.33288
2018-12-24 13:49:12,939 INFO : valid_misclass            0.45119
2018-12-24 13:49:12,940 INFO : test_misclass             0.40278
2018-12-24 13:49:12,940 INFO : runtime                   8.88610
2018-12-24 13:49:12,940 INFO : 
2018-12-24 13:49:18,483 INFO : Time only for tr

2018-12-24 13:50:42,952 INFO : valid_loss                1.30183
2018-12-24 13:50:42,953 INFO : test_loss                 1.38482
2018-12-24 13:50:42,954 INFO : train_sample_misclass     0.38585
2018-12-24 13:50:42,954 INFO : valid_sample_misclass     0.53544
2018-12-24 13:50:42,955 INFO : test_sample_misclass      0.59353
2018-12-24 13:50:42,955 INFO : train_misclass            0.34211
2018-12-24 13:50:42,955 INFO : valid_misclass            0.51844
2018-12-24 13:50:42,955 INFO : test_misclass             0.62674
2018-12-24 13:50:42,956 INFO : runtime                   8.88458
2018-12-24 13:50:42,956 INFO : 
2018-12-24 13:50:48,385 INFO : Time only for training updates: 4.73s
2018-12-24 13:50:51,807 INFO : Epoch 73
2018-12-24 13:50:51,807 INFO : train_loss                0.87609
2018-12-24 13:50:51,808 INFO : valid_loss                1.21315
2018-12-24 13:50:51,808 INFO : test_loss                 0.99496
2018-12-24 13:50:51,809 INFO : train_sample_misclass     0.34585
2018-12-24 13:

2018-12-24 13:52:12,580 INFO : train_misclass            0.29327
2018-12-24 13:52:12,580 INFO : valid_misclass            0.45119
2018-12-24 13:52:12,581 INFO : test_misclass             0.38194
2018-12-24 13:52:12,581 INFO : runtime                   8.86769
2018-12-24 13:52:12,582 INFO : 
2018-12-24 13:52:18,004 INFO : Time only for training updates: 4.72s
2018-12-24 13:52:21,428 INFO : Epoch 83
2018-12-24 13:52:21,429 INFO : train_loss                0.86497
2018-12-24 13:52:21,429 INFO : valid_loss                1.11439
2018-12-24 13:52:21,430 INFO : test_loss                 1.04475
2018-12-24 13:52:21,430 INFO : train_sample_misclass     0.34323
2018-12-24 13:52:21,431 INFO : valid_sample_misclass     0.45113
2018-12-24 13:52:21,431 INFO : test_sample_misclass      0.43921
2018-12-24 13:52:21,432 INFO : train_misclass            0.29626
2018-12-24 13:52:21,433 INFO : valid_misclass            0.40456
2018-12-24 13:52:21,433 INFO : test_misclass             0.42014
2018-12-24 13:

2018-12-24 13:53:46,627 INFO : Time only for training updates: 4.73s
2018-12-24 13:53:50,056 INFO : Epoch 93
2018-12-24 13:53:50,057 INFO : train_loss                0.87392
2018-12-24 13:53:50,058 INFO : valid_loss                1.10712
2018-12-24 13:53:50,058 INFO : test_loss                 1.07140
2018-12-24 13:53:50,059 INFO : train_sample_misclass     0.36064
2018-12-24 13:53:50,059 INFO : valid_sample_misclass     0.45807
2018-12-24 13:53:50,059 INFO : test_sample_misclass      0.46147
2018-12-24 13:53:50,060 INFO : train_misclass            0.31606
2018-12-24 13:53:50,060 INFO : valid_misclass            0.39913
2018-12-24 13:53:50,061 INFO : test_misclass             0.44618
2018-12-24 13:53:50,061 INFO : runtime                   8.88117
2018-12-24 13:53:50,061 INFO : 
2018-12-24 13:53:55,491 INFO : Time only for training updates: 4.73s
2018-12-24 13:53:58,916 INFO : Epoch 94
2018-12-24 13:53:58,917 INFO : train_loss                0.82208
2018-12-24 13:53:58,918 INFO : vali

2018-12-24 13:55:18,673 INFO : train_sample_misclass     0.36024
2018-12-24 13:55:18,674 INFO : valid_sample_misclass     0.50066
2018-12-24 13:55:18,674 INFO : test_sample_misclass      0.47808
2018-12-24 13:55:18,675 INFO : train_misclass            0.31470
2018-12-24 13:55:18,676 INFO : valid_misclass            0.47180
2018-12-24 13:55:18,676 INFO : test_misclass             0.47049
2018-12-24 13:55:18,677 INFO : runtime                   8.85723
2018-12-24 13:55:18,677 INFO : 
2018-12-24 13:55:24,096 INFO : Time only for training updates: 4.72s
2018-12-24 13:55:27,521 INFO : Epoch 104
2018-12-24 13:55:27,522 INFO : train_loss                0.88750
2018-12-24 13:55:27,523 INFO : valid_loss                1.15031
2018-12-24 13:55:27,523 INFO : test_loss                 0.90709
2018-12-24 13:55:27,524 INFO : train_sample_misclass     0.35032
2018-12-24 13:55:27,524 INFO : valid_sample_misclass     0.47282
2018-12-24 13:55:27,525 INFO : test_sample_misclass      0.37453
2018-12-24 13

###  valid_misclass: 0.241866, test_misclass: 0.51042

In [16]:
leave_one_out_crop_run(9)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-24 13:55:51,964 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-24 13:55:52,227 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-24 13:57:13,343 INFO : runtime                   0.00000
2018-12-24 13:57:13,343 INFO : 
2018-12-24 13:57:13,345 INFO : New best valid_misclass: 0.749458
2018-12-24 13:57:13,345 INFO : 
2018-12-24 13:57:18,736 INFO : Time only for training updates: 4.70s
2018-12-24 13:57:22,152 INFO : Epoch 1
2018-12-24 13:57:22,152 INFO : train_loss                1.29315
2018-12-24 13:57:22,153 INFO : valid_loss                1.25264
2018-12-24 13:57:22,154 INFO : test_loss                 1.22006
2018-12-24 13:57:22,154 INFO : train_sample_misclass     0.61086
2018-12-24 13:57:22,155 INFO : valid_sample_misclass     0.57538
2018-12-24 13:57:22,155 INFO : test_sample_misclass      0.56214
2018-12-24 13:57:22,156 INFO : train_misclass            0.59767
2018-12-24 13:57:22,156 INFO : valid_misclass            0.54230
2018-12-24 13:57:22,156 INFO : test_misclass             0.55382
2018-12-24 13:57:22,157 INFO : runtime                   8.89473
2018-12-24 13:57:22,157 INFO : 
2018-12-24 13:57

2018-12-24 13:58:41,698 INFO : test_misclass             0.39931
2018-12-24 13:58:41,699 INFO : runtime                   8.83274
2018-12-24 13:58:41,699 INFO : 
2018-12-24 13:58:41,704 INFO : New best valid_misclass: 0.439262
2018-12-24 13:58:41,705 INFO : 
2018-12-24 13:58:47,108 INFO : Time only for training updates: 4.71s
2018-12-24 13:58:50,558 INFO : Epoch 11
2018-12-24 13:58:50,559 INFO : train_loss                1.06288
2018-12-24 13:58:50,560 INFO : valid_loss                1.10015
2018-12-24 13:58:50,561 INFO : test_loss                 1.17079
2018-12-24 13:58:50,561 INFO : train_sample_misclass     0.46104
2018-12-24 13:58:50,561 INFO : valid_sample_misclass     0.48793
2018-12-24 13:58:50,562 INFO : test_sample_misclass      0.47299
2018-12-24 13:58:50,563 INFO : train_misclass            0.41915
2018-12-24 13:58:50,563 INFO : valid_misclass            0.46638
2018-12-24 13:58:50,563 INFO : test_misclass             0.42882
2018-12-24 13:58:50,564 INFO : runtime         

2018-12-24 14:00:19,908 INFO : Epoch 21
2018-12-24 14:00:19,908 INFO : train_loss                1.04764
2018-12-24 14:00:19,909 INFO : valid_loss                1.33955
2018-12-24 14:00:19,910 INFO : test_loss                 1.35868
2018-12-24 14:00:19,911 INFO : train_sample_misclass     0.44759
2018-12-24 14:00:19,911 INFO : valid_sample_misclass     0.57977
2018-12-24 14:00:19,912 INFO : test_sample_misclass      0.55016
2018-12-24 14:00:19,912 INFO : train_misclass            0.41074
2018-12-24 14:00:19,912 INFO : valid_misclass            0.58894
2018-12-24 14:00:19,913 INFO : test_misclass             0.52604
2018-12-24 14:00:19,913 INFO : runtime                   9.01914
2018-12-24 14:00:19,914 INFO : 
2018-12-24 14:00:25,390 INFO : Time only for training updates: 4.77s
2018-12-24 14:00:28,881 INFO : Epoch 22
2018-12-24 14:00:28,881 INFO : train_loss                0.97577
2018-12-24 14:00:28,881 INFO : valid_loss                1.04442
2018-12-24 14:00:28,882 INFO : test_los

2018-12-24 14:01:50,166 INFO : valid_loss                1.10390
2018-12-24 14:01:50,167 INFO : test_loss                 1.22631
2018-12-24 14:01:50,167 INFO : train_sample_misclass     0.39869
2018-12-24 14:01:50,168 INFO : valid_sample_misclass     0.47785
2018-12-24 14:01:50,168 INFO : test_sample_misclass      0.50987
2018-12-24 14:01:50,169 INFO : train_misclass            0.35160
2018-12-24 14:01:50,169 INFO : valid_misclass            0.44143
2018-12-24 14:01:50,169 INFO : test_misclass             0.48438
2018-12-24 14:01:50,170 INFO : runtime                   9.14218
2018-12-24 14:01:50,170 INFO : 
2018-12-24 14:01:55,658 INFO : Time only for training updates: 4.79s
2018-12-24 14:01:59,266 INFO : Epoch 32
2018-12-24 14:01:59,267 INFO : train_loss                0.95336
2018-12-24 14:01:59,268 INFO : valid_loss                1.16736
2018-12-24 14:01:59,268 INFO : test_loss                 1.14096
2018-12-24 14:01:59,269 INFO : train_sample_misclass     0.39118
2018-12-24 14:

...

2018-12-24 14:37:24,765 INFO : test_misclass             0.48958
2018-12-24 14:37:24,765 INFO : runtime                   8.89765
2018-12-24 14:37:24,766 INFO : 
2018-12-24 14:37:30,224 INFO : Time only for training updates: 4.73s
2018-12-24 14:37:33,676 INFO : Epoch 270
2018-12-24 14:37:33,676 INFO : train_loss                0.78597
2018-12-24 14:37:33,677 INFO : valid_loss                0.99882
2018-12-24 14:37:33,677 INFO : test_loss                 1.33062
2018-12-24 14:37:33,677 INFO : train_sample_misclass     0.29296
2018-12-24 14:37:33,678 INFO : valid_sample_misclass     0.41691
2018-12-24 14:37:33,679 INFO : test_sample_misclass      0.50237
2018-12-24 14:37:33,680 INFO : train_misclass            0.23006
2018-12-24 14:37:33,680 INFO : valid_misclass            0.36334
2018-12-24 14:37:33,681 INFO : test_misclass             0.49132
2018-12-24 14:37:33,681 INFO : runtime                   8.91702
2018-12-24 14:37:33,681 INFO : 
2018-12-24 14:37:39,119 INFO : Time only for t

2018-12-24 14:39:02,627 INFO : valid_loss                1.05108
2018-12-24 14:39:02,628 INFO : test_loss                 1.42443
2018-12-24 14:39:02,628 INFO : train_sample_misclass     0.26676
2018-12-24 14:39:02,628 INFO : valid_sample_misclass     0.44546
2018-12-24 14:39:02,629 INFO : test_sample_misclass      0.50386
2018-12-24 14:39:02,629 INFO : train_misclass            0.20130
2018-12-24 14:39:02,630 INFO : valid_misclass            0.40672
2018-12-24 14:39:02,631 INFO : test_misclass             0.46181
2018-12-24 14:39:02,631 INFO : runtime                   8.88158
2018-12-24 14:39:02,631 INFO : 
2018-12-24 14:39:08,095 INFO : Time only for training updates: 4.74s
2018-12-24 14:39:11,546 INFO : Epoch 281
2018-12-24 14:39:11,546 INFO : train_loss                0.78150
2018-12-24 14:39:11,547 INFO : valid_loss                1.09060
2018-12-24 14:39:11,548 INFO : test_loss                 1.27278
2018-12-24 14:39:11,548 INFO : train_sample_misclass     0.27881
2018-12-24 14

2018-12-24 14:40:31,647 INFO : train_misclass            0.23467
2018-12-24 14:40:31,648 INFO : valid_misclass            0.36768
2018-12-24 14:40:31,648 INFO : test_misclass             0.52083
2018-12-24 14:40:31,649 INFO : runtime                   8.89586
2018-12-24 14:40:31,649 INFO : 
2018-12-24 14:40:37,085 INFO : Time only for training updates: 4.74s
2018-12-24 14:40:40,533 INFO : Epoch 291
2018-12-24 14:40:40,534 INFO : train_loss                0.79508
2018-12-24 14:40:40,535 INFO : valid_loss                1.07231
2018-12-24 14:40:40,536 INFO : test_loss                 1.29643
2018-12-24 14:40:40,537 INFO : train_sample_misclass     0.29257
2018-12-24 14:40:40,537 INFO : valid_sample_misclass     0.45459
2018-12-24 14:40:40,538 INFO : test_sample_misclass      0.50172
2018-12-24 14:40:40,538 INFO : train_misclass            0.23386
2018-12-24 14:40:40,539 INFO : valid_misclass            0.41866
2018-12-24 14:40:40,539 INFO : test_misclass             0.49479
2018-12-24 14

2018-12-24 14:42:06,098 INFO : Time only for training updates: 4.73s
2018-12-24 14:42:09,545 INFO : Epoch 301
2018-12-24 14:42:09,546 INFO : train_loss                0.77909
2018-12-24 14:42:09,547 INFO : valid_loss                1.00535
2018-12-24 14:42:09,548 INFO : test_loss                 1.24578
2018-12-24 14:42:09,548 INFO : train_sample_misclass     0.28774
2018-12-24 14:42:09,548 INFO : valid_sample_misclass     0.42591
2018-12-24 14:42:09,549 INFO : test_sample_misclass      0.47785
2018-12-24 14:42:09,549 INFO : train_misclass            0.22626
2018-12-24 14:42:09,550 INFO : valid_misclass            0.38720
2018-12-24 14:42:09,551 INFO : test_misclass             0.45833
2018-12-24 14:42:09,551 INFO : runtime                   8.89318
2018-12-24 14:42:09,552 INFO : 
2018-12-24 14:42:14,991 INFO : Time only for training updates: 4.74s
2018-12-24 14:42:18,435 INFO : Epoch 302
2018-12-24 14:42:18,436 INFO : train_loss                0.82474
2018-12-24 14:42:18,436 INFO : va

2018-12-24 14:43:38,570 INFO : train_sample_misclass     0.28972
2018-12-24 14:43:38,570 INFO : valid_sample_misclass     0.45111
2018-12-24 14:43:38,570 INFO : test_sample_misclass      0.48543
2018-12-24 14:43:38,571 INFO : train_misclass            0.22680
2018-12-24 14:43:38,571 INFO : valid_misclass            0.43384
2018-12-24 14:43:38,572 INFO : test_misclass             0.44444
2018-12-24 14:43:38,572 INFO : runtime                   8.89731
2018-12-24 14:43:38,572 INFO : 
2018-12-24 14:43:44,016 INFO : Time only for training updates: 4.74s
2018-12-24 14:43:47,458 INFO : Epoch 312
2018-12-24 14:43:47,459 INFO : train_loss                0.88291
2018-12-24 14:43:47,459 INFO : valid_loss                1.07483
2018-12-24 14:43:47,460 INFO : test_loss                 1.27614
2018-12-24 14:43:47,460 INFO : train_sample_misclass     0.34782
2018-12-24 14:43:47,461 INFO : valid_sample_misclass     0.44682
2018-12-24 14:43:47,462 INFO : test_sample_misclass      0.48965
2018-12-24 14

In [11]:
def leave_one_out_crop__deep_run(out):
    subjects_list = [i for i in range(1, 10)]
    subjects_list.remove(out)
    train_data = load_train_data(subjects_list)
    test_data = load_subject_data(out)

    logging.basicConfig(format='%(asctime)s %(levelname)s : %(message)s',
                            level=logging.DEBUG, stream=sys.stdout)
    cuda = True
    exp = run_crop_exp(train_data, test_data, low_cut_hz, "deep", cuda)
    log.info("Last 10 epochs")
    log.info("\n" + str(exp.epochs_df.iloc[-10:]))

###  valid_misclass: 0.099783, test_misclass: 0.24479

In [19]:
leave_one_out_crop__deep_run(1)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  2708.672 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 662665  =      0.000 ...  2650.660 secs...
2018-12-24 14:46:29,984 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
2018-12-24 14:46:30,248 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  26

2018-12-24 14:47:52,216 INFO : Run until first stop...
2018-12-24 14:47:56,619 INFO : Epoch 0
2018-12-24 14:47:56,620 INFO : train_loss                1.38738
2018-12-24 14:47:56,620 INFO : valid_loss                1.38781
2018-12-24 14:47:56,621 INFO : test_loss                 1.38467
2018-12-24 14:47:56,621 INFO : train_sample_misclass     0.74873
2018-12-24 14:47:56,622 INFO : valid_sample_misclass     0.74823
2018-12-24 14:47:56,622 INFO : test_sample_misclass      0.73086
2018-12-24 14:47:56,623 INFO : train_misclass            0.74932
2018-12-24 14:47:56,624 INFO : valid_misclass            0.73753
2018-12-24 14:47:56,624 INFO : test_misclass             0.68750
2018-12-24 14:47:56,624 INFO : runtime                   0.00000
2018-12-24 14:47:56,625 INFO : 
2018-12-24 14:47:56,630 INFO : New best valid_misclass: 0.737527
2018-12-24 14:47:56,630 INFO : 
2018-12-24 14:48:04,553 INFO : Time only for training updates: 7.21s
2018-12-24 14:48:08,863 INFO : Epoch 1
2018-12-24 14:48:08

2018-12-24 14:49:47,566 INFO : 
2018-12-24 14:49:47,571 INFO : New best valid_misclass: 0.379610
2018-12-24 14:49:47,572 INFO : 
2018-12-24 14:49:55,568 INFO : Time only for training updates: 7.28s
2018-12-24 14:49:59,905 INFO : Epoch 10
2018-12-24 14:49:59,906 INFO : train_loss                1.12364
2018-12-24 14:49:59,907 INFO : valid_loss                1.17559
2018-12-24 14:49:59,908 INFO : test_loss                 1.03917
2018-12-24 14:49:59,908 INFO : train_sample_misclass     0.49746
2018-12-24 14:49:59,909 INFO : valid_sample_misclass     0.49491
2018-12-24 14:49:59,909 INFO : test_sample_misclass      0.44575
2018-12-24 14:49:59,910 INFO : train_misclass            0.44927
2018-12-24 14:49:59,910 INFO : valid_misclass            0.44360
2018-12-24 14:49:59,910 INFO : test_misclass             0.42188
2018-12-24 14:49:59,911 INFO : runtime                   12.33731
2018-12-24 14:49:59,911 INFO : 
2018-12-24 14:50:07,912 INFO : Time only for training updates: 7.28s
2018-12-24

2018-12-24 14:52:03,340 INFO : valid_loss                1.15199
2018-12-24 14:52:03,341 INFO : test_loss                 0.86306
2018-12-24 14:52:03,341 INFO : train_sample_misclass     0.40667
2018-12-24 14:52:03,341 INFO : valid_sample_misclass     0.46804
2018-12-24 14:52:03,342 INFO : test_sample_misclass      0.39583
2018-12-24 14:52:03,342 INFO : train_misclass            0.35241
2018-12-24 14:52:03,343 INFO : valid_misclass            0.42842
2018-12-24 14:52:03,343 INFO : test_misclass             0.36632
2018-12-24 14:52:03,343 INFO : runtime                   12.34158
2018-12-24 14:52:03,344 INFO : 
2018-12-24 14:52:11,336 INFO : Time only for training updates: 7.28s
2018-12-24 14:52:15,675 INFO : Epoch 21
2018-12-24 14:52:15,676 INFO : train_loss                0.96541
2018-12-24 14:52:15,676 INFO : valid_loss                1.15574
2018-12-24 14:52:15,677 INFO : test_loss                 0.89339
2018-12-24 14:52:15,677 INFO : train_sample_misclass     0.41759
2018-12-24 14

2018-12-24 14:54:06,800 INFO : valid_sample_misclass     0.47035
2018-12-24 14:54:06,800 INFO : test_sample_misclass      0.40009
2018-12-24 14:54:06,801 INFO : train_misclass            0.31769
2018-12-24 14:54:06,801 INFO : valid_misclass            0.42408
2018-12-24 14:54:06,802 INFO : test_misclass             0.37847
2018-12-24 14:54:06,802 INFO : runtime                   12.33593
2018-12-24 14:54:06,802 INFO : 
2018-12-24 14:54:14,789 INFO : Time only for training updates: 7.27s
2018-12-24 14:54:19,131 INFO : Epoch 31
2018-12-24 14:54:19,131 INFO : train_loss                0.87136
2018-12-24 14:54:19,132 INFO : valid_loss                1.15098
2018-12-24 14:54:19,132 INFO : test_loss                 0.87606
2018-12-24 14:54:19,133 INFO : train_sample_misclass     0.35598
2018-12-24 14:54:19,133 INFO : valid_sample_misclass     0.43492
2018-12-24 14:54:19,134 INFO : test_sample_misclass      0.36844
2018-12-24 14:54:19,135 INFO : train_misclass            0.29381
2018-12-24 14

...

2018-12-24 15:32:30,225 INFO : train_misclass            0.10852
2018-12-24 15:32:30,226 INFO : valid_misclass            0.36876
2018-12-24 15:32:30,226 INFO : test_misclass             0.27778
2018-12-24 15:32:30,226 INFO : runtime                   12.38165
2018-12-24 15:32:30,227 INFO : 
2018-12-24 15:32:38,255 INFO : Time only for training updates: 7.31s
2018-12-24 15:32:42,606 INFO : Epoch 217
2018-12-24 15:32:42,606 INFO : train_loss                0.50583
2018-12-24 15:32:42,607 INFO : valid_loss                1.09608
2018-12-24 15:32:42,607 INFO : test_loss                 0.82372
2018-12-24 15:32:42,608 INFO : train_sample_misclass     0.17187
2018-12-24 15:32:42,608 INFO : valid_sample_misclass     0.42644
2018-12-24 15:32:42,608 INFO : test_sample_misclass      0.34178
2018-12-24 15:32:42,609 INFO : train_misclass            0.09658
2018-12-24 15:32:42,610 INFO : valid_misclass            0.37310
2018-12-24 15:32:42,610 INFO : test_misclass             0.28993
2018-12-24 1

2018-12-24 15:34:42,188 INFO : Time only for training updates: 7.32s
2018-12-24 15:34:46,543 INFO : Epoch 227
2018-12-24 15:34:46,544 INFO : train_loss                0.48291
2018-12-24 15:34:46,544 INFO : valid_loss                1.24228
2018-12-24 15:34:46,545 INFO : test_loss                 0.88955
2018-12-24 15:34:46,545 INFO : train_sample_misclass     0.17063
2018-12-24 15:34:46,546 INFO : valid_sample_misclass     0.43781
2018-12-24 15:34:46,546 INFO : test_sample_misclass      0.35101
2018-12-24 15:34:46,547 INFO : train_misclass            0.10174
2018-12-24 15:34:46,547 INFO : valid_misclass            0.39588
2018-12-24 15:34:46,547 INFO : test_misclass             0.31076
2018-12-24 15:34:46,548 INFO : runtime                   12.38649
2018-12-24 15:34:46,548 INFO : 
2018-12-24 15:34:54,574 INFO : Time only for training updates: 7.31s
2018-12-24 15:34:58,922 INFO : Epoch 228
2018-12-24 15:34:58,922 INFO : train_loss                0.48843
2018-12-24 15:34:58,923 INFO : v

2018-12-24 15:36:50,493 INFO : train_sample_misclass     0.17100
2018-12-24 15:36:50,494 INFO : valid_sample_misclass     0.43329
2018-12-24 15:36:50,494 INFO : test_sample_misclass      0.35283
2018-12-24 15:36:50,494 INFO : train_misclass            0.10689
2018-12-24 15:36:50,495 INFO : valid_misclass            0.37310
2018-12-24 15:36:50,495 INFO : test_misclass             0.29167
2018-12-24 15:36:50,496 INFO : runtime                   12.38649
2018-12-24 15:36:50,496 INFO : 
2018-12-24 15:36:58,529 INFO : Time only for training updates: 7.32s
2018-12-24 15:37:02,881 INFO : Epoch 238
2018-12-24 15:37:02,882 INFO : train_loss                0.54072
2018-12-24 15:37:02,882 INFO : valid_loss                1.19679
2018-12-24 15:37:02,883 INFO : test_loss                 0.95498
2018-12-24 15:37:02,884 INFO : train_sample_misclass     0.19892
2018-12-24 15:37:02,884 INFO : valid_sample_misclass     0.44306
2018-12-24 15:37:02,885 INFO : test_sample_misclass      0.34959
2018-12-24 1

2018-12-24 15:38:52,889 INFO : train_sample_misclass     0.21618
2018-12-24 15:38:52,889 INFO : valid_sample_misclass     0.25830
2018-12-24 15:38:52,890 INFO : test_sample_misclass      0.34305
2018-12-24 15:38:52,890 INFO : train_misclass            0.14648
2018-12-24 15:38:52,891 INFO : valid_misclass            0.17679
2018-12-24 15:38:52,891 INFO : test_misclass             0.31250
2018-12-24 15:38:52,892 INFO : runtime                   15.18503
2018-12-24 15:38:52,892 INFO : 
2018-12-24 15:38:52,898 INFO : New best valid_misclass: 0.176790
2018-12-24 15:38:52,898 INFO : 
2018-12-24 15:39:02,944 INFO : Time only for training updates: 9.16s
2018-12-24 15:39:08,107 INFO : Epoch 168
2018-12-24 15:39:08,108 INFO : train_loss                0.59426
2018-12-24 15:39:08,108 INFO : valid_loss                0.65604
2018-12-24 15:39:08,109 INFO : test_loss                 0.83573
2018-12-24 15:39:08,109 INFO : train_sample_misclass     0.22764
2018-12-24 15:39:08,111 INFO : valid_sample_m

2018-12-24 15:41:09,766 INFO : New best valid_misclass: 0.125813
2018-12-24 15:41:09,767 INFO : 
2018-12-24 15:41:19,888 INFO : Time only for training updates: 9.21s
2018-12-24 15:41:25,010 INFO : Epoch 177
2018-12-24 15:41:25,011 INFO : train_loss                0.66323
2018-12-24 15:41:25,011 INFO : valid_loss                0.69924
2018-12-24 15:41:25,012 INFO : test_loss                 0.79218
2018-12-24 15:41:25,012 INFO : train_sample_misclass     0.26111
2018-12-24 15:41:25,013 INFO : valid_sample_misclass     0.27755
2018-12-24 15:41:25,014 INFO : test_sample_misclass      0.32841
2018-12-24 15:41:25,014 INFO : train_misclass            0.20356
2018-12-24 15:41:25,014 INFO : valid_misclass            0.22234
2018-12-24 15:41:25,015 INFO : test_misclass             0.29688
2018-12-24 15:41:25,015 INFO : runtime                   15.32767
2018-12-24 15:41:25,016 INFO : 
2018-12-24 15:41:35,203 INFO : Time only for training updates: 9.29s
2018-12-24 15:41:40,386 INFO : Epoch 178


###  valid_misclass: 0.080260, test_misclass: 0.74653

In [ ]:
leave_one_out_crop__deep_run(2)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-24 15:41:49,877 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-24 15:41:50,136 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  26

2018-12-24 15:43:08,190 INFO : Run until first stop...
2018-12-24 15:43:12,582 INFO : Epoch 0
2018-12-24 15:43:12,582 INFO : train_loss                1.38687
2018-12-24 15:43:12,583 INFO : valid_loss                1.38781
2018-12-24 15:43:12,584 INFO : test_loss                 1.38794
2018-12-24 15:43:12,584 INFO : train_sample_misclass     0.74560
2018-12-24 15:43:12,584 INFO : valid_sample_misclass     0.74823
2018-12-24 15:43:12,585 INFO : test_sample_misclass      0.75091
2018-12-24 15:43:12,586 INFO : train_misclass            0.73630
2018-12-24 15:43:12,586 INFO : valid_misclass            0.73753
2018-12-24 15:43:12,586 INFO : test_misclass             0.77083
2018-12-24 15:43:12,587 INFO : runtime                   0.00000
2018-12-24 15:43:12,587 INFO : 
2018-12-24 15:43:12,593 INFO : New best valid_misclass: 0.737527
2018-12-24 15:43:12,594 INFO : 
2018-12-24 15:43:20,518 INFO : Time only for training updates: 7.22s
2018-12-24 15:43:24,852 INFO : Epoch 1
2018-12-24 15:43:24

2018-12-24 15:45:03,591 INFO : 
2018-12-24 15:45:03,597 INFO : New best valid_misclass: 0.427332
2018-12-24 15:45:03,597 INFO : 
2018-12-24 15:45:11,591 INFO : Time only for training updates: 7.28s
2018-12-24 15:45:15,936 INFO : Epoch 10
2018-12-24 15:45:15,936 INFO : train_loss                0.98197
2018-12-24 15:45:15,937 INFO : valid_loss                1.13731
2018-12-24 15:45:15,937 INFO : test_loss                 1.73344
2018-12-24 15:45:15,938 INFO : train_sample_misclass     0.42108
2018-12-24 15:45:15,938 INFO : valid_sample_misclass     0.47566
2018-12-24 15:45:15,939 INFO : test_sample_misclass      0.72761
2018-12-24 15:45:15,939 INFO : train_misclass            0.36679
2018-12-24 15:45:15,939 INFO : valid_misclass            0.41540
2018-12-24 15:45:15,940 INFO : test_misclass             0.72743
2018-12-24 15:45:15,940 INFO : runtime                   12.34854
2018-12-24 15:45:15,941 INFO : 
2018-12-24 15:45:15,950 INFO : New best valid_misclass: 0.415401
2018-12-24 15:

2018-12-24 15:47:07,101 INFO : runtime                   12.32945
2018-12-24 15:47:07,101 INFO : 
2018-12-24 15:47:15,096 INFO : Time only for training updates: 7.28s
2018-12-24 15:47:19,436 INFO : Epoch 20
2018-12-24 15:47:19,437 INFO : train_loss                0.91723
2018-12-24 15:47:19,438 INFO : valid_loss                1.18202
2018-12-24 15:47:19,438 INFO : test_loss                 2.59757
2018-12-24 15:47:19,439 INFO : train_sample_misclass     0.39158
2018-12-24 15:47:19,439 INFO : valid_sample_misclass     0.45838
2018-12-24 15:47:19,439 INFO : test_sample_misclass      0.73216
2018-12-24 15:47:19,440 INFO : train_misclass            0.35241
2018-12-24 15:47:19,441 INFO : valid_misclass            0.41323
2018-12-24 15:47:19,441 INFO : test_misclass             0.72569
2018-12-24 15:47:19,441 INFO : runtime                   12.37308
2018-12-24 15:47:19,442 INFO : 
2018-12-24 15:47:27,431 INFO : Time only for training updates: 7.28s
2018-12-24 15:47:31,777 INFO : Epoch 21
2

2018-12-24 15:49:22,925 INFO : test_loss                 2.37697
2018-12-24 15:49:22,926 INFO : train_sample_misclass     0.30333
2018-12-24 15:49:22,926 INFO : valid_sample_misclass     0.45192
2018-12-24 15:49:22,926 INFO : test_sample_misclass      0.74217
2018-12-24 15:49:22,927 INFO : train_misclass            0.23440
2018-12-24 15:49:22,927 INFO : valid_misclass            0.40347
2018-12-24 15:49:22,928 INFO : test_misclass             0.73090
2018-12-24 15:49:22,928 INFO : runtime                   12.34833
2018-12-24 15:49:22,929 INFO : 
2018-12-24 15:49:30,916 INFO : Time only for training updates: 7.28s
2018-12-24 15:49:35,261 INFO : Epoch 31
2018-12-24 15:49:35,261 INFO : train_loss                0.74032
2018-12-24 15:49:35,262 INFO : valid_loss                1.13039
2018-12-24 15:49:35,263 INFO : test_loss                 2.40696
2018-12-24 15:49:35,264 INFO : train_sample_misclass     0.30396
2018-12-24 15:49:35,264 INFO : valid_sample_misclass     0.41618
2018-12-24 15

...

2018-12-24 16:36:13,733 INFO : valid_loss                1.14053
2018-12-24 16:36:13,733 INFO : test_loss                 2.84333
2018-12-24 16:36:13,734 INFO : train_sample_misclass     0.13021
2018-12-24 16:36:13,734 INFO : valid_sample_misclass     0.42881
2018-12-24 16:36:13,735 INFO : test_sample_misclass      0.74365
2018-12-24 16:36:13,736 INFO : train_misclass            0.06701
2018-12-24 16:36:13,736 INFO : valid_misclass            0.36009
2018-12-24 16:36:13,736 INFO : test_misclass             0.74479
2018-12-24 16:36:13,737 INFO : runtime                   12.39839
2018-12-24 16:36:13,737 INFO : 
2018-12-24 16:36:21,765 INFO : Time only for training updates: 7.32s
2018-12-24 16:36:26,128 INFO : Epoch 258
2018-12-24 16:36:26,128 INFO : train_loss                0.44604
2018-12-24 16:36:26,129 INFO : valid_loss                1.22922
2018-12-24 16:36:26,129 INFO : test_loss                 3.09603
2018-12-24 16:36:26,130 INFO : train_sample_misclass     0.17257
2018-12-24 1

2018-12-24 16:38:17,762 INFO : train_misclass            0.06891
2018-12-24 16:38:17,762 INFO : valid_misclass            0.31779
2018-12-24 16:38:17,763 INFO : test_misclass             0.74479
2018-12-24 16:38:17,763 INFO : runtime                   12.39637
2018-12-24 16:38:17,764 INFO : 
2018-12-24 16:38:17,764 INFO : Setup for second stop...
2018-12-24 16:38:17,771 INFO : Train loss to reach 0.45327
2018-12-24 16:38:17,772 INFO : Run until second stop...
2018-12-24 16:38:22,981 INFO : Epoch 188
2018-12-24 16:38:22,982 INFO : train_loss                0.57377
2018-12-24 16:38:22,982 INFO : valid_loss                1.05551
2018-12-24 16:38:22,982 INFO : test_loss                 2.44806
2018-12-24 16:38:22,984 INFO : train_sample_misclass     0.20652
2018-12-24 16:38:22,984 INFO : valid_sample_misclass     0.38162
2018-12-24 16:38:22,984 INFO : test_sample_misclass      0.71686
2018-12-24 16:38:22,985 INFO : train_misclass            0.13954
2018-12-24 16:38:22,985 INFO : valid_mis

2018-12-24 16:40:39,865 INFO : train_sample_misclass     0.21572
2018-12-24 16:40:39,866 INFO : valid_sample_misclass     0.24232
2018-12-24 16:40:39,866 INFO : test_sample_misclass      0.74072
2018-12-24 16:40:39,866 INFO : train_misclass            0.15625
2018-12-24 16:40:39,867 INFO : valid_misclass            0.17679
2018-12-24 16:40:39,868 INFO : test_misclass             0.74653
2018-12-24 16:40:39,868 INFO : runtime                   15.22120
2018-12-24 16:40:39,868 INFO : 
2018-12-24 16:40:49,920 INFO : Time only for training updates: 9.16s
2018-12-24 16:40:55,060 INFO : Epoch 198
2018-12-24 16:40:55,061 INFO : train_loss                0.50764
2018-12-24 16:40:55,062 INFO : valid_loss                0.56053
2018-12-24 16:40:55,062 INFO : test_loss                 2.49411
2018-12-24 16:40:55,063 INFO : train_sample_misclass     0.19415
2018-12-24 16:40:55,064 INFO : valid_sample_misclass     0.21263
2018-12-24 16:40:55,064 INFO : test_sample_misclass      0.76348
2018-12-24 1

2018-12-24 16:43:11,984 INFO : test_loss                 2.34866
2018-12-24 16:43:11,985 INFO : train_sample_misclass     0.20050
2018-12-24 16:43:11,985 INFO : valid_sample_misclass     0.21458
2018-12-24 16:43:11,986 INFO : test_sample_misclass      0.72510
2018-12-24 16:43:11,987 INFO : train_misclass            0.13845
2018-12-24 16:43:11,988 INFO : valid_misclass            0.13124
2018-12-24 16:43:11,988 INFO : test_misclass             0.72222
2018-12-24 16:43:11,989 INFO : runtime                   15.22425
2018-12-24 16:43:11,989 INFO : 
2018-12-24 16:43:22,035 INFO : Time only for training updates: 9.16s
2018-12-24 16:43:27,172 INFO : Epoch 208
2018-12-24 16:43:27,172 INFO : train_loss                0.49091
2018-12-24 16:43:27,173 INFO : valid_loss                0.52598
2018-12-24 16:43:27,174 INFO : test_loss                 2.59881
2018-12-24 16:43:27,174 INFO : train_sample_misclass     0.17959
2018-12-24 16:43:27,175 INFO : valid_sample_misclass     0.20431
2018-12-24 1

2018-12-24 16:45:44,033 INFO : test_sample_misclass      0.74667
2018-12-24 16:45:44,033 INFO : train_misclass            0.10395
2018-12-24 16:45:44,034 INFO : valid_misclass            0.08026
2018-12-24 16:45:44,034 INFO : test_misclass             0.74653
2018-12-24 16:45:44,035 INFO : runtime                   15.23164
2018-12-24 16:45:44,035 INFO : 
2018-12-24 16:45:44,042 INFO : New best valid_misclass: 0.080260
2018-12-24 16:45:44,042 INFO : 
2018-12-24 16:45:44,043 INFO : Last 10 epochs
2018-12-24 16:45:44,049 INFO : 
     train_loss  valid_loss  test_loss  train_sample_misclass  \
208    0.490910    0.525979   2.598809               0.179590   
209    0.525752    0.544490   3.297720               0.203511   
210    0.483268    0.552007   2.826874               0.177101   
211    0.517615    0.541756   2.634793               0.201060   
212    0.528291    0.522154   2.438313               0.210207   
213    0.489755    0.481884   2.725853               0.186056   
214    0.508

###  valid_misclass: 0.106291 test_misclass: 0.38368

In [12]:
leave_one_out_crop__deep_run(3)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  2708.672 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 662665 

2018-12-24 18:32:36,576 INFO : 
2018-12-24 18:32:36,582 INFO : New best valid_misclass: 0.671367
2018-12-24 18:32:36,582 INFO : 
2018-12-24 18:32:44,629 INFO : Time only for training updates: 7.33s
2018-12-24 18:32:49,038 INFO : Epoch 2
2018-12-24 18:32:49,039 INFO : train_loss                1.26214
2018-12-24 18:32:49,039 INFO : valid_loss                1.18247
2018-12-24 18:32:49,040 INFO : test_loss                 1.06565
2018-12-24 18:32:49,040 INFO : train_sample_misclass     0.59611
2018-12-24 18:32:49,041 INFO : valid_sample_misclass     0.51002
2018-12-24 18:32:49,041 INFO : test_sample_misclass      0.40558
2018-12-24 18:32:49,041 INFO : train_misclass            0.57379
2018-12-24 18:32:49,042 INFO : valid_misclass            0.46529
2018-12-24 18:32:49,042 INFO : test_misclass             0.34549
2018-12-24 18:32:49,043 INFO : runtime                   12.48297
2018-12-24 18:32:49,043 INFO : 
2018-12-24 18:32:49,048 INFO : New best valid_misclass: 0.465293
2018-12-24 18:3

2018-12-24 18:34:41,094 INFO : 
2018-12-24 18:34:49,107 INFO : Time only for training updates: 7.27s
2018-12-24 18:34:53,474 INFO : Epoch 12
2018-12-24 18:34:53,475 INFO : train_loss                1.06491
2018-12-24 18:34:53,475 INFO : valid_loss                1.16354
2018-12-24 18:34:53,476 INFO : test_loss                 0.99710
2018-12-24 18:34:53,477 INFO : train_sample_misclass     0.47284
2018-12-24 18:34:53,477 INFO : valid_sample_misclass     0.49799
2018-12-24 18:34:53,477 INFO : test_sample_misclass      0.39765
2018-12-24 18:34:53,478 INFO : train_misclass            0.42404
2018-12-24 18:34:53,478 INFO : valid_misclass            0.44252
2018-12-24 18:34:53,479 INFO : test_misclass             0.33681
2018-12-24 18:34:53,479 INFO : runtime                   12.36705
2018-12-24 18:34:53,480 INFO : 
2018-12-24 18:35:01,464 INFO : Time only for training updates: 7.27s
2018-12-24 18:35:05,804 INFO : Epoch 13
2018-12-24 18:35:05,804 INFO : train_loss                1.04575
20

2018-12-24 18:36:56,900 INFO : valid_loss                1.18477
2018-12-24 18:36:56,900 INFO : test_loss                 1.00146
2018-12-24 18:36:56,901 INFO : train_sample_misclass     0.37604
2018-12-24 18:36:56,901 INFO : valid_sample_misclass     0.48421
2018-12-24 18:36:56,901 INFO : test_sample_misclass      0.42405
2018-12-24 18:36:56,902 INFO : train_misclass            0.31199
2018-12-24 18:36:56,903 INFO : valid_misclass            0.42950
2018-12-24 18:36:56,903 INFO : test_misclass             0.37326
2018-12-24 18:36:56,904 INFO : runtime                   12.34821
2018-12-24 18:36:56,904 INFO : 
2018-12-24 18:37:04,921 INFO : Time only for training updates: 7.27s
2018-12-24 18:37:09,270 INFO : Epoch 23
2018-12-24 18:37:09,270 INFO : train_loss                0.89997
2018-12-24 18:37:09,271 INFO : valid_loss                1.12471
2018-12-24 18:37:09,272 INFO : test_loss                 1.03675
2018-12-24 18:37:09,272 INFO : train_sample_misclass     0.37995
2018-12-24 18

2018-12-24 18:39:00,398 INFO : valid_sample_misclass     0.49812
2018-12-24 18:39:00,398 INFO : test_sample_misclass      0.45093
2018-12-24 18:39:00,399 INFO : train_misclass            0.24173
2018-12-24 18:39:00,400 INFO : valid_misclass            0.45879
2018-12-24 18:39:00,400 INFO : test_misclass             0.40799
2018-12-24 18:39:00,400 INFO : runtime                   12.34701
2018-12-24 18:39:00,401 INFO : 
2018-12-24 18:39:08,381 INFO : Time only for training updates: 7.26s
2018-12-24 18:39:12,733 INFO : Epoch 33
2018-12-24 18:39:12,734 INFO : train_loss                0.79759
2018-12-24 18:39:12,734 INFO : valid_loss                1.08070
2018-12-24 18:39:12,735 INFO : test_loss                 0.99731
2018-12-24 18:39:12,736 INFO : train_sample_misclass     0.31271
2018-12-24 18:39:12,736 INFO : valid_sample_misclass     0.43390
2018-12-24 18:39:12,736 INFO : test_sample_misclass      0.42180
2018-12-24 18:39:12,737 INFO : train_misclass            0.24661
2018-12-24 18

...

2018-12-24 19:15:16,708 INFO : train_loss                0.50113
2018-12-24 19:15:16,709 INFO : valid_loss                1.07990
2018-12-24 19:15:16,709 INFO : test_loss                 0.97969
2018-12-24 19:15:16,710 INFO : train_sample_misclass     0.18043
2018-12-24 19:15:16,710 INFO : valid_sample_misclass     0.42309
2018-12-24 19:15:16,711 INFO : test_sample_misclass      0.40010
2018-12-24 19:15:16,711 INFO : train_misclass            0.11612
2018-12-24 19:15:16,711 INFO : valid_misclass            0.35900
2018-12-24 19:15:16,712 INFO : test_misclass             0.33333
2018-12-24 19:15:16,712 INFO : runtime                   12.39040
2018-12-24 19:15:16,712 INFO : 
2018-12-24 19:15:24,739 INFO : Time only for training updates: 7.31s
2018-12-24 19:15:29,101 INFO : Epoch 209
2018-12-24 19:15:29,101 INFO : train_loss                0.49000
2018-12-24 19:15:29,103 INFO : valid_loss                1.19173
2018-12-24 19:15:29,103 INFO : test_loss                 1.08498
2018-12-24 1

2018-12-24 19:17:20,660 INFO : test_sample_misclass      0.45755
2018-12-24 19:17:20,660 INFO : train_misclass            0.12154
2018-12-24 19:17:20,661 INFO : valid_misclass            0.40130
2018-12-24 19:17:20,661 INFO : test_misclass             0.42014
2018-12-24 19:17:20,662 INFO : runtime                   12.38626
2018-12-24 19:17:20,662 INFO : 
2018-12-24 19:17:28,681 INFO : Time only for training updates: 7.30s
2018-12-24 19:17:33,041 INFO : Epoch 219
2018-12-24 19:17:33,042 INFO : train_loss                0.49955
2018-12-24 19:17:33,043 INFO : valid_loss                1.11049
2018-12-24 19:17:33,043 INFO : test_loss                 1.07732
2018-12-24 19:17:33,044 INFO : train_sample_misclass     0.17776
2018-12-24 19:17:33,044 INFO : valid_sample_misclass     0.43171
2018-12-24 19:17:33,044 INFO : test_sample_misclass      0.46336
2018-12-24 19:17:33,045 INFO : train_misclass            0.10635
2018-12-24 19:17:33,045 INFO : valid_misclass            0.36117
2018-12-24 1

2018-12-24 19:19:24,633 INFO : 
2018-12-24 19:19:32,654 INFO : Time only for training updates: 7.31s
2018-12-24 19:19:37,024 INFO : Epoch 229
2018-12-24 19:19:37,024 INFO : train_loss                0.48077
2018-12-24 19:19:37,025 INFO : valid_loss                1.10796
2018-12-24 19:19:37,026 INFO : test_loss                 1.17704
2018-12-24 19:19:37,026 INFO : train_sample_misclass     0.17447
2018-12-24 19:19:37,028 INFO : valid_sample_misclass     0.42882
2018-12-24 19:19:37,028 INFO : test_sample_misclass      0.49775
2018-12-24 19:19:37,028 INFO : train_misclass            0.11096
2018-12-24 19:19:37,029 INFO : valid_misclass            0.36768
2018-12-24 19:19:37,029 INFO : test_misclass             0.44965
2018-12-24 19:19:37,030 INFO : runtime                   12.38678
2018-12-24 19:19:37,030 INFO : 
2018-12-24 19:19:45,045 INFO : Time only for training updates: 7.30s
2018-12-24 19:19:49,397 INFO : Epoch 230
2018-12-24 19:19:49,398 INFO : train_loss                0.50046


2018-12-24 19:21:41,008 INFO : test_loss                 1.22750
2018-12-24 19:21:41,009 INFO : train_sample_misclass     0.18998
2018-12-24 19:21:41,009 INFO : valid_sample_misclass     0.43237
2018-12-24 19:21:41,010 INFO : test_sample_misclass      0.53790
2018-12-24 19:21:41,010 INFO : train_misclass            0.13239
2018-12-24 19:21:41,011 INFO : valid_misclass            0.37852
2018-12-24 19:21:41,011 INFO : test_misclass             0.50694
2018-12-24 19:21:41,011 INFO : runtime                   12.40659
2018-12-24 19:21:41,012 INFO : 
2018-12-24 19:21:49,035 INFO : Time only for training updates: 7.30s
2018-12-24 19:21:53,411 INFO : Epoch 240
2018-12-24 19:21:53,411 INFO : train_loss                0.50678
2018-12-24 19:21:53,412 INFO : valid_loss                1.13959
2018-12-24 19:21:53,413 INFO : test_loss                 1.09687
2018-12-24 19:21:53,413 INFO : train_sample_misclass     0.17819
2018-12-24 19:21:53,414 INFO : valid_sample_misclass     0.44110
2018-12-24 1

2018-12-24 19:23:46,226 INFO : valid_loss                0.69390
2018-12-24 19:23:46,226 INFO : test_loss                 0.97727
2018-12-24 19:23:46,227 INFO : train_sample_misclass     0.21546
2018-12-24 19:23:46,227 INFO : valid_sample_misclass     0.26612
2018-12-24 19:23:46,227 INFO : test_sample_misclass      0.41816
2018-12-24 19:23:46,228 INFO : train_misclass            0.13867
2018-12-24 19:23:46,229 INFO : valid_misclass            0.18655
2018-12-24 19:23:46,229 INFO : test_misclass             0.36111
2018-12-24 19:23:46,230 INFO : runtime                   15.22028
2018-12-24 19:23:46,230 INFO : 
2018-12-24 19:23:56,280 INFO : Time only for training updates: 9.16s
2018-12-24 19:24:01,429 INFO : Epoch 170
2018-12-24 19:24:01,430 INFO : train_loss                0.59656
2018-12-24 19:24:01,430 INFO : valid_loss                0.63091
2018-12-24 19:24:01,431 INFO : test_loss                 1.00639
2018-12-24 19:24:01,431 INFO : train_sample_misclass     0.22782
2018-12-24 1

###  valid_misclass: 0.074837 test_misclass: 0.67708

In [13]:
leave_one_out_crop__deep_run(4)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-24 19:25:42,118 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-24 19:25:42,378 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-24 19:27:01,034 INFO : Run until first stop...
2018-12-24 19:27:05,440 INFO : Epoch 0
2018-12-24 19:27:05,440 INFO : train_loss                1.38701
2018-12-24 19:27:05,441 INFO : valid_loss                1.38781
2018-12-24 19:27:05,442 INFO : test_loss                 1.38705
2018-12-24 19:27:05,442 INFO : train_sample_misclass     0.74603
2018-12-24 19:27:05,443 INFO : valid_sample_misclass     0.74823
2018-12-24 19:27:05,443 INFO : test_sample_misclass      0.74815
2018-12-24 19:27:05,444 INFO : train_misclass            0.73901
2018-12-24 19:27:05,445 INFO : valid_misclass            0.73753
2018-12-24 19:27:05,445 INFO : test_misclass             0.75347
2018-12-24 19:27:05,446 INFO : runtime                   0.00000
2018-12-24 19:27:05,446 INFO : 
2018-12-24 19:27:05,451 INFO : New best valid_misclass: 0.737527
2018-12-24 19:27:05,451 INFO : 
2018-12-24 19:27:13,367 INFO : Time only for training updates: 7.20s
2018-12-24 19:27:17,710 INFO : Epoch 1
2018-12-24 19:27:17

2018-12-24 19:28:56,433 INFO : test_misclass             0.61285
2018-12-24 19:28:56,433 INFO : runtime                   12.32808
2018-12-24 19:28:56,434 INFO : 
2018-12-24 19:29:04,419 INFO : Time only for training updates: 7.27s
2018-12-24 19:29:08,757 INFO : Epoch 10
2018-12-24 19:29:08,757 INFO : train_loss                1.04346
2018-12-24 19:29:08,758 INFO : valid_loss                1.12172
2018-12-24 19:29:08,758 INFO : test_loss                 1.42513
2018-12-24 19:29:08,759 INFO : train_sample_misclass     0.46319
2018-12-24 19:29:08,760 INFO : valid_sample_misclass     0.44684
2018-12-24 19:29:08,760 INFO : test_sample_misclass      0.65701
2018-12-24 19:29:08,760 INFO : train_misclass            0.42539
2018-12-24 19:29:08,761 INFO : valid_misclass            0.39588
2018-12-24 19:29:08,762 INFO : test_misclass             0.64583
2018-12-24 19:29:08,762 INFO : runtime                   12.34048
2018-12-24 19:29:08,762 INFO : 
2018-12-24 19:29:08,769 INFO : New best valid

2018-12-24 19:30:59,844 INFO : valid_misclass            0.36985
2018-12-24 19:30:59,844 INFO : test_misclass             0.63021
2018-12-24 19:30:59,845 INFO : runtime                   12.32739
2018-12-24 19:30:59,845 INFO : 
2018-12-24 19:31:07,827 INFO : Time only for training updates: 7.26s
2018-12-24 19:31:12,166 INFO : Epoch 20
2018-12-24 19:31:12,166 INFO : train_loss                0.87273
2018-12-24 19:31:12,167 INFO : valid_loss                1.14093
2018-12-24 19:31:12,168 INFO : test_loss                 1.48832
2018-12-24 19:31:12,168 INFO : train_sample_misclass     0.36286
2018-12-24 19:31:12,169 INFO : valid_sample_misclass     0.45265
2018-12-24 19:31:12,169 INFO : test_sample_misclass      0.65385
2018-12-24 19:31:12,170 INFO : train_misclass            0.30412
2018-12-24 19:31:12,170 INFO : valid_misclass            0.39046
2018-12-24 19:31:12,171 INFO : test_misclass             0.62326
2018-12-24 19:31:12,171 INFO : runtime                   12.32908
2018-12-24 1

2018-12-24 19:33:15,557 INFO : Epoch 30
2018-12-24 19:33:15,558 INFO : train_loss                0.83257
2018-12-24 19:33:15,558 INFO : valid_loss                1.17801
2018-12-24 19:33:15,558 INFO : test_loss                 1.75243
2018-12-24 19:33:15,559 INFO : train_sample_misclass     0.35630
2018-12-24 19:33:15,559 INFO : valid_sample_misclass     0.45867
2018-12-24 19:33:15,560 INFO : test_sample_misclass      0.66795
2018-12-24 19:33:15,560 INFO : train_misclass            0.31769
2018-12-24 19:33:15,560 INFO : valid_misclass            0.41323
2018-12-24 19:33:15,561 INFO : test_misclass             0.65451
2018-12-24 19:33:15,561 INFO : runtime                   12.33807
2018-12-24 19:33:15,561 INFO : 
2018-12-24 19:33:23,543 INFO : Time only for training updates: 7.27s
2018-12-24 19:33:27,890 INFO : Epoch 31
2018-12-24 19:33:27,891 INFO : train_loss                0.77996
2018-12-24 19:33:27,891 INFO : valid_loss                1.11159
2018-12-24 19:33:27,892 INFO : test_lo

...

2018-12-24 20:17:59,370 INFO : train_misclass            0.08736
2018-12-24 20:17:59,370 INFO : valid_misclass            0.38395
2018-12-24 20:17:59,370 INFO : test_misclass             0.64931
2018-12-24 20:17:59,371 INFO : runtime                   12.38387
2018-12-24 20:17:59,371 INFO : 
2018-12-24 20:18:07,398 INFO : Time only for training updates: 7.28s
2018-12-24 20:18:11,754 INFO : Epoch 248
2018-12-24 20:18:11,754 INFO : train_loss                0.41693
2018-12-24 20:18:11,755 INFO : valid_loss                1.09584
2018-12-24 20:18:11,756 INFO : test_loss                 1.78994
2018-12-24 20:18:11,756 INFO : train_sample_misclass     0.14831
2018-12-24 20:18:11,757 INFO : valid_sample_misclass     0.40824
2018-12-24 20:18:11,758 INFO : test_sample_misclass      0.65943
2018-12-24 20:18:11,759 INFO : train_misclass            0.08546
2018-12-24 20:18:11,760 INFO : valid_misclass            0.33948
2018-12-24 20:18:11,760 INFO : test_misclass             0.66146
2018-12-24 2

2018-12-24 20:20:10,985 INFO : Time only for training updates: 7.28s
2018-12-24 20:20:15,333 INFO : Epoch 258
2018-12-24 20:20:15,334 INFO : train_loss                0.40643
2018-12-24 20:20:15,334 INFO : valid_loss                1.17937
2018-12-24 20:20:15,335 INFO : test_loss                 1.96990
2018-12-24 20:20:15,335 INFO : train_sample_misclass     0.14024
2018-12-24 20:20:15,336 INFO : valid_sample_misclass     0.42718
2018-12-24 20:20:15,336 INFO : test_sample_misclass      0.66270
2018-12-24 20:20:15,337 INFO : train_misclass            0.08573
2018-12-24 20:20:15,337 INFO : valid_misclass            0.36334
2018-12-24 20:20:15,338 INFO : test_misclass             0.64236
2018-12-24 20:20:15,339 INFO : runtime                   12.35550
2018-12-24 20:20:15,339 INFO : 
2018-12-24 20:20:23,365 INFO : Time only for training updates: 7.31s
2018-12-24 20:20:27,721 INFO : Epoch 259
2018-12-24 20:20:27,722 INFO : train_loss                0.43713
2018-12-24 20:20:27,723 INFO : v

2018-12-24 20:22:05,122 INFO : 
2018-12-24 20:22:05,127 INFO : New best valid_misclass: 0.172451
2018-12-24 20:22:05,128 INFO : 
2018-12-24 20:22:15,138 INFO : Time only for training updates: 9.12s
2018-12-24 20:22:20,276 INFO : Epoch 188
2018-12-24 20:22:20,276 INFO : train_loss                0.54708
2018-12-24 20:22:20,277 INFO : valid_loss                0.69081
2018-12-24 20:22:20,277 INFO : test_loss                 1.85626
2018-12-24 20:22:20,278 INFO : train_sample_misclass     0.20756
2018-12-24 20:22:20,278 INFO : valid_sample_misclass     0.27243
2018-12-24 20:22:20,279 INFO : test_sample_misclass      0.66128
2018-12-24 20:22:20,279 INFO : train_misclass            0.14366
2018-12-24 20:22:20,279 INFO : valid_misclass            0.18330
2018-12-24 20:22:20,280 INFO : test_misclass             0.64757
2018-12-24 20:22:20,280 INFO : runtime                   15.16348
2018-12-24 20:22:20,280 INFO : 
2018-12-24 20:22:30,319 INFO : Time only for training updates: 9.14s
2018-12-2

2018-12-24 20:24:36,770 INFO : runtime                   15.17870
2018-12-24 20:24:36,770 INFO : 
2018-12-24 20:24:46,767 INFO : Time only for training updates: 9.11s
2018-12-24 20:24:51,913 INFO : Epoch 198
2018-12-24 20:24:51,914 INFO : train_loss                0.55533
2018-12-24 20:24:51,915 INFO : valid_loss                0.58105
2018-12-24 20:24:51,915 INFO : test_loss                 2.08454
2018-12-24 20:24:51,915 INFO : train_sample_misclass     0.21298
2018-12-24 20:24:51,916 INFO : valid_sample_misclass     0.22228
2018-12-24 20:24:51,917 INFO : test_sample_misclass      0.66688
2018-12-24 20:24:51,917 INFO : train_misclass            0.15603
2018-12-24 20:24:51,918 INFO : valid_misclass            0.14751
2018-12-24 20:24:51,918 INFO : test_misclass             0.65278
2018-12-24 20:24:51,919 INFO : runtime                   15.17871
2018-12-24 20:24:51,919 INFO : 
2018-12-24 20:25:01,922 INFO : Time only for training updates: 9.11s
2018-12-24 20:25:07,067 INFO : Epoch 199

2018-12-24 20:27:08,405 INFO : test_misclass             0.66840
2018-12-24 20:27:08,406 INFO : runtime                   15.15750
2018-12-24 20:27:08,406 INFO : 
2018-12-24 20:27:18,417 INFO : Time only for training updates: 9.12s
2018-12-24 20:27:23,561 INFO : Epoch 208
2018-12-24 20:27:23,562 INFO : train_loss                0.52819
2018-12-24 20:27:23,562 INFO : valid_loss                0.54333
2018-12-24 20:27:23,563 INFO : test_loss                 1.94714
2018-12-24 20:27:23,564 INFO : train_sample_misclass     0.19862
2018-12-24 20:27:23,564 INFO : valid_sample_misclass     0.20917
2018-12-24 20:27:23,564 INFO : test_sample_misclass      0.66647
2018-12-24 20:27:23,565 INFO : train_misclass            0.13216
2018-12-24 20:27:23,565 INFO : valid_misclass            0.12798
2018-12-24 20:27:23,565 INFO : test_misclass             0.65278
2018-12-24 20:27:23,566 INFO : runtime                   15.16326
2018-12-24 20:27:23,566 INFO : 
2018-12-24 20:27:33,576 INFO : Time only for

###  valid_misclass: 0.124729 test_misclass: 0.69792

In [14]:
leave_one_out_crop__deep_run(5)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-24 20:29:19,220 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-24 20:29:19,480 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-24 20:30:38,095 INFO : Run until first stop...
2018-12-24 20:30:42,489 INFO : Epoch 0
2018-12-24 20:30:42,490 INFO : train_loss                1.38683
2018-12-24 20:30:42,490 INFO : valid_loss                1.38781
2018-12-24 20:30:42,490 INFO : test_loss                 1.38822
2018-12-24 20:30:42,491 INFO : train_sample_misclass     0.74542
2018-12-24 20:30:42,491 INFO : valid_sample_misclass     0.74823
2018-12-24 20:30:42,492 INFO : test_sample_misclass      0.75205
2018-12-24 20:30:42,493 INFO : train_misclass            0.73956
2018-12-24 20:30:42,493 INFO : valid_misclass            0.73753
2018-12-24 20:30:42,493 INFO : test_misclass             0.75000
2018-12-24 20:30:42,494 INFO : runtime                   0.00000
2018-12-24 20:30:42,494 INFO : 
2018-12-24 20:30:42,499 INFO : New best valid_misclass: 0.737527
2018-12-24 20:30:42,500 INFO : 
2018-12-24 20:30:50,408 INFO : Time only for training updates: 7.20s
2018-12-24 20:30:54,746 INFO : Epoch 1
2018-12-24 20:30:54

2018-12-24 20:32:33,459 INFO : test_misclass             0.70312
2018-12-24 20:32:33,459 INFO : runtime                   12.33618
2018-12-24 20:32:33,460 INFO : 
2018-12-24 20:32:41,480 INFO : Time only for training updates: 7.27s
2018-12-24 20:32:45,828 INFO : Epoch 10
2018-12-24 20:32:45,829 INFO : train_loss                1.01729
2018-12-24 20:32:45,830 INFO : valid_loss                1.13707
2018-12-24 20:32:45,830 INFO : test_loss                 2.06170
2018-12-24 20:32:45,831 INFO : train_sample_misclass     0.44030
2018-12-24 20:32:45,831 INFO : valid_sample_misclass     0.46341
2018-12-24 20:32:45,832 INFO : test_sample_misclass      0.70844
2018-12-24 20:32:45,832 INFO : train_misclass            0.39908
2018-12-24 20:32:45,833 INFO : valid_misclass            0.41540
2018-12-24 20:32:45,833 INFO : test_misclass             0.69618
2018-12-24 20:32:45,834 INFO : runtime                   12.37270
2018-12-24 20:32:45,834 INFO : 
2018-12-24 20:32:53,818 INFO : Time only for 

2018-12-24 20:34:36,952 INFO : 
2018-12-24 20:34:36,956 INFO : New best valid_misclass: 0.374187
2018-12-24 20:34:36,957 INFO : 
2018-12-24 20:34:44,936 INFO : Time only for training updates: 7.27s
2018-12-24 20:34:49,287 INFO : Epoch 20
2018-12-24 20:34:49,288 INFO : train_loss                0.84994
2018-12-24 20:34:49,288 INFO : valid_loss                1.16544
2018-12-24 20:34:49,289 INFO : test_loss                 1.79754
2018-12-24 20:34:49,290 INFO : train_sample_misclass     0.35606
2018-12-24 20:34:49,290 INFO : valid_sample_misclass     0.46449
2018-12-24 20:34:49,291 INFO : test_sample_misclass      0.68708
2018-12-24 20:34:49,291 INFO : train_misclass            0.29436
2018-12-24 20:34:49,291 INFO : valid_misclass            0.40239
2018-12-24 20:34:49,292 INFO : test_misclass             0.67708
2018-12-24 20:34:49,292 INFO : runtime                   12.33880
2018-12-24 20:34:49,293 INFO : 
2018-12-24 20:34:57,305 INFO : Time only for training updates: 7.27s
2018-12-24

2018-12-24 20:36:40,420 INFO : 
2018-12-24 20:36:48,402 INFO : Time only for training updates: 7.27s
2018-12-24 20:36:52,743 INFO : Epoch 30
2018-12-24 20:36:52,744 INFO : train_loss                0.75437
2018-12-24 20:36:52,744 INFO : valid_loss                1.06940
2018-12-24 20:36:52,745 INFO : test_loss                 2.20470
2018-12-24 20:36:52,746 INFO : train_sample_misclass     0.30230
2018-12-24 20:36:52,746 INFO : valid_sample_misclass     0.41953
2018-12-24 20:36:52,747 INFO : test_sample_misclass      0.70154
2018-12-24 20:36:52,747 INFO : train_misclass            0.23711
2018-12-24 20:36:52,748 INFO : valid_misclass            0.36876
2018-12-24 20:36:52,748 INFO : test_misclass             0.70833
2018-12-24 20:36:52,748 INFO : runtime                   12.33191
2018-12-24 20:36:52,749 INFO : 
2018-12-24 20:36:52,756 INFO : New best valid_misclass: 0.368764
2018-12-24 20:36:52,757 INFO : 
2018-12-24 20:37:00,737 INFO : Time only for training updates: 7.27s
2018-12-24

...

2018-12-24 20:53:45,192 INFO : train_loss                0.53507
2018-12-24 20:53:45,193 INFO : valid_loss                1.20713
2018-12-24 20:53:45,194 INFO : test_loss                 2.30144
2018-12-24 20:53:45,194 INFO : train_sample_misclass     0.20067
2018-12-24 20:53:45,195 INFO : valid_sample_misclass     0.43719
2018-12-24 20:53:45,196 INFO : test_sample_misclass      0.66178
2018-12-24 20:53:45,196 INFO : train_misclass            0.13918
2018-12-24 20:53:45,197 INFO : valid_misclass            0.39262
2018-12-24 20:53:45,197 INFO : test_misclass             0.64931
2018-12-24 20:53:45,197 INFO : runtime                   12.33430
2018-12-24 20:53:45,198 INFO : 
2018-12-24 20:53:53,193 INFO : Time only for training updates: 7.28s
2018-12-24 20:53:57,544 INFO : Epoch 113
2018-12-24 20:53:57,545 INFO : train_loss                0.58225
2018-12-24 20:53:57,545 INFO : valid_loss                1.18662
2018-12-24 20:53:57,546 INFO : test_loss                 3.01876
2018-12-24 2

2018-12-24 20:55:48,674 INFO : test_sample_misclass      0.66988
2018-12-24 20:55:48,675 INFO : train_misclass            0.11801
2018-12-24 20:55:48,676 INFO : valid_misclass            0.38395
2018-12-24 20:55:48,676 INFO : test_misclass             0.66319
2018-12-24 20:55:48,677 INFO : runtime                   12.33977
2018-12-24 20:55:48,678 INFO : 
2018-12-24 20:55:56,675 INFO : Time only for training updates: 7.28s
2018-12-24 20:56:01,030 INFO : Epoch 123
2018-12-24 20:56:01,030 INFO : train_loss                0.48239
2018-12-24 20:56:01,031 INFO : valid_loss                1.12691
2018-12-24 20:56:01,032 INFO : test_loss                 2.96766
2018-12-24 20:56:01,032 INFO : train_sample_misclass     0.17091
2018-12-24 20:56:01,033 INFO : valid_sample_misclass     0.40962
2018-12-24 20:56:01,033 INFO : test_sample_misclass      0.69296
2018-12-24 20:56:01,034 INFO : train_misclass            0.09523
2018-12-24 20:56:01,034 INFO : valid_misclass            0.35358
2018-12-24 2

2018-12-24 20:57:52,208 INFO : 
2018-12-24 20:58:00,202 INFO : Time only for training updates: 7.27s
2018-12-24 20:58:04,546 INFO : Epoch 133
2018-12-24 20:58:04,547 INFO : train_loss                0.48419
2018-12-24 20:58:04,547 INFO : valid_loss                1.16546
2018-12-24 20:58:04,548 INFO : test_loss                 2.45682
2018-12-24 20:58:04,549 INFO : train_sample_misclass     0.17555
2018-12-24 20:58:04,550 INFO : valid_sample_misclass     0.41801
2018-12-24 20:58:04,551 INFO : test_sample_misclass      0.66308
2018-12-24 20:58:04,551 INFO : train_misclass            0.11096
2018-12-24 20:58:04,552 INFO : valid_misclass            0.36443
2018-12-24 20:58:04,552 INFO : test_misclass             0.64757
2018-12-24 20:58:04,553 INFO : runtime                   12.37332
2018-12-24 20:58:04,553 INFO : 
2018-12-24 20:58:12,542 INFO : Time only for training updates: 7.27s
2018-12-24 20:58:16,901 INFO : Epoch 134
2018-12-24 20:58:16,902 INFO : train_loss                0.45960


2018-12-24 21:00:08,033 INFO : test_loss                 2.31816
2018-12-24 21:00:08,033 INFO : train_sample_misclass     0.16461
2018-12-24 21:00:08,033 INFO : valid_sample_misclass     0.40078
2018-12-24 21:00:08,034 INFO : test_sample_misclass      0.68890
2018-12-24 21:00:08,035 INFO : train_misclass            0.09848
2018-12-24 21:00:08,036 INFO : valid_misclass            0.35033
2018-12-24 21:00:08,036 INFO : test_misclass             0.69271
2018-12-24 21:00:08,037 INFO : runtime                   12.34789
2018-12-24 21:00:08,037 INFO : 
2018-12-24 21:00:16,028 INFO : Time only for training updates: 7.27s
2018-12-24 21:00:20,376 INFO : Epoch 144
2018-12-24 21:00:20,376 INFO : train_loss                0.47106
2018-12-24 21:00:20,377 INFO : valid_loss                1.18407
2018-12-24 21:00:20,378 INFO : test_loss                 2.30171
2018-12-24 21:00:20,379 INFO : train_sample_misclass     0.16893
2018-12-24 21:00:20,379 INFO : valid_sample_misclass     0.43569
2018-12-24 2

2018-12-24 21:02:12,799 INFO : valid_loss                0.73840
2018-12-24 21:02:12,800 INFO : test_loss                 2.63926
2018-12-24 21:02:12,800 INFO : train_sample_misclass     0.24916
2018-12-24 21:02:12,801 INFO : valid_sample_misclass     0.29280
2018-12-24 21:02:12,801 INFO : test_sample_misclass      0.70458
2018-12-24 21:02:12,802 INFO : train_misclass            0.17600
2018-12-24 21:02:12,803 INFO : valid_misclass            0.21692
2018-12-24 21:02:12,803 INFO : test_misclass             0.70486
2018-12-24 21:02:12,803 INFO : runtime                   15.17007
2018-12-24 21:02:12,804 INFO : 
2018-12-24 21:02:22,802 INFO : Time only for training updates: 9.11s
2018-12-24 21:02:27,937 INFO : Epoch 74
2018-12-24 21:02:27,938 INFO : train_loss                0.65246
2018-12-24 21:02:27,939 INFO : valid_loss                0.68769
2018-12-24 21:02:27,939 INFO : test_loss                 2.67163
2018-12-24 21:02:27,940 INFO : train_sample_misclass     0.25504
2018-12-24 21

In [ ]:
leave_one_out_crop__deep_run(5)

In [ ]:
leave_one_out_crop__deep_run(6)

In [12]:
def leave_one_out_deep_run(out):
    subjects_list = [i for i in range(1, 10)]
    subjects_list.remove(out)
    train_data = load_train_data(subjects_list)
    test_data = load_subject_data(out)

    logging.basicConfig(format='%(asctime)s %(levelname)s : %(message)s',
                            level=logging.DEBUG, stream=sys.stdout)
    cuda = True
    exp = run_exp(train_data, test_data, low_cut_hz, "deep", cuda)
    log.info("Last 10 epochs")
    log.info("\n" + str(exp.epochs_df.iloc[-10:]))

###  valid_misclass: 0.01193 test_misclass: 0.29688

In [18]:
leave_one_out_deep_run(1)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  2708.672 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 662665  =      0.000 ...  2650.660 secs...
2018-12-24 21:32:31,499 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
2018-12-24 21:32:31,752 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  26

2018-12-24 21:33:50,523 INFO : Run until first stop...
2018-12-24 21:33:54,057 INFO : Epoch 0
2018-12-24 21:33:54,057 INFO : train_loss                1.40307
2018-12-24 21:33:54,058 INFO : valid_loss                1.40089
2018-12-24 21:33:54,059 INFO : test_loss                 1.40378
2018-12-24 21:33:54,060 INFO : train_misclass            0.75203
2018-12-24 21:33:54,060 INFO : valid_misclass            0.75054
2018-12-24 21:33:54,061 INFO : test_misclass             0.72743
2018-12-24 21:33:54,061 INFO : runtime                   0.00000
2018-12-24 21:33:54,062 INFO : 
2018-12-24 21:33:54,066 INFO : New best valid_misclass: 0.750542
2018-12-24 21:33:54,066 INFO : 
2018-12-24 21:33:59,013 INFO : Time only for training updates: 4.95s
2018-12-24 21:34:02,573 INFO : Epoch 1
2018-12-24 21:34:02,573 INFO : train_loss                1.78749
2018-12-24 21:34:02,574 INFO : valid_loss                1.68003
2018-12-24 21:34:02,574 INFO : test_loss                 1.77210
2018-12-24 21:34:02

2018-12-24 21:35:36,640 INFO : train_misclass            0.56864
2018-12-24 21:35:36,640 INFO : valid_misclass            0.52061
2018-12-24 21:35:36,641 INFO : test_misclass             0.41667
2018-12-24 21:35:36,641 INFO : runtime                   8.56190
2018-12-24 21:35:36,642 INFO : 
2018-12-24 21:35:41,716 INFO : Time only for training updates: 5.07s
2018-12-24 21:35:45,375 INFO : Epoch 13
2018-12-24 21:35:45,376 INFO : train_loss                1.16238
2018-12-24 21:35:45,376 INFO : valid_loss                1.10602
2018-12-24 21:35:45,376 INFO : test_loss                 0.95606
2018-12-24 21:35:45,377 INFO : train_misclass            0.53418
2018-12-24 21:35:45,377 INFO : valid_misclass            0.47072
2018-12-24 21:35:45,378 INFO : test_misclass             0.37674
2018-12-24 21:35:45,378 INFO : runtime                   8.65827
2018-12-24 21:35:45,379 INFO : 
2018-12-24 21:35:45,383 INFO : New best valid_misclass: 0.470716
2018-12-24 21:35:45,383 INFO : 
2018-12-24 21:3

2018-12-24 21:37:30,358 INFO : runtime                   8.73803
2018-12-24 21:37:30,359 INFO : 
2018-12-24 21:37:35,484 INFO : Time only for training updates: 5.12s
2018-12-24 21:37:39,151 INFO : Epoch 26
2018-12-24 21:37:39,151 INFO : train_loss                0.90258
2018-12-24 21:37:39,152 INFO : valid_loss                1.00192
2018-12-24 21:37:39,152 INFO : test_loss                 0.81017
2018-12-24 21:37:39,152 INFO : train_misclass            0.36625
2018-12-24 21:37:39,153 INFO : valid_misclass            0.43059
2018-12-24 21:37:39,153 INFO : test_misclass             0.34201
2018-12-24 21:37:39,153 INFO : runtime                   8.82694
2018-12-24 21:37:39,154 INFO : 
2018-12-24 21:37:44,282 INFO : Time only for training updates: 5.13s
2018-12-24 21:37:47,870 INFO : Epoch 27
2018-12-24 21:37:47,871 INFO : train_loss                0.88875
2018-12-24 21:37:47,871 INFO : valid_loss                0.98486
2018-12-24 21:37:47,872 INFO : test_loss                 0.78855
201

2018-12-24 21:39:32,496 INFO : valid_misclass            0.40456
2018-12-24 21:39:32,497 INFO : test_misclass             0.35938
2018-12-24 21:39:32,497 INFO : runtime                   8.73467
2018-12-24 21:39:32,498 INFO : 
2018-12-24 21:39:37,611 INFO : Time only for training updates: 5.11s
2018-12-24 21:39:41,286 INFO : Epoch 40
2018-12-24 21:39:41,287 INFO : train_loss                0.73921
2018-12-24 21:39:41,287 INFO : valid_loss                1.02532
2018-12-24 21:39:41,288 INFO : test_loss                 0.87245
2018-12-24 21:39:41,288 INFO : train_misclass            0.29788
2018-12-24 21:39:41,289 INFO : valid_misclass            0.41974
2018-12-24 21:39:41,289 INFO : test_misclass             0.37153
2018-12-24 21:39:41,289 INFO : runtime                   8.76957
2018-12-24 21:39:41,290 INFO : 
2018-12-24 21:39:46,581 INFO : Time only for training updates: 5.29s
2018-12-24 21:39:50,220 INFO : Epoch 41
2018-12-24 21:39:50,220 INFO : train_loss                0.62230
201

...

2018-12-24 22:11:26,541 INFO : valid_loss                1.04999
2018-12-24 22:11:26,541 INFO : test_loss                 0.73572
2018-12-24 22:11:26,542 INFO : train_misclass            0.00000
2018-12-24 22:11:26,542 INFO : valid_misclass            0.37419
2018-12-24 22:11:26,543 INFO : test_misclass             0.29167
2018-12-24 22:11:26,543 INFO : runtime                   8.80529
2018-12-24 22:11:26,544 INFO : 
2018-12-24 22:11:31,680 INFO : Time only for training updates: 5.13s
2018-12-24 22:11:35,390 INFO : Epoch 260
2018-12-24 22:11:35,390 INFO : train_loss                0.03046
2018-12-24 22:11:35,391 INFO : valid_loss                1.04079
2018-12-24 22:11:35,392 INFO : test_loss                 0.78783
2018-12-24 22:11:35,392 INFO : train_misclass            0.00027
2018-12-24 22:11:35,393 INFO : valid_misclass            0.36117
2018-12-24 22:11:35,393 INFO : test_misclass             0.31597
2018-12-24 22:11:35,394 INFO : runtime                   8.85055
2018-12-24 22

2018-12-24 22:13:29,232 INFO : Epoch 273
2018-12-24 22:13:29,232 INFO : train_loss                0.03435
2018-12-24 22:13:29,233 INFO : valid_loss                1.07158
2018-12-24 22:13:29,234 INFO : test_loss                 0.83496
2018-12-24 22:13:29,234 INFO : train_misclass            0.00027
2018-12-24 22:13:29,235 INFO : valid_misclass            0.38069
2018-12-24 22:13:29,235 INFO : test_misclass             0.30208
2018-12-24 22:13:29,235 INFO : runtime                   8.61232
2018-12-24 22:13:29,236 INFO : 
2018-12-24 22:13:34,311 INFO : Time only for training updates: 5.07s
2018-12-24 22:13:38,027 INFO : Epoch 274
2018-12-24 22:13:38,028 INFO : train_loss                0.02747
2018-12-24 22:13:38,028 INFO : valid_loss                1.03662
2018-12-24 22:13:38,029 INFO : test_loss                 0.80559
2018-12-24 22:13:38,029 INFO : train_misclass            0.00027
2018-12-24 22:13:38,030 INFO : valid_misclass            0.36443
2018-12-24 22:13:38,030 INFO : test_m

2018-12-24 22:15:24,108 INFO : train_loss                0.21042
2018-12-24 22:15:24,109 INFO : valid_loss                0.36434
2018-12-24 22:15:24,109 INFO : test_loss                 0.68619
2018-12-24 22:15:24,110 INFO : train_misclass            0.03971
2018-12-24 22:15:24,110 INFO : valid_misclass            0.12148
2018-12-24 22:15:24,111 INFO : test_misclass             0.28646
2018-12-24 22:15:24,112 INFO : runtime                   10.59751
2018-12-24 22:15:24,112 INFO : 
2018-12-24 22:15:24,116 INFO : New best valid_misclass: 0.121475
2018-12-24 22:15:24,117 INFO : 
2018-12-24 22:15:30,433 INFO : Time only for training updates: 6.32s
2018-12-24 22:15:34,688 INFO : Epoch 127
2018-12-24 22:15:34,688 INFO : train_loss                0.18912
2018-12-24 22:15:34,689 INFO : valid_loss                0.36380
2018-12-24 22:15:34,689 INFO : test_loss                 0.72556
2018-12-24 22:15:34,690 INFO : train_misclass            0.02843
2018-12-24 22:15:34,691 INFO : valid_misclass

2018-12-24 22:17:30,721 INFO : valid_misclass            0.04121
2018-12-24 22:17:30,722 INFO : test_misclass             0.29514
2018-12-24 22:17:30,722 INFO : runtime                   10.59428
2018-12-24 22:17:30,723 INFO : 
2018-12-24 22:17:30,727 INFO : New best valid_misclass: 0.041215
2018-12-24 22:17:30,727 INFO : 
2018-12-24 22:17:37,053 INFO : Time only for training updates: 6.32s
2018-12-24 22:17:41,296 INFO : Epoch 139
2018-12-24 22:17:41,297 INFO : train_loss                0.17991
2018-12-24 22:17:41,297 INFO : valid_loss                0.19895
2018-12-24 22:17:41,298 INFO : test_loss                 0.81963
2018-12-24 22:17:41,299 INFO : train_misclass            0.02127
2018-12-24 22:17:41,299 INFO : valid_misclass            0.03471
2018-12-24 22:17:41,300 INFO : test_misclass             0.35938
2018-12-24 22:17:41,300 INFO : runtime                   10.59383
2018-12-24 22:17:41,301 INFO : 
2018-12-24 22:17:41,306 INFO : New best valid_misclass: 0.034707
2018-12-24 2

2018-12-24 22:19:37,591 INFO : 
2018-12-24 22:19:37,596 INFO : New best valid_misclass: 0.009761
2018-12-24 22:19:37,597 INFO : 
2018-12-24 22:19:43,912 INFO : Time only for training updates: 6.31s
2018-12-24 22:19:48,162 INFO : Epoch 151
2018-12-24 22:19:48,162 INFO : train_loss                0.12029
2018-12-24 22:19:48,163 INFO : valid_loss                0.11766
2018-12-24 22:19:48,163 INFO : test_loss                 0.71925
2018-12-24 22:19:48,164 INFO : train_misclass            0.00694
2018-12-24 22:19:48,164 INFO : valid_misclass            0.01518
2018-12-24 22:19:48,164 INFO : test_misclass             0.29861
2018-12-24 22:19:48,165 INFO : runtime                   10.57603
2018-12-24 22:19:48,166 INFO : 
2018-12-24 22:19:54,490 INFO : Time only for training updates: 6.32s
2018-12-24 22:19:58,745 INFO : Epoch 152
2018-12-24 22:19:58,746 INFO : train_loss                0.12355
2018-12-24 22:19:58,746 INFO : valid_loss                0.11750
2018-12-24 22:19:58,746 INFO : te

###  valid_misclass: 0.00000 test_misclass: 0.65451

In [13]:
leave_one_out_deep_run(2)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 660529  =      0.000 ...  2642.116 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A03E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 648774 

2018-12-25 10:30:21,651 INFO : valid_misclass            0.74729
2018-12-25 10:30:21,651 INFO : test_misclass             0.75000
2018-12-25 10:30:21,652 INFO : runtime                   8.66292
2018-12-25 10:30:21,652 INFO : 
2018-12-25 10:30:21,657 INFO : New best valid_misclass: 0.747289
2018-12-25 10:30:21,657 INFO : 
2018-12-25 10:30:26,653 INFO : Time only for training updates: 5.00s
2018-12-25 10:30:30,260 INFO : Epoch 3
2018-12-25 10:30:30,261 INFO : train_loss                1.74811
2018-12-25 10:30:30,261 INFO : valid_loss                1.58554
2018-12-25 10:30:30,262 INFO : test_loss                 2.27968
2018-12-25 10:30:30,262 INFO : train_misclass            0.72355
2018-12-25 10:30:30,262 INFO : valid_misclass            0.75163
2018-12-25 10:30:30,263 INFO : test_misclass             0.75000
2018-12-25 10:30:30,263 INFO : runtime                   8.60355
2018-12-25 10:30:30,264 INFO : 
2018-12-25 10:30:35,282 INFO : Time only for training updates: 5.02s
2018-12-25 1

2018-12-25 10:32:13,733 INFO : Epoch 15
2018-12-25 10:32:13,734 INFO : train_loss                1.15263
2018-12-25 10:32:13,734 INFO : valid_loss                1.13013
2018-12-25 10:32:13,734 INFO : test_loss                 1.82705
2018-12-25 10:32:13,735 INFO : train_misclass            0.51763
2018-12-25 10:32:13,736 INFO : valid_misclass            0.44577
2018-12-25 10:32:13,736 INFO : test_misclass             0.74653
2018-12-25 10:32:13,737 INFO : runtime                   8.57607
2018-12-25 10:32:13,737 INFO : 
2018-12-25 10:32:13,742 INFO : New best valid_misclass: 0.445770
2018-12-25 10:32:13,742 INFO : 
2018-12-25 10:32:18,731 INFO : Time only for training updates: 4.99s
2018-12-25 10:32:22,314 INFO : Epoch 16
2018-12-25 10:32:22,314 INFO : train_loss                1.09239
2018-12-25 10:32:22,315 INFO : valid_loss                1.16579
2018-12-25 10:32:22,315 INFO : test_loss                 1.68286
2018-12-25 10:32:22,316 INFO : train_misclass            0.50217
2018-12

2018-12-25 10:34:05,904 INFO : valid_misclass            0.47072
2018-12-25 10:34:05,905 INFO : test_misclass             0.71181
2018-12-25 10:34:05,906 INFO : runtime                   8.58004
2018-12-25 10:34:05,906 INFO : 
2018-12-25 10:34:10,893 INFO : Time only for training updates: 4.99s
2018-12-25 10:34:14,483 INFO : Epoch 29
2018-12-25 10:34:14,484 INFO : train_loss                0.87046
2018-12-25 10:34:14,484 INFO : valid_loss                1.18543
2018-12-25 10:34:14,485 INFO : test_loss                 1.95077
2018-12-25 10:34:14,485 INFO : train_misclass            0.36245
2018-12-25 10:34:14,486 INFO : valid_misclass            0.46421
2018-12-25 10:34:14,487 INFO : test_misclass             0.69618
2018-12-25 10:34:14,487 INFO : runtime                   8.57707
2018-12-25 10:34:14,488 INFO : 
2018-12-25 10:34:19,478 INFO : Time only for training updates: 4.99s
2018-12-25 10:34:23,066 INFO : Epoch 30
2018-12-25 10:34:23,067 INFO : train_loss                0.76508
201

2018-12-25 10:36:06,045 INFO : test_loss                 2.04971
2018-12-25 10:36:06,045 INFO : train_misclass            0.25122
2018-12-25 10:36:06,046 INFO : valid_misclass            0.44794
2018-12-25 10:36:06,047 INFO : test_misclass             0.70486
2018-12-25 10:36:06,047 INFO : runtime                   8.57963
2018-12-25 10:36:06,047 INFO : 
2018-12-25 10:36:11,034 INFO : Time only for training updates: 4.99s
2018-12-25 10:36:14,621 INFO : Epoch 43
2018-12-25 10:36:14,622 INFO : train_loss                0.61843
2018-12-25 10:36:14,622 INFO : valid_loss                1.14534
2018-12-25 10:36:14,622 INFO : test_loss                 2.01150
2018-12-25 10:36:14,623 INFO : train_misclass            0.23494
2018-12-25 10:36:14,623 INFO : valid_misclass            0.45228
2018-12-25 10:36:14,624 INFO : test_misclass             0.67361
2018-12-25 10:36:14,624 INFO : runtime                   8.58631
2018-12-25 10:36:14,625 INFO : 
2018-12-25 10:36:19,612 INFO : Time only for tr

...

2018-12-25 11:42:32,085 INFO : test_misclass             0.65278
2018-12-25 11:42:32,086 INFO : runtime                   10.49583
2018-12-25 11:42:32,087 INFO : 
2018-12-25 11:42:38,359 INFO : Time only for training updates: 6.27s
2018-12-25 11:42:42,574 INFO : Epoch 331
2018-12-25 11:42:42,575 INFO : train_loss                0.04253
2018-12-25 11:42:42,575 INFO : valid_loss                0.04110
2018-12-25 11:42:42,576 INFO : test_loss                 2.11528
2018-12-25 11:42:42,576 INFO : train_misclass            0.00043
2018-12-25 11:42:42,577 INFO : valid_misclass            0.00000
2018-12-25 11:42:42,578 INFO : test_misclass             0.66493
2018-12-25 11:42:42,578 INFO : runtime                   10.49879
2018-12-25 11:42:42,579 INFO : 
2018-12-25 11:42:42,585 INFO : New best valid_misclass: 0.000000
2018-12-25 11:42:42,585 INFO : 
2018-12-25 11:42:48,861 INFO : Time only for training updates: 6.27s
2018-12-25 11:42:53,078 INFO : Epoch 332
2018-12-25 11:42:53,078 INFO : t

2018-12-25 11:44:48,588 INFO : train_misclass            0.00022
2018-12-25 11:44:48,589 INFO : valid_misclass            0.00000
2018-12-25 11:44:48,589 INFO : test_misclass             0.64062
2018-12-25 11:44:48,591 INFO : runtime                   10.49780
2018-12-25 11:44:48,591 INFO : 
2018-12-25 11:44:48,595 INFO : New best valid_misclass: 0.000000
2018-12-25 11:44:48,596 INFO : 
2018-12-25 11:44:54,867 INFO : Time only for training updates: 6.27s
2018-12-25 11:44:59,085 INFO : Epoch 344
2018-12-25 11:44:59,085 INFO : train_loss                0.04210
2018-12-25 11:44:59,086 INFO : valid_loss                0.04474
2018-12-25 11:44:59,086 INFO : test_loss                 2.01547
2018-12-25 11:44:59,087 INFO : train_misclass            0.00000
2018-12-25 11:44:59,087 INFO : valid_misclass            0.00000
2018-12-25 11:44:59,087 INFO : test_misclass             0.66667
2018-12-25 11:44:59,088 INFO : runtime                   10.49539
2018-12-25 11:44:59,088 INFO : 
2018-12-25 1

2018-12-25 11:47:05,061 INFO : Epoch 356
2018-12-25 11:47:05,062 INFO : train_loss                0.04379
2018-12-25 11:47:05,062 INFO : valid_loss                0.04114
2018-12-25 11:47:05,062 INFO : test_loss                 2.17619
2018-12-25 11:47:05,063 INFO : train_misclass            0.00022
2018-12-25 11:47:05,063 INFO : valid_misclass            0.00000
2018-12-25 11:47:05,064 INFO : test_misclass             0.66493
2018-12-25 11:47:05,064 INFO : runtime                   10.49867
2018-12-25 11:47:05,065 INFO : 
2018-12-25 11:47:05,072 INFO : New best valid_misclass: 0.000000
2018-12-25 11:47:05,072 INFO : 
2018-12-25 11:47:11,345 INFO : Time only for training updates: 6.27s
2018-12-25 11:47:15,564 INFO : Epoch 357
2018-12-25 11:47:15,564 INFO : train_loss                0.03572
2018-12-25 11:47:15,565 INFO : valid_loss                0.03290
2018-12-25 11:47:15,565 INFO : test_loss                 1.99530
2018-12-25 11:47:15,566 INFO : train_misclass            0.00022
2018

2018-12-25 11:49:11,054 INFO : 
2018-12-25 11:49:11,059 INFO : New best valid_misclass: 0.000000
2018-12-25 11:49:11,060 INFO : 
2018-12-25 11:49:17,328 INFO : Time only for training updates: 6.27s
2018-12-25 11:49:21,544 INFO : Epoch 369
2018-12-25 11:49:21,545 INFO : train_loss                0.05024
2018-12-25 11:49:21,546 INFO : valid_loss                0.04921
2018-12-25 11:49:21,546 INFO : test_loss                 2.21078
2018-12-25 11:49:21,547 INFO : train_misclass            0.00217
2018-12-25 11:49:21,547 INFO : valid_misclass            0.00325
2018-12-25 11:49:21,548 INFO : test_misclass             0.65799
2018-12-25 11:49:21,549 INFO : runtime                   10.49501
2018-12-25 11:49:21,549 INFO : 
2018-12-25 11:49:27,820 INFO : Time only for training updates: 6.27s
2018-12-25 11:49:32,047 INFO : Epoch 370
2018-12-25 11:49:32,048 INFO : train_loss                0.04193
2018-12-25 11:49:32,049 INFO : valid_loss                0.03837
2018-12-25 11:49:32,049 INFO : te

2018-12-25 11:51:38,004 INFO : train_loss                0.04745
2018-12-25 11:51:38,005 INFO : valid_loss                0.04859
2018-12-25 11:51:38,005 INFO : test_loss                 2.28267
2018-12-25 11:51:38,006 INFO : train_misclass            0.00174
2018-12-25 11:51:38,006 INFO : valid_misclass            0.00651
2018-12-25 11:51:38,007 INFO : test_misclass             0.67708
2018-12-25 11:51:38,007 INFO : runtime                   10.50117
2018-12-25 11:51:38,008 INFO : 
2018-12-25 11:51:44,281 INFO : Time only for training updates: 6.27s
2018-12-25 11:51:48,497 INFO : Epoch 383
2018-12-25 11:51:48,497 INFO : train_loss                0.03223
2018-12-25 11:51:48,498 INFO : valid_loss                0.03464
2018-12-25 11:51:48,499 INFO : test_loss                 2.12985
2018-12-25 11:51:48,499 INFO : train_misclass            0.00043
2018-12-25 11:51:48,500 INFO : valid_misclass            0.00108
2018-12-25 11:51:48,500 INFO : test_misclass             0.67535
2018-12-25 1

###  valid_misclass: 0.374187 test_misclass: 0.39062

In [14]:
leave_one_out_deep_run(3)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-25 11:53:00,891 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-25 11:53:01,155 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-25 11:54:19,091 INFO : Run until first stop...
2018-12-25 11:54:22,610 INFO : Epoch 0
2018-12-25 11:54:22,611 INFO : train_loss                1.40392
2018-12-25 11:54:22,612 INFO : valid_loss                1.40089
2018-12-25 11:54:22,612 INFO : test_loss                 1.39835
2018-12-25 11:54:22,612 INFO : train_misclass            0.74851
2018-12-25 11:54:22,613 INFO : valid_misclass            0.75054
2018-12-25 11:54:22,613 INFO : test_misclass             0.75000
2018-12-25 11:54:22,614 INFO : runtime                   0.00000
2018-12-25 11:54:22,615 INFO : 
2018-12-25 11:54:22,619 INFO : New best valid_misclass: 0.750542
2018-12-25 11:54:22,619 INFO : 
2018-12-25 11:54:27,580 INFO : Time only for training updates: 4.96s
2018-12-25 11:54:31,151 INFO : Epoch 1
2018-12-25 11:54:31,151 INFO : train_loss                1.73426
2018-12-25 11:54:31,152 INFO : valid_loss                1.62570
2018-12-25 11:54:31,152 INFO : test_loss                 1.68699
2018-12-25 11:54:31

2018-12-25 11:56:05,446 INFO : runtime                   8.58039
2018-12-25 11:56:05,447 INFO : 
2018-12-25 11:56:10,431 INFO : Time only for training updates: 4.98s
2018-12-25 11:56:14,022 INFO : Epoch 13
2018-12-25 11:56:14,023 INFO : train_loss                1.13310
2018-12-25 11:56:14,023 INFO : valid_loss                1.06793
2018-12-25 11:56:14,024 INFO : test_loss                 1.02030
2018-12-25 11:56:14,024 INFO : train_misclass            0.49023
2018-12-25 11:56:14,025 INFO : valid_misclass            0.44252
2018-12-25 11:56:14,026 INFO : test_misclass             0.39410
2018-12-25 11:56:14,026 INFO : runtime                   8.58160
2018-12-25 11:56:14,027 INFO : 
2018-12-25 11:56:14,032 INFO : New best valid_misclass: 0.442516
2018-12-25 11:56:14,033 INFO : 
2018-12-25 11:56:19,015 INFO : Time only for training updates: 4.98s
2018-12-25 11:56:22,601 INFO : Epoch 14
2018-12-25 11:56:22,602 INFO : train_loss                1.17473
2018-12-25 11:56:22,602 INFO : valid

2018-12-25 11:57:56,978 INFO : 
2018-12-25 11:58:01,965 INFO : Time only for training updates: 4.99s
2018-12-25 11:58:05,549 INFO : Epoch 26
2018-12-25 11:58:05,550 INFO : train_loss                1.00205
2018-12-25 11:58:05,550 INFO : valid_loss                1.08152
2018-12-25 11:58:05,552 INFO : test_loss                 1.01074
2018-12-25 11:58:05,552 INFO : train_misclass            0.43163
2018-12-25 11:58:05,552 INFO : valid_misclass            0.46095
2018-12-25 11:58:05,553 INFO : test_misclass             0.42361
2018-12-25 11:58:05,553 INFO : runtime                   8.57587
2018-12-25 11:58:05,553 INFO : 
2018-12-25 11:58:10,538 INFO : Time only for training updates: 4.98s
2018-12-25 11:58:14,127 INFO : Epoch 27
2018-12-25 11:58:14,127 INFO : train_loss                0.91067
2018-12-25 11:58:14,128 INFO : valid_loss                1.02180
2018-12-25 11:58:14,128 INFO : test_loss                 0.90905
2018-12-25 11:58:14,128 INFO : train_misclass            0.36435
201

2018-12-25 11:59:57,042 INFO : test_misclass             0.35938
2018-12-25 11:59:57,043 INFO : runtime                   8.57555
2018-12-25 11:59:57,044 INFO : 
2018-12-25 12:00:02,029 INFO : Time only for training updates: 4.98s
2018-12-25 12:00:05,617 INFO : Epoch 40
2018-12-25 12:00:05,617 INFO : train_loss                0.72878
2018-12-25 12:00:05,617 INFO : valid_loss                1.13906
2018-12-25 12:00:05,618 INFO : test_loss                 0.91876
2018-12-25 12:00:05,618 INFO : train_misclass            0.27971
2018-12-25 12:00:05,619 INFO : valid_misclass            0.46312
2018-12-25 12:00:05,620 INFO : test_misclass             0.38542
2018-12-25 12:00:05,620 INFO : runtime                   8.57470
2018-12-25 12:00:05,620 INFO : 
2018-12-25 12:00:10,607 INFO : Time only for training updates: 4.99s
2018-12-25 12:00:14,194 INFO : Epoch 41
2018-12-25 12:00:14,194 INFO : train_loss                0.66495
2018-12-25 12:00:14,195 INFO : valid_loss                0.98197
201

...

2018-12-25 12:11:48,983 INFO : train_misclass            0.00733
2018-12-25 12:11:48,984 INFO : valid_misclass            0.42842
2018-12-25 12:11:48,984 INFO : test_misclass             0.38715
2018-12-25 12:11:48,985 INFO : runtime                   8.58077
2018-12-25 12:11:48,985 INFO : 
2018-12-25 12:11:53,975 INFO : Time only for training updates: 4.99s
2018-12-25 12:11:57,562 INFO : Epoch 123
2018-12-25 12:11:57,563 INFO : train_loss                0.10877
2018-12-25 12:11:57,564 INFO : valid_loss                1.10993
2018-12-25 12:11:57,564 INFO : test_loss                 0.97764
2018-12-25 12:11:57,565 INFO : train_misclass            0.00353
2018-12-25 12:11:57,565 INFO : valid_misclass            0.41649
2018-12-25 12:11:57,566 INFO : test_misclass             0.39236
2018-12-25 12:11:57,566 INFO : runtime                   8.57938
2018-12-25 12:11:57,567 INFO : 
2018-12-25 12:12:02,555 INFO : Time only for training updates: 4.99s
2018-12-25 12:12:06,140 INFO : Epoch 124
2

2018-12-25 12:13:49,102 INFO : valid_loss                1.01552
2018-12-25 12:13:49,103 INFO : test_loss                 1.06093
2018-12-25 12:13:49,103 INFO : train_misclass            0.00163
2018-12-25 12:13:49,104 INFO : valid_misclass            0.38720
2018-12-25 12:13:49,105 INFO : test_misclass             0.43229
2018-12-25 12:13:49,105 INFO : runtime                   8.58045
2018-12-25 12:13:49,106 INFO : 
2018-12-25 12:13:54,093 INFO : Time only for training updates: 4.99s
2018-12-25 12:13:57,679 INFO : Epoch 137
2018-12-25 12:13:57,680 INFO : train_loss                0.08517
2018-12-25 12:13:57,680 INFO : valid_loss                1.13352
2018-12-25 12:13:57,681 INFO : test_loss                 0.97621
2018-12-25 12:13:57,681 INFO : train_misclass            0.00081
2018-12-25 12:13:57,681 INFO : valid_misclass            0.42191
2018-12-25 12:13:57,682 INFO : test_misclass             0.40625
2018-12-25 12:13:57,682 INFO : runtime                   8.57845
2018-12-25 12

2018-12-25 12:15:49,201 INFO : Epoch 150
2018-12-25 12:15:49,202 INFO : train_loss                0.07772
2018-12-25 12:15:49,203 INFO : valid_loss                1.18174
2018-12-25 12:15:49,204 INFO : test_loss                 1.12445
2018-12-25 12:15:49,205 INFO : train_misclass            0.00190
2018-12-25 12:15:49,206 INFO : valid_misclass            0.43709
2018-12-25 12:15:49,206 INFO : test_misclass             0.44097
2018-12-25 12:15:49,206 INFO : runtime                   8.57784
2018-12-25 12:15:49,207 INFO : 
2018-12-25 12:15:54,191 INFO : Time only for training updates: 4.98s
2018-12-25 12:15:57,785 INFO : Epoch 151
2018-12-25 12:15:57,786 INFO : train_loss                0.08513
2018-12-25 12:15:57,786 INFO : valid_loss                1.20208
2018-12-25 12:15:57,787 INFO : test_loss                 0.89346
2018-12-25 12:15:57,788 INFO : train_misclass            0.00353
2018-12-25 12:15:57,788 INFO : valid_misclass            0.43926
2018-12-25 12:15:57,789 INFO : test_m

2018-12-25 12:17:40,708 INFO : 
2018-12-25 12:17:45,696 INFO : Time only for training updates: 4.99s
2018-12-25 12:17:49,281 INFO : Epoch 164
2018-12-25 12:17:49,282 INFO : train_loss                0.07018
2018-12-25 12:17:49,282 INFO : valid_loss                1.13890
2018-12-25 12:17:49,284 INFO : test_loss                 1.02022
2018-12-25 12:17:49,285 INFO : train_misclass            0.00298
2018-12-25 12:17:49,285 INFO : valid_misclass            0.42516
2018-12-25 12:17:49,285 INFO : test_misclass             0.40799
2018-12-25 12:17:49,286 INFO : runtime                   8.57983
2018-12-25 12:17:49,286 INFO : 
2018-12-25 12:17:54,273 INFO : Time only for training updates: 4.99s
2018-12-25 12:17:57,860 INFO : Epoch 165
2018-12-25 12:17:57,861 INFO : train_loss                0.06314
2018-12-25 12:17:57,862 INFO : valid_loss                1.10080
2018-12-25 12:17:57,862 INFO : test_loss                 0.91556
2018-12-25 12:17:57,863 INFO : train_misclass            0.00380
2

2018-12-25 12:19:40,800 INFO : test_misclass             0.39062
2018-12-25 12:19:40,801 INFO : runtime                   8.58757
2018-12-25 12:19:40,801 INFO : 
2018-12-25 12:19:45,788 INFO : Time only for training updates: 4.99s
2018-12-25 12:19:49,375 INFO : Epoch 178
2018-12-25 12:19:49,376 INFO : train_loss                0.05475
2018-12-25 12:19:49,377 INFO : valid_loss                1.28118
2018-12-25 12:19:49,377 INFO : test_loss                 1.06753
2018-12-25 12:19:49,377 INFO : train_misclass            0.00353
2018-12-25 12:19:49,378 INFO : valid_misclass            0.43167
2018-12-25 12:19:49,378 INFO : test_misclass             0.41493
2018-12-25 12:19:49,379 INFO : runtime                   8.58217
2018-12-25 12:19:49,379 INFO : 
2018-12-25 12:19:49,380 INFO : Setup for second stop...
2018-12-25 12:19:49,387 INFO : Train loss to reach 1.08518
2018-12-25 12:19:49,387 INFO : Run until second stop...
2018-12-25 12:19:53,593 INFO : Epoch 19
2018-12-25 12:19:53,593 INFO :

###  valid_misclass: 0.000000 test_misclass: 0.54340

In [15]:
leave_one_out_deep_run(4)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-25 12:21:06,405 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-25 12:21:06,666 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-25 12:22:25,463 INFO : Run until first stop...
2018-12-25 12:22:28,979 INFO : Epoch 0
2018-12-25 12:22:28,980 INFO : train_loss                1.40136
2018-12-25 12:22:28,980 INFO : valid_loss                1.40089
2018-12-25 12:22:28,981 INFO : test_loss                 1.41471
2018-12-25 12:22:28,982 INFO : train_misclass            0.75014
2018-12-25 12:22:28,982 INFO : valid_misclass            0.75054
2018-12-25 12:22:28,982 INFO : test_misclass             0.73958
2018-12-25 12:22:28,983 INFO : runtime                   0.00000
2018-12-25 12:22:28,983 INFO : 
2018-12-25 12:22:28,988 INFO : New best valid_misclass: 0.750542
2018-12-25 12:22:28,989 INFO : 
2018-12-25 12:22:33,951 INFO : Time only for training updates: 4.96s
2018-12-25 12:22:37,525 INFO : Epoch 1
2018-12-25 12:22:37,525 INFO : train_loss                1.79464
2018-12-25 12:22:37,526 INFO : valid_loss                1.67297
2018-12-25 12:22:37,526 INFO : test_loss                 1.78933
2018-12-25 12:22:37

2018-12-25 12:24:11,858 INFO : train_loss                1.39530
2018-12-25 12:24:11,859 INFO : valid_loss                1.43431
2018-12-25 12:24:11,859 INFO : test_loss                 1.49255
2018-12-25 12:24:11,860 INFO : train_misclass            0.59224
2018-12-25 12:24:11,860 INFO : valid_misclass            0.63557
2018-12-25 12:24:11,860 INFO : test_misclass             0.70660
2018-12-25 12:24:11,861 INFO : runtime                   8.59164
2018-12-25 12:24:11,861 INFO : 
2018-12-25 12:24:16,850 INFO : Time only for training updates: 4.99s
2018-12-25 12:24:20,435 INFO : Epoch 13
2018-12-25 12:24:20,436 INFO : train_loss                1.18034
2018-12-25 12:24:20,436 INFO : valid_loss                1.27925
2018-12-25 12:24:20,436 INFO : test_loss                 1.31058
2018-12-25 12:24:20,437 INFO : train_misclass            0.53608
2018-12-25 12:24:20,438 INFO : valid_misclass            0.58243
2018-12-25 12:24:20,438 INFO : test_misclass             0.61979
2018-12-25 12:

2018-12-25 12:26:03,402 INFO : Epoch 25
2018-12-25 12:26:03,403 INFO : train_loss                1.01497
2018-12-25 12:26:03,403 INFO : valid_loss                1.06784
2018-12-25 12:26:03,403 INFO : test_loss                 1.48625
2018-12-25 12:26:03,404 INFO : train_misclass            0.46093
2018-12-25 12:26:03,404 INFO : valid_misclass            0.43167
2018-12-25 12:26:03,405 INFO : test_misclass             0.63889
2018-12-25 12:26:03,407 INFO : runtime                   8.57849
2018-12-25 12:26:03,407 INFO : 
2018-12-25 12:26:03,411 INFO : New best valid_misclass: 0.431670
2018-12-25 12:26:03,411 INFO : 
2018-12-25 12:26:08,398 INFO : Time only for training updates: 4.99s
2018-12-25 12:26:11,986 INFO : Epoch 26
2018-12-25 12:26:11,987 INFO : train_loss                0.90411
2018-12-25 12:26:11,987 INFO : valid_loss                1.00011
2018-12-25 12:26:11,988 INFO : test_loss                 1.37820
2018-12-25 12:26:11,988 INFO : train_misclass            0.38551
2018-12

2018-12-25 12:27:54,931 INFO : test_loss                 1.37014
2018-12-25 12:27:54,932 INFO : train_misclass            0.30955
2018-12-25 12:27:54,932 INFO : valid_misclass            0.40781
2018-12-25 12:27:54,933 INFO : test_misclass             0.58854
2018-12-25 12:27:54,933 INFO : runtime                   8.57419
2018-12-25 12:27:54,934 INFO : 
2018-12-25 12:27:59,921 INFO : Time only for training updates: 4.99s
2018-12-25 12:28:03,509 INFO : Epoch 39
2018-12-25 12:28:03,509 INFO : train_loss                0.74603
2018-12-25 12:28:03,510 INFO : valid_loss                0.99448
2018-12-25 12:28:03,510 INFO : test_loss                 1.39634
2018-12-25 12:28:03,511 INFO : train_misclass            0.30874
2018-12-25 12:28:03,512 INFO : valid_misclass            0.38395
2018-12-25 12:28:03,512 INFO : test_misclass             0.59549
2018-12-25 12:28:03,512 INFO : runtime                   8.57853
2018-12-25 12:28:03,513 INFO : 
2018-12-25 12:28:08,500 INFO : Time only for tr

...

2018-12-25 13:01:23,920 INFO : test_loss                 1.55596
2018-12-25 13:01:23,921 INFO : train_misclass            0.01780
2018-12-25 13:01:23,921 INFO : valid_misclass            0.06616
2018-12-25 13:01:23,922 INFO : test_misclass             0.53646
2018-12-25 13:01:23,922 INFO : runtime                   10.50025
2018-12-25 13:01:23,923 INFO : 
2018-12-25 13:01:30,200 INFO : Time only for training updates: 6.28s
2018-12-25 13:01:34,422 INFO : Epoch 199
2018-12-25 13:01:34,423 INFO : train_loss                0.11415
2018-12-25 13:01:34,424 INFO : valid_loss                0.18262
2018-12-25 13:01:34,424 INFO : test_loss                 1.73399
2018-12-25 13:01:34,425 INFO : train_misclass            0.01194
2018-12-25 13:01:34,425 INFO : valid_misclass            0.04555
2018-12-25 13:01:34,426 INFO : test_misclass             0.57118
2018-12-25 13:01:34,426 INFO : runtime                   10.50011
2018-12-25 13:01:34,427 INFO : 
2018-12-25 13:01:34,432 INFO : New best vali

2018-12-25 13:03:40,432 INFO : train_loss                0.09338
2018-12-25 13:03:40,432 INFO : valid_loss                0.11329
2018-12-25 13:03:40,433 INFO : test_loss                 1.49714
2018-12-25 13:03:40,434 INFO : train_misclass            0.00456
2018-12-25 13:03:40,434 INFO : valid_misclass            0.01627
2018-12-25 13:03:40,435 INFO : test_misclass             0.55556
2018-12-25 13:03:40,435 INFO : runtime                   10.50296
2018-12-25 13:03:40,436 INFO : 
2018-12-25 13:03:40,440 INFO : New best valid_misclass: 0.016269
2018-12-25 13:03:40,440 INFO : 
2018-12-25 13:03:46,713 INFO : Time only for training updates: 6.27s
2018-12-25 13:03:50,936 INFO : Epoch 212
2018-12-25 13:03:50,937 INFO : train_loss                0.09791
2018-12-25 13:03:50,937 INFO : valid_loss                0.13558
2018-12-25 13:03:50,938 INFO : test_loss                 1.58591
2018-12-25 13:03:50,939 INFO : train_misclass            0.00803
2018-12-25 13:03:50,939 INFO : valid_misclass

2018-12-25 13:05:47,070 INFO : 
2018-12-25 13:05:53,573 INFO : Time only for training updates: 6.50s
2018-12-25 13:05:57,943 INFO : Epoch 224
2018-12-25 13:05:57,943 INFO : train_loss                0.07903
2018-12-25 13:05:57,944 INFO : valid_loss                0.07600
2018-12-25 13:05:57,944 INFO : test_loss                 1.52567
2018-12-25 13:05:57,944 INFO : train_misclass            0.00304
2018-12-25 13:05:57,945 INFO : valid_misclass            0.00217
2018-12-25 13:05:57,945 INFO : test_misclass             0.53646
2018-12-25 13:05:57,946 INFO : runtime                   10.75698
2018-12-25 13:05:57,947 INFO : 
2018-12-25 13:05:57,951 INFO : New best valid_misclass: 0.002169
2018-12-25 13:05:57,952 INFO : 
2018-12-25 13:06:04,305 INFO : Time only for training updates: 6.35s
2018-12-25 13:06:08,527 INFO : Epoch 225
2018-12-25 13:06:08,528 INFO : train_loss                0.09090
2018-12-25 13:06:08,529 INFO : valid_loss                0.08302
2018-12-25 13:06:08,529 INFO : te

2018-12-25 13:08:17,533 INFO : test_loss                 1.43212
2018-12-25 13:08:17,534 INFO : train_misclass            0.00738
2018-12-25 13:08:17,534 INFO : valid_misclass            0.00217
2018-12-25 13:08:17,534 INFO : test_misclass             0.53472
2018-12-25 13:08:17,535 INFO : runtime                   10.95585
2018-12-25 13:08:17,535 INFO : 
2018-12-25 13:08:17,541 INFO : New best valid_misclass: 0.002169
2018-12-25 13:08:17,541 INFO : 
2018-12-25 13:08:24,103 INFO : Time only for training updates: 6.56s
2018-12-25 13:08:28,484 INFO : Epoch 238
2018-12-25 13:08:28,485 INFO : train_loss                0.06650
2018-12-25 13:08:28,486 INFO : valid_loss                0.05614
2018-12-25 13:08:28,486 INFO : test_loss                 1.49032
2018-12-25 13:08:28,487 INFO : train_misclass            0.00109
2018-12-25 13:08:28,487 INFO : valid_misclass            0.00108
2018-12-25 13:08:28,488 INFO : test_misclass             0.53646
2018-12-25 13:08:28,488 INFO : runtime       

2018-12-25 13:10:36,891 INFO : valid_misclass            0.00217
2018-12-25 13:10:36,891 INFO : test_misclass             0.56076
2018-12-25 13:10:36,891 INFO : runtime                   10.70955
2018-12-25 13:10:36,892 INFO : 
2018-12-25 13:10:43,384 INFO : Time only for training updates: 6.49s
2018-12-25 13:10:47,786 INFO : Epoch 251
2018-12-25 13:10:47,787 INFO : train_loss                0.06490
2018-12-25 13:10:47,787 INFO : valid_loss                0.06515
2018-12-25 13:10:47,788 INFO : test_loss                 1.52862
2018-12-25 13:10:47,789 INFO : train_misclass            0.00195
2018-12-25 13:10:47,789 INFO : valid_misclass            0.00325
2018-12-25 13:10:47,789 INFO : test_misclass             0.56076
2018-12-25 13:10:47,790 INFO : runtime                   10.79720
2018-12-25 13:10:47,790 INFO : 
2018-12-25 13:10:54,155 INFO : Time only for training updates: 6.36s
2018-12-25 13:10:58,469 INFO : Epoch 252
2018-12-25 13:10:58,469 INFO : train_loss                0.06442

###  valid_misclass: 0.000000 test_misclass: 0.69097

In [16]:
leave_one_out_deep_run(5)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
2018-12-25 13:11:08,590 INFO : Trial per class:
Counter({'Tongue': 72, 'Foot': 72, 'Right Hand': 72, 'Left Hand': 72})
2018-12-25 13:11:08,890 INFO : Trial per class:
Counter({'Left Hand': 72, 'Right Hand': 72, 'Foot': 72, 'Tongue': 72})
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  27

2018-12-25 13:12:31,340 INFO : Run until first stop...
2018-12-25 13:12:34,849 INFO : Epoch 0
2018-12-25 13:12:34,850 INFO : train_loss                1.40322
2018-12-25 13:12:34,851 INFO : valid_loss                1.40089
2018-12-25 13:12:34,851 INFO : test_loss                 1.40283
2018-12-25 13:12:34,852 INFO : train_misclass            0.74634
2018-12-25 13:12:34,852 INFO : valid_misclass            0.75054
2018-12-25 13:12:34,853 INFO : test_misclass             0.76389
2018-12-25 13:12:34,853 INFO : runtime                   0.00000
2018-12-25 13:12:34,853 INFO : 
2018-12-25 13:12:34,856 INFO : New best valid_misclass: 0.750542
2018-12-25 13:12:34,857 INFO : 
2018-12-25 13:12:39,816 INFO : Time only for training updates: 4.96s
2018-12-25 13:12:43,393 INFO : Epoch 1
2018-12-25 13:12:43,394 INFO : train_loss                1.91467
2018-12-25 13:12:43,394 INFO : valid_loss                1.70227
2018-12-25 13:12:43,395 INFO : test_loss                 2.13946
2018-12-25 13:12:43

2018-12-25 13:14:17,772 INFO : train_misclass            0.50705
2018-12-25 13:14:17,773 INFO : valid_misclass            0.52820
2018-12-25 13:14:17,774 INFO : test_misclass             0.73438
2018-12-25 13:14:17,774 INFO : runtime                   8.57457
2018-12-25 13:14:17,775 INFO : 
2018-12-25 13:14:22,759 INFO : Time only for training updates: 4.98s
2018-12-25 13:14:26,346 INFO : Epoch 13
2018-12-25 13:14:26,346 INFO : train_loss                1.06594
2018-12-25 13:14:26,347 INFO : valid_loss                1.07913
2018-12-25 13:14:26,347 INFO : test_loss                 1.76259
2018-12-25 13:14:26,348 INFO : train_misclass            0.47667
2018-12-25 13:14:26,348 INFO : valid_misclass            0.45987
2018-12-25 13:14:26,349 INFO : test_misclass             0.74132
2018-12-25 13:14:26,349 INFO : runtime                   8.57424
2018-12-25 13:14:26,350 INFO : 
2018-12-25 13:14:26,356 INFO : New best valid_misclass: 0.459870
2018-12-25 13:14:26,357 INFO : 
2018-12-25 13:1

2018-12-25 13:16:09,255 INFO : 
2018-12-25 13:16:14,243 INFO : Time only for training updates: 4.99s
2018-12-25 13:16:17,828 INFO : Epoch 26
2018-12-25 13:16:17,829 INFO : train_loss                0.86564
2018-12-25 13:16:17,829 INFO : valid_loss                1.08474
2018-12-25 13:16:17,830 INFO : test_loss                 1.71844
2018-12-25 13:16:17,830 INFO : train_misclass            0.38307
2018-12-25 13:16:17,831 INFO : valid_misclass            0.44577
2018-12-25 13:16:17,831 INFO : test_misclass             0.70486
2018-12-25 13:16:17,832 INFO : runtime                   8.57810
2018-12-25 13:16:17,832 INFO : 
2018-12-25 13:16:22,814 INFO : Time only for training updates: 4.98s
2018-12-25 13:16:26,399 INFO : Epoch 27
2018-12-25 13:16:26,399 INFO : train_loss                0.81955
2018-12-25 13:16:26,400 INFO : valid_loss                1.00404
2018-12-25 13:16:26,401 INFO : test_loss                 1.72162
2018-12-25 13:16:26,401 INFO : train_misclass            0.33478
201

2018-12-25 13:18:09,303 INFO : test_loss                 1.94854
2018-12-25 13:18:09,303 INFO : train_misclass            0.24417
2018-12-25 13:18:09,304 INFO : valid_misclass            0.38829
2018-12-25 13:18:09,304 INFO : test_misclass             0.69444
2018-12-25 13:18:09,305 INFO : runtime                   8.57421
2018-12-25 13:18:09,305 INFO : 
2018-12-25 13:18:14,288 INFO : Time only for training updates: 4.98s
2018-12-25 13:18:17,871 INFO : Epoch 40
2018-12-25 13:18:17,872 INFO : train_loss                0.65114
2018-12-25 13:18:17,872 INFO : valid_loss                0.98225
2018-12-25 13:18:17,873 INFO : test_loss                 2.00668
2018-12-25 13:18:17,873 INFO : train_misclass            0.26099
2018-12-25 13:18:17,874 INFO : valid_misclass            0.39262
2018-12-25 13:18:17,874 INFO : test_misclass             0.68750
2018-12-25 13:18:17,875 INFO : runtime                   8.56908
2018-12-25 13:18:17,875 INFO : 
2018-12-25 13:18:22,856 INFO : Time only for tr

...

2018-12-25 14:13:35,855 INFO : Epoch 260
2018-12-25 14:13:35,856 INFO : train_loss                0.08930
2018-12-25 14:13:35,856 INFO : valid_loss                0.10297
2018-12-25 14:13:35,857 INFO : test_loss                 2.00917
2018-12-25 14:13:35,857 INFO : train_misclass            0.00651
2018-12-25 14:13:35,858 INFO : valid_misclass            0.01193
2018-12-25 14:13:35,858 INFO : test_misclass             0.66319
2018-12-25 14:13:35,859 INFO : runtime                   10.53073
2018-12-25 14:13:35,859 INFO : 
2018-12-25 14:13:35,866 INFO : New best valid_misclass: 0.011931
2018-12-25 14:13:35,866 INFO : 
2018-12-25 14:13:42,157 INFO : Time only for training updates: 6.29s
2018-12-25 14:13:46,388 INFO : Epoch 261
2018-12-25 14:13:46,389 INFO : train_loss                0.07111
2018-12-25 14:13:46,390 INFO : valid_loss                0.08720
2018-12-25 14:13:46,390 INFO : test_loss                 2.61207
2018-12-25 14:13:46,391 INFO : train_misclass            0.00543
2018

2018-12-25 14:15:42,332 INFO : 
2018-12-25 14:15:48,673 INFO : Time only for training updates: 6.34s
2018-12-25 14:15:52,944 INFO : Epoch 273
2018-12-25 14:15:52,944 INFO : train_loss                0.06266
2018-12-25 14:15:52,945 INFO : valid_loss                0.06572
2018-12-25 14:15:52,945 INFO : test_loss                 2.68083
2018-12-25 14:15:52,946 INFO : train_misclass            0.00412
2018-12-25 14:15:52,947 INFO : valid_misclass            0.00108
2018-12-25 14:15:52,948 INFO : test_misclass             0.70833
2018-12-25 14:15:52,948 INFO : runtime                   10.61350
2018-12-25 14:15:52,949 INFO : 
2018-12-25 14:15:59,304 INFO : Time only for training updates: 6.35s
2018-12-25 14:16:03,584 INFO : Epoch 274
2018-12-25 14:16:03,585 INFO : train_loss                0.06774
2018-12-25 14:16:03,586 INFO : valid_loss                0.07924
2018-12-25 14:16:03,586 INFO : test_loss                 2.52062
2018-12-25 14:16:03,587 INFO : train_misclass            0.00391


2018-12-25 14:18:11,764 INFO : train_loss                0.07058
2018-12-25 14:18:11,764 INFO : valid_loss                0.05260
2018-12-25 14:18:11,765 INFO : test_loss                 3.04139
2018-12-25 14:18:11,765 INFO : train_misclass            0.00347
2018-12-25 14:18:11,765 INFO : valid_misclass            0.00000
2018-12-25 14:18:11,766 INFO : test_misclass             0.72049
2018-12-25 14:18:11,766 INFO : runtime                   10.66582
2018-12-25 14:18:11,766 INFO : 
2018-12-25 14:18:11,772 INFO : New best valid_misclass: 0.000000
2018-12-25 14:18:11,773 INFO : 
2018-12-25 14:18:18,200 INFO : Time only for training updates: 6.43s
2018-12-25 14:18:22,474 INFO : Epoch 287
2018-12-25 14:18:22,474 INFO : train_loss                0.06095
2018-12-25 14:18:22,475 INFO : valid_loss                0.06150
2018-12-25 14:18:22,475 INFO : test_loss                 2.23095
2018-12-25 14:18:22,476 INFO : train_misclass            0.00326
2018-12-25 14:18:22,476 INFO : valid_misclass

2018-12-25 14:20:30,412 INFO : valid_loss                0.05129
2018-12-25 14:20:30,413 INFO : test_loss                 2.72112
2018-12-25 14:20:30,413 INFO : train_misclass            0.00152
2018-12-25 14:20:30,414 INFO : valid_misclass            0.00108
2018-12-25 14:20:30,414 INFO : test_misclass             0.69965
2018-12-25 14:20:30,415 INFO : runtime                   10.78571
2018-12-25 14:20:30,416 INFO : 
2018-12-25 14:20:36,815 INFO : Time only for training updates: 6.40s
2018-12-25 14:20:41,155 INFO : Epoch 300
2018-12-25 14:20:41,156 INFO : train_loss                0.06221
2018-12-25 14:20:41,156 INFO : valid_loss                0.05131
2018-12-25 14:20:41,157 INFO : test_loss                 2.17612
2018-12-25 14:20:41,157 INFO : train_misclass            0.00195
2018-12-25 14:20:41,157 INFO : valid_misclass            0.00108
2018-12-25 14:20:41,158 INFO : test_misclass             0.67014
2018-12-25 14:20:41,158 INFO : runtime                   10.71962
2018-12-25 

2018-12-25 14:22:49,289 INFO : Epoch 312
2018-12-25 14:22:49,289 INFO : train_loss                0.05092
2018-12-25 14:22:49,290 INFO : valid_loss                0.04687
2018-12-25 14:22:49,290 INFO : test_loss                 2.43887
2018-12-25 14:22:49,291 INFO : train_misclass            0.00065
2018-12-25 14:22:49,291 INFO : valid_misclass            0.00000
2018-12-25 14:22:49,292 INFO : test_misclass             0.66840
2018-12-25 14:22:49,292 INFO : runtime                   10.70359
2018-12-25 14:22:49,293 INFO : 
2018-12-25 14:22:49,298 INFO : New best valid_misclass: 0.000000
2018-12-25 14:22:49,298 INFO : 
2018-12-25 14:22:55,637 INFO : Time only for training updates: 6.34s
2018-12-25 14:22:59,971 INFO : Epoch 313
2018-12-25 14:22:59,971 INFO : train_loss                0.06629
2018-12-25 14:22:59,972 INFO : valid_loss                0.05095
2018-12-25 14:22:59,972 INFO : test_loss                 2.43737
2018-12-25 14:22:59,973 INFO : train_misclass            0.00391
2018

###  valid_misclass: 0.000000 test_misclass: 0.69097

In [ ]:
leave_one_out_deep_run(6)

Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 672527  =      0.000 ...  2690.108 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A01E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 686999  =      0.000 ...  2747.996 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02T.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 677168  =      0.000 ...  2708.672 secs...
Extracting EDF parameters from /Users/debaojian/OneDrive/OneDrive - UNSW/UNSW/Research/EEG/BCI_Competition/A02E.gdf...
GDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 662665 

2018-12-27 16:02:29,030 INFO : valid_misclass            0.74078
2018-12-27 16:02:29,030 INFO : test_misclass             0.75000
2018-12-27 16:02:29,031 INFO : runtime                   8.48283
2018-12-27 16:02:29,031 INFO : 
2018-12-27 16:02:29,036 INFO : New best valid_misclass: 0.740781
2018-12-27 16:02:29,036 INFO : 
2018-12-27 16:02:33,968 INFO : Time only for training updates: 4.93s
2018-12-27 16:02:37,514 INFO : Epoch 3
2018-12-27 16:02:37,515 INFO : train_loss                1.88285
2018-12-27 16:02:37,515 INFO : valid_loss                1.53902
2018-12-27 16:02:37,516 INFO : test_loss                 1.81397
2018-12-27 16:02:37,516 INFO : train_misclass            0.70998
2018-12-27 16:02:37,516 INFO : valid_misclass            0.69957
2018-12-27 16:02:37,517 INFO : test_misclass             0.71354
2018-12-27 16:02:37,517 INFO : runtime                   8.51901
2018-12-27 16:02:37,518 INFO : 
2018-12-27 16:02:37,524 INFO : New best valid_misclass: 0.699566
2018-12-27 16:02

2018-12-27 16:04:12,419 INFO : 
2018-12-27 16:04:17,429 INFO : Time only for training updates: 5.01s
2018-12-27 16:04:21,033 INFO : Epoch 15
2018-12-27 16:04:21,033 INFO : train_loss                1.18881
2018-12-27 16:04:21,034 INFO : valid_loss                1.16822
2018-12-27 16:04:21,034 INFO : test_loss                 1.41462
2018-12-27 16:04:21,035 INFO : train_misclass            0.53120
2018-12-27 16:04:21,036 INFO : valid_misclass            0.49675
2018-12-27 16:04:21,036 INFO : test_misclass             0.60590
2018-12-27 16:04:21,037 INFO : runtime                   8.63931
2018-12-27 16:04:21,037 INFO : 
2018-12-27 16:04:26,042 INFO : Time only for training updates: 5.00s
2018-12-27 16:04:29,637 INFO : Epoch 16
2018-12-27 16:04:29,638 INFO : train_loss                1.06264
2018-12-27 16:04:29,638 INFO : valid_loss                0.99713
2018-12-27 16:04:29,639 INFO : test_loss                 1.34798
2018-12-27 16:04:29,639 INFO : train_misclass            0.49213
201

2018-12-27 16:06:13,173 INFO : valid_misclass            0.44685
2018-12-27 16:06:13,174 INFO : test_misclass             0.61285
2018-12-27 16:06:13,174 INFO : runtime                   8.61290
2018-12-27 16:06:13,174 INFO : 
2018-12-27 16:06:18,193 INFO : Time only for training updates: 5.02s
2018-12-27 16:06:21,820 INFO : Epoch 29
2018-12-27 16:06:21,820 INFO : train_loss                0.99596
2018-12-27 16:06:21,822 INFO : valid_loss                1.23357
2018-12-27 16:06:21,822 INFO : test_loss                 1.49722
2018-12-27 16:06:21,823 INFO : train_misclass            0.43082
2018-12-27 16:06:21,823 INFO : valid_misclass            0.46529
2018-12-27 16:06:21,824 INFO : test_misclass             0.57986
2018-12-27 16:06:21,824 INFO : runtime                   8.63421
2018-12-27 16:06:21,825 INFO : 
2018-12-27 16:06:26,835 INFO : Time only for training updates: 5.01s
2018-12-27 16:06:30,435 INFO : Epoch 30
2018-12-27 16:06:30,436 INFO : train_loss                0.91398
201

2018-12-27 16:08:14,295 INFO : Epoch 42
2018-12-27 16:08:14,296 INFO : train_loss                0.68826
2018-12-27 16:08:14,296 INFO : valid_loss                1.04646
2018-12-27 16:08:14,298 INFO : test_loss                 1.69890
2018-12-27 16:08:14,298 INFO : train_misclass            0.29029
2018-12-27 16:08:14,298 INFO : valid_misclass            0.40347
2018-12-27 16:08:14,299 INFO : test_misclass             0.61285
2018-12-27 16:08:14,299 INFO : runtime                   8.55211
2018-12-27 16:08:14,300 INFO : 
2018-12-27 16:08:19,261 INFO : Time only for training updates: 4.96s
2018-12-27 16:08:22,839 INFO : Epoch 43
2018-12-27 16:08:22,839 INFO : train_loss                0.70627
2018-12-27 16:08:22,840 INFO : valid_loss                1.07918
2018-12-27 16:08:22,840 INFO : test_loss                 1.69983
2018-12-27 16:08:22,840 INFO : train_misclass            0.28866
2018-12-27 16:08:22,841 INFO : valid_misclass            0.40998
2018-12-27 16:08:22,842 INFO : test_mis

...

2018-12-27 16:27:33,306 INFO : 
2018-12-27 16:27:38,252 INFO : Time only for training updates: 4.95s
2018-12-27 16:27:41,805 INFO : Epoch 178
2018-12-27 16:27:41,805 INFO : train_loss                0.07854
2018-12-27 16:27:41,806 INFO : valid_loss                1.04717
2018-12-27 16:27:41,807 INFO : test_loss                 2.16570
2018-12-27 16:27:41,807 INFO : train_misclass            0.00624
2018-12-27 16:27:41,807 INFO : valid_misclass            0.36551
2018-12-27 16:27:41,809 INFO : test_misclass             0.62847
2018-12-27 16:27:41,809 INFO : runtime                   8.50282
2018-12-27 16:27:41,810 INFO : 
2018-12-27 16:27:46,757 INFO : Time only for training updates: 4.95s
2018-12-27 16:27:50,308 INFO : Epoch 179
2018-12-27 16:27:50,309 INFO : train_loss                0.06529
2018-12-27 16:27:50,309 INFO : valid_loss                1.10167
2018-12-27 16:27:50,310 INFO : test_loss                 2.34704
2018-12-27 16:27:50,311 INFO : train_misclass            0.00054
2

2018-12-27 16:29:32,385 INFO : test_misclass             0.62500
2018-12-27 16:29:32,386 INFO : runtime                   8.50151
2018-12-27 16:29:32,386 INFO : 
2018-12-27 16:29:37,333 INFO : Time only for training updates: 4.95s
2018-12-27 16:29:40,887 INFO : Epoch 192
2018-12-27 16:29:40,887 INFO : train_loss                0.07333
2018-12-27 16:29:40,887 INFO : valid_loss                1.01602
2018-12-27 16:29:40,888 INFO : test_loss                 2.09956
2018-12-27 16:29:40,888 INFO : train_misclass            0.00163
2018-12-27 16:29:40,889 INFO : valid_misclass            0.35141
2018-12-27 16:29:40,890 INFO : test_misclass             0.61285
2018-12-27 16:29:40,890 INFO : runtime                   8.50513
2018-12-27 16:29:40,891 INFO : 
2018-12-27 16:29:45,838 INFO : Time only for training updates: 4.95s
2018-12-27 16:29:49,390 INFO : Epoch 193
2018-12-27 16:29:49,391 INFO : train_loss                0.05855
2018-12-27 16:29:49,391 INFO : valid_loss                0.98767
2

2018-12-27 16:31:31,443 INFO : valid_loss                1.09347
2018-12-27 16:31:31,443 INFO : test_loss                 2.14394
2018-12-27 16:31:31,444 INFO : train_misclass            0.00109
2018-12-27 16:31:31,445 INFO : valid_misclass            0.36985
2018-12-27 16:31:31,445 INFO : test_misclass             0.63021
2018-12-27 16:31:31,446 INFO : runtime                   8.50099
2018-12-27 16:31:31,446 INFO : 
2018-12-27 16:31:36,393 INFO : Time only for training updates: 4.95s
2018-12-27 16:31:39,948 INFO : Epoch 206
2018-12-27 16:31:39,948 INFO : train_loss                0.07196
2018-12-27 16:31:39,949 INFO : valid_loss                1.17255
2018-12-27 16:31:39,949 INFO : test_loss                 2.17801
2018-12-27 16:31:39,949 INFO : train_misclass            0.00326
2018-12-27 16:31:39,950 INFO : valid_misclass            0.37636
2018-12-27 16:31:39,950 INFO : test_misclass             0.60243
2018-12-27 16:31:39,951 INFO : runtime                   8.50688
2018-12-27 16

2018-12-27 16:33:30,510 INFO : Epoch 219
2018-12-27 16:33:30,511 INFO : train_loss                0.07142
2018-12-27 16:33:30,511 INFO : valid_loss                1.08139
2018-12-27 16:33:30,512 INFO : test_loss                 2.00757
2018-12-27 16:33:30,512 INFO : train_misclass            0.00787
2018-12-27 16:33:30,513 INFO : valid_misclass            0.35792
2018-12-27 16:33:30,513 INFO : test_misclass             0.58854
2018-12-27 16:33:30,514 INFO : runtime                   8.50514
2018-12-27 16:33:30,514 INFO : 
2018-12-27 16:33:35,461 INFO : Time only for training updates: 4.95s
2018-12-27 16:33:39,013 INFO : Epoch 220
2018-12-27 16:33:39,014 INFO : train_loss                0.04293
2018-12-27 16:33:39,014 INFO : valid_loss                1.07917
2018-12-27 16:33:39,014 INFO : test_loss                 2.26983
2018-12-27 16:33:39,015 INFO : train_misclass            0.00027
2018-12-27 16:33:39,015 INFO : valid_misclass            0.35249
2018-12-27 16:33:39,016 INFO : test_m

2018-12-27 16:35:21,096 INFO : 
2018-12-27 16:35:26,041 INFO : Time only for training updates: 4.94s
2018-12-27 16:35:29,592 INFO : Epoch 233
2018-12-27 16:35:29,593 INFO : train_loss                0.04602
2018-12-27 16:35:29,593 INFO : valid_loss                1.00959
2018-12-27 16:35:29,594 INFO : test_loss                 2.16087
2018-12-27 16:35:29,595 INFO : train_misclass            0.00081
2018-12-27 16:35:29,595 INFO : valid_misclass            0.33839
2018-12-27 16:35:29,596 INFO : test_misclass             0.62326
2018-12-27 16:35:29,596 INFO : runtime                   8.50760
2018-12-27 16:35:29,597 INFO : 
2018-12-27 16:35:34,544 INFO : Time only for training updates: 4.95s
2018-12-27 16:35:38,092 INFO : Epoch 234
2018-12-27 16:35:38,092 INFO : train_loss                0.04643
2018-12-27 16:35:38,093 INFO : valid_loss                1.16579
2018-12-27 16:35:38,094 INFO : test_loss                 2.12376
2018-12-27 16:35:38,094 INFO : train_misclass            0.00027
2

| test subject id | shallow |   deep  | crop shallow | crop deep |
|-----------------|:-------:|:-------:|--------------|-----------|
|        1        | 0.29688 | 0.29688 | 0.35764      | 0.24479   |
|        2        | 0.65451 | 0.65451 | 0.76215      | 0.74653   |
|        3        | 0.24826 | 0.39062 | 0.55729      | 0.38368   |
|        4        | 0.50347 | 0.54340 | 0.61806      | 0.67708   |
|        5        | 0.72222 | 0.69097 | 0.74826      | 0.69792   |
|        6        | 0.61806 |   <i></i>        | 0.71875      |  <i></i>           |
|        7        | 0.56944 |   <i></i>        | 0.72222      |   <i></i>          |
|        8        | 0.27604 |   <i></i>       | 0.55556      |   <i></i>          |
|        9        | 0.33854 |   <i></i>        | 0.51042      |   <i></i>          |